In [1]:
import pandas as pd
import numpy as np
from scipy.integrate import trapz
from scipy.signal import find_peaks
from lets_plot import *
import pingouin as pg

LetsPlot.setup_html()

## Gesamter Datensatz Isokinet

In [42]:
iso = pd.read_csv(r"C:\Users\bvenn\OneDrive\Desktop\Publikation\Zusammenfassung Arbeitssätze\isokinet csv\isokinet_dataframe.csv")

# daten formatieren
iso['id'] = iso['id'].astype('int64')
iso['measurement'] = iso['measurement'].astype('category')
iso['experiment'] = iso['experiment'].astype('category')
iso['group'] = iso['group'].astype('category')

# Daten zur Berechnung in ihre Einheiten Tranformieren
iso['pos_1/10_deg/s_or_mm'] = iso['pos_1/10_deg/s_or_mm'] / 10
iso['torque_1/10nm_or_force_n'] = iso['torque_1/10nm_or_force_n'] / (-10)
iso['speed_1/10_deg/sec_or_1/10_mm/s'] = iso['speed_1/10_deg/sec_or_1/10_mm/s'] / 10

# torque werte *(-1), um positive zahl zu erhalten

iso.rename(columns={'pos_1/10_deg/s_or_mm': 'pos_deg_or_mm', 'torque_1/10nm_or_force_n': 'torque_nm',
                   'speed_1/10_deg/sec_or_1/10_mm/s': 'speed_deg/s_or_mm/s'}, inplace=True)
iso.head()

id measurement  time_ms  pos_deg_or_mm  torque_nm  speed_deg/s_or_mm/s  \
0  15073      warmup        5           12.0       -3.0                  0.0   
1  15073      warmup       10           12.0       -3.0                  0.5   
2  15073      warmup       15           12.0       -2.3                  4.0   
3  15073      warmup       20           12.1       -0.0                 18.3   
4  15073      warmup       25           12.1       11.3                 23.5   

   torque_without_comp  rep  set  torque_dyn  force_right  force_left  \
0                  293    1    1          30            0           0   
1                  293    1    1          30            0           0   
2                  293    1    1          23            0           0   
3                  293    1    1           0            0           0   
4                  293    1    1        -113            0           0   

  experiment     group  
0    pretest  beta_ala  
1    pretest  beta_ala  
2    pretest  beta_ala  
3    pretest  beta_ala  
4    pretest  beta_ala

## Automatisierung Peakt Torque Berechnung

In [150]:
# Dataframe mit Ergebnissen erstellen
pt_results = pd.DataFrame(columns = ['id', 'group', 'peak_torque_pre', 'abbruchkriterium_pre', 'peak_torque_post',
                                     'abbruchkriterium_post'])

probanden_ids = iso['id'].unique()

for proband_id in probanden_ids:
    proband_data = iso[iso['id'] == proband_id]
    
    # Gruppeninfo abgreifen
    group = proband_data['group'].iloc[0]
    
    # Filtern des Probandenframes nach pre und posttest
    proband_data_pre = proband_data[proband_data['experiment'] == 'pretest']
    proband_data_post = proband_data[proband_data['experiment'] == 'posttest']
    
    # pre und posttest frames filtern nach peak torque Messung und konzentrischen reps(jeder zweite)
    kon_pre = proband_data_pre.query('measurement == "pt" and rep % 2 == 0')
    kon_post = proband_data_post.query('measurement == "pt" and rep % 2 == 0')
    
    # pt und Abbruch berechnen
    # pretest
    
    peak_torque_pre = kon_pre['torque_nm'].max()
    abort_pre = peak_torque_pre / 2
    
    # posttest
    
    peak_torque_post = kon_post['torque_nm'].max()

    # Abbruchkriterium berechnen: 50% peak torque
    abort_post = peak_torque_post / 2
    
    ergebnis_row = pd.DataFrame({
        'id': [proband_id],
        'group': [group],
        'peak_torque_pre': [peak_torque_pre],
        'abbruchkriterium_pre': [abort_pre],
        'peak_torque_post': [peak_torque_post],
        'abbruchkriterium_post': [abort_post]
        
    })
    
    # Ergebnisse in dataframe einfügen
    pt_results = pd.concat([pt_results, ergebnis_row], ignore_index = True)
    
pt_results

C:\Users\bvenn\AppData\Local\Temp\ipykernel_7280\3911513928.py:45: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  pt_results = pd.concat([pt_results, ergebnis_row], ignore_index = True)


id     group  peak_torque_pre  abbruchkriterium_pre  peak_torque_post  \
0   15073  beta_ala            249.5                124.75             269.0   
1   20438  beta_ala            306.8                153.40             291.0   
2   25778  beta_ala            163.2                 81.60             155.7   
3   26107  beta_ala            201.5                100.75             194.0   
4   27351  beta_ala            162.8                 81.40             166.5   
5   28514   placebo            121.2                 60.60             139.2   
6   93672  beta_ala            294.5                147.25             338.3   
7   33468   placebo            156.5                 78.25             171.0   
8   39337   placebo            296.7                148.35             261.5   
9   39750   placebo            139.2                 69.60             131.3   
10  44858  beta_ala            143.3                 71.65             152.3   
11  49444   placebo            136.5                 68.25             146.0   
12  49830  beta_ala            174.8                 87.40             194.0   
13  50843   placebo            272.0                136.00             266.0   
14  54145  beta_ala            213.5                106.75             192.8   
15  54658   placebo            184.5                 92.25             175.5   
16  58046  beta_ala            307.2                153.60             305.0   
17  59289  beta_ala            341.3                170.65             343.5   
18  61104   placebo            274.5                137.25             286.5   
19  71620   placebo            230.7                115.35             271.5   
20  73162  beta_ala            252.8                126.40             240.0   
21  76847   placebo            225.0                112.50             234.0   
22  82556   placebo            179.7                 89.85             194.0   
23  93302   placebo            178.2                 89.10             182.7   

    abbruchkriterium_post  
0                  134.50  
1                  145.50  
2                   77.85  
3                   97.00  
4                   83.25  
5                   69.60  
6                  169.15  
7                   85.50  
8                  130.75  
9                   65.65  
10                  76.15  
11                  73.00  
12                  97.00  
13                 133.00  
14                  96.40  
15                  87.75  
16                 152.50  
17                 171.75  
18                 143.25  
19                 135.75  
20                 120.00  
21                 117.00  
22                  97.00  
23                  91.35

In [151]:
pt_results_l = pd.melt(pt_results.drop(columns=['abbruchkriterium_pre', 'abbruchkriterium_post']), id_vars = ['id', 'group'], value_name='torque', var_name = 'measurement')
pt_results_l.head()

id     group      measurement  torque
0  15073  beta_ala  peak_torque_pre   249.5
1  20438  beta_ala  peak_torque_pre   306.8
2  25778  beta_ala  peak_torque_pre   163.2
3  26107  beta_ala  peak_torque_pre   201.5
4  27351  beta_ala  peak_torque_pre   162.8

In [152]:
# Visualisierung Gruppenunterschied Peak Torque

(
    ggplot(pt_results_l, aes(x='measurement', y='torque'))
    + geom_boxplot(aes(group='group', color='group'))
    + labs(title='Peak Torque im Pre- und Post Test - Aufgeteilt nach Gruppen.')
    + ylab('Peak Torque [Nm]')
)

In [153]:
pt_stat = pg.mixed_anova(dv='torque',between='group', within='measurement', subject='id', data=pt_results_l, correction='auto', effsize='np2')
pt_stat

Source            SS  DF1  DF2            MS         F     p-unc  \
0        group  13313.340833    1   22  13313.340833  1.684440  0.207779   
1  measurement    189.607500    1   22    189.607500  1.118742  0.301666   
2  Interaction     23.520000    1   22     23.520000  0.138775  0.713066   

        np2  eps  
0  0.071120  NaN  
1  0.048391  1.0  
2  0.006268  NaN

### Wie viele Sätze hat jeder Proband durchgeführt?

In [154]:
##### Gruppieren Sie den DataFrame nach 'id', 'experiment' und 'group' und zählen Sie die eindeutigen Werte in 'measurement'
all_sets = iso.groupby(['id', 'experiment', 'group'])['measurement'].nunique()

warmup = 1
pt = 1
fatigue_sets = all_sets - warmup - pt

fatigue_sets_df = pd.DataFrame({'fatigue_sets': fatigue_sets})

# Mithilfe von reset_index() werden die gruppierten Spalten zu normalen Spalten
fatigue_sets_df = fatigue_sets_df.reset_index()

# Nun sind 'experiment' und 'group' Variablen in Ihrem DataFrame
fatigue_sets_df


C:\Users\bvenn\AppData\Local\Temp\ipykernel_7280\190093233.py:2: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  all_sets = iso.groupby(['id', 'experiment', 'group'])['measurement'].nunique()


id experiment     group  fatigue_sets
0   15073   posttest  beta_ala             6
1   15073   posttest   placebo            -2
2   15073    pretest  beta_ala             5
3   15073    pretest   placebo            -2
4   20438   posttest  beta_ala             7
..    ...        ...       ...           ...
91  93302    pretest   placebo             2
92  93672   posttest  beta_ala             2
93  93672   posttest   placebo            -2
94  93672    pretest  beta_ala             2
95  93672    pretest   placebo            -2

[96 rows x 4 columns]

In [155]:
# Visualisierung Anzahl Ermüdungssätze S1-Sn

(
    ggplot(fatigue_sets_df, aes(x='experiment', y='fatigue_sets'))
    + geom_boxplot(aes(group='group', color='group'))
    + labs(title='Absolvierte Sätze aufgeteilt nach Gruppen', subtitle='Achtung Zeitreihenfolge vertauscht')
    + ylab('Absolvierte Ermüdungssätze')
    + xlab('Zeitpunkt')
)

In [156]:
sets_stat = pg.mixed_anova(dv='fatigue_sets',between='group', within='experiment', subject='id', data=fatigue_sets_df, correction='auto', effsize='np2')
sets_stat

ValueError: Subject IDs cannot overlap between groups: each group in `group` must have a unique set of subject IDs, e.g. group1 = [1, 2, 3, ..., 10] and group2 = [11, 12, 13, ..., 20]

### Nach wie vielen Wiederholungen wurde das Abbruchkriterium erreicht?

In [157]:
# frames für pre-und post test erstellen
pretest = iso[iso['experiment'] == 'pretest'][['id', 'rep', 'torque_nm', 'measurement']]
posttest = iso[iso['experiment'] == 'posttest'][['id', 'rep', 'torque_nm', 'measurement']]

In [158]:
# Einzelne Probandenframes Pretest
# Absolvierte Sätze wurden optisch geprüft

pretest[['id', 'rep', 'torque_nm']]
p15073 = pretest.query('id == 15073 and rep % 2 == 0 and measurement == "s5"').copy()
p20438 = pretest.query('id == 20438 and rep % 2 == 0 and measurement == "s2"').copy()
p25778 = pretest.query('id == 25778 and rep % 2 == 0 and measurement == "s4"').copy()
p26107 = pretest.query('id == 26107 and rep % 2 == 0 and measurement == "s8"').copy()
p27351 = pretest.query('id == 27351 and rep % 2 == 0 and measurement == "s2"').copy()
p28514 = pretest.query('id == 28514 and rep % 2 == 0 and measurement == "s7"').copy()
p93672 = pretest.query('id == 93672 and rep % 2 == 0 and measurement == "s2"').copy()
p33468 = pretest.query('id == 33468 and rep % 2 == 0 and measurement == "s2"').copy()
p39337 = pretest.query('id == 39337 and rep % 2 == 0 and measurement == "s3"').copy()
p39750 = pretest.query('id == 39750 and rep % 2 == 0 and measurement == "s2"').copy()
p44858 = pretest.query('id == 44858 and rep % 2 == 0 and measurement == "s3"').copy()
p49444 = pretest.query('id == 49444 and rep % 2 == 0 and measurement == "s3"').copy()
p50843 = pretest.query('id == 50843 and rep % 2 == 0 and measurement == "s3"').copy()
p54145 = pretest.query('id == 54145 and rep % 2 == 0 and measurement == "s3"').copy()
p54658 = pretest.query('id == 54658 and rep % 2 == 0 and measurement == "s4"').copy()
p58046 = pretest.query('id == 58046 and rep % 2 == 0 and measurement == "s3"').copy()
p59289 = pretest.query('id == 59289 and rep % 2 == 0 and measurement == "s4"').copy()
p61104 = pretest.query('id == 61104 and rep % 2 == 0 and measurement == "s2"').copy()
p71620 = pretest.query('id == 71620 and rep % 2 == 0 and measurement == "s2"').copy()
p73162 = pretest.query('id == 73162 and rep % 2 == 0 and measurement == "s3"').copy()
p76847 = pretest.query('id == 76847 and rep % 2 == 0 and measurement == "s2"').copy()
p82556 = pretest.query('id == 82556 and rep % 2 == 0 and measurement == "s6"').copy()
p93302 = pretest.query('id == 93302 and rep % 2 == 0 and measurement == "s2"').copy()
p49830 = pretest.query('id == 49830 and rep % 2 == 0 and measurement == "s2"').copy()

In [159]:
# Einzelne Probandenframes Posttest
# Absolvierte Sätze wurden optisch geprüft

posttest[['id', 'rep', 'torque_nm']]
p15073 = posttest.query('id == 15073 and rep % 2 == 0 and measurement == "s6"').copy()
p20438 = posttest.query('id == 20438 and rep % 2 == 0 and measurement == "s7"').copy()
p25778 = posttest.query('id == 25778 and rep % 2 == 0 and measurement == "s2"').copy()
p26107 = posttest.query('id == 26107 and rep % 2 == 0 and measurement == "s6"').copy()
p27351 = posttest.query('id == 27351 and rep % 2 == 0 and measurement == "s1"').copy()
p28514 = posttest.query('id == 28514 and rep % 2 == 0 and measurement == "s7"').copy()
p93672 = posttest.query('id == 93672 and rep % 2 == 0 and measurement == "s2"').copy()
p33468 = posttest.query('id == 33468 and rep % 2 == 0 and measurement == "s2"').copy()
p39337 = posttest.query('id == 39337 and rep % 2 == 0 and measurement == "s4"').copy()
p39750 = posttest.query('id == 39750 and rep % 2 == 0 and measurement == "s4"').copy()
p44858 = posttest.query('id == 44858 and rep % 2 == 0 and measurement == "s4"').copy()
p49444 = posttest.query('id == 49444 and rep % 2 == 0 and measurement == "s4"').copy()
p50843 = posttest.query('id == 50843 and rep % 2 == 0 and measurement == "s3"').copy()
p54145 = posttest.query('id == 54145 and rep % 2 == 0 and measurement == "s3"').copy()
p54658 = posttest.query('id == 54658 and rep % 2 == 0 and measurement == "s4"').copy()
p58046 = posttest.query('id == 58046 and rep % 2 == 0 and measurement == "s2"').copy()
p59289 = posttest.query('id == 59289 and rep % 2 == 0 and measurement == "s3"').copy()
p61104 = posttest.query('id == 61104 and rep % 2 == 0 and measurement == "s2"').copy()
p71620 = posttest.query('id == 71620 and rep % 2 == 0 and measurement == "s1"').copy()
p73162 = posttest.query('id == 73162 and rep % 2 == 0 and measurement == "s6"').copy()
p76847 = posttest.query('id == 76847 and rep % 2 == 0 and measurement == "s2"').copy()
p82556 = posttest.query('id == 82556 and rep % 2 == 0 and measurement == "s3"').copy()
p93302 = posttest.query('id == 93302 and rep % 2 == 0 and measurement == "s1"').copy()
p49830 = posttest.query('id == 49830 and rep % 2 == 0 and measurement == "s4"').copy()

In [160]:
# Plot zum Sählen der absovierten Reps- id und Abbruchkriterium einsetzen

id_nr = p39337

id_nr.reset_index(drop=True, inplace=True)

# Erstellen Sie eine neue Spalte 'measurement_count', um die Reihenfolge der Messungen innerhalb des Experiments zu verfolgen
id_nr['measurement_count'] = range(1, len(id_nr) + 1)

# Aktualisieren Sie die 'time_ms'-Spalte basierend auf der 'measurement_count'
id_nr['time_ms'] = id_nr['measurement_count'] * 5 + 5

# Entfernen Sie die 'measurement_count'-Spalte, wenn sie nicht mehr benötigt wird
id_nr.drop('measurement_count', axis=1, inplace=True)



# Letzten Belastungssatz plotten
# Abbruchkriterium: Drei reps unter x Nm
(
    ggplot(id_nr, aes(x='time_ms', y='torque_nm'))
    + geom_line()
    + geom_hline(yintercept=148.35, linetype='dashed', color='red')
    + labs(title='Letztes Set Pre-test')
)

### Beispiel abbruch knapp verpasst p73162 post test, 82556

In [161]:
# Sets done = Anzahl der sets die durchlaufen wurden, inklusive des sets in dem das Abbruchkriterium erreicht wurde
# total_reps = Summe aller Wiederholungen des fatigue protokolls, die bis Erreichen des Abbruchkriteriums absolviert wurden

absolvierte_reps = pd.read_excel(r"C:\Users\bvenn\OneDrive\Desktop\Publikation\Zusammenfassung Arbeitssätze\Absolvierte_reps.xlsx")
absolvierte_reps

id     group  sets_done_pre  reps_done_last set_pre  total_reps_pre  \
0   15073  beta_ala              5                      15              75   
1   20438  beta_ala              2                      12              27   
2   25778  beta_ala              4                      15              60   
3   26107  beta_ala              8                      15             120   
4   27351  beta_ala              2                      14              29   
5   28514   placebo              7                      15             105   
6   33468   placebo              3                      15              45   
7   39337   placebo              3                      14              44   
8   39750   placebo              2                      15              30   
9   44858  beta_ala              3                      14              44   
10  49444   placebo              3                      14              44   
11  49830  beta_ala              4                      15              60   
12  50843   placebo              3                      12              42   
13  54145  beta_ala              3                      13              43   
14  54658   placebo              4                      11              56   
15  58046  beta_ala              3                      14              44   
16  59289  beta_ala              4                      10              55   
17  61104   placebo              2                      13              28   
18  71620   placebo              2                      11              26   
19  73162  beta_ala              3                      10              40   
20  76847   placebo              2                      11              26   
21  82556   placebo              6                      15              90   
22  93302   placebo              2                      15              30   
23  93672  beta_ala              2                      15              30   

     cut_at_pre  sets_done_post  reps_done_last_set_post  total_reps_post  \
0           NaN               6                       13               88   
1   s2 rep > 24               7                       13              103   
2           NaN               2                       14               29   
3           NaN               6                       14               89   
4     s2 rep>28               1                       14               14   
5           NaN               7                        9               99   
6           NaN               2                       14               29   
7   s3 rep > 28               4                       15               60   
8           NaN               4                       12               57   
9   s3 rep > 28               4                       13               58   
10  s3 rep > 28               4                       15               60   
11          NaN               4                       11               56   
12   s3 re > 24               3                       13               43   
13  s3 rep > 26               3                       14               44   
14  s4 rep > 22               4                       15               60   
15  s3 rep > 28               2                       15               30   
16  s4 rep > 20               3                        8               38   
17  s2 rep > 26               2                       11               26   
18  s2 rep > 22               1                       15               15   
19  s3 rep > 20               6                       15               90   
20  s2 rep > 22               2                       13               28   
21          NaN               3                       15               45   
22          NaN               1                       13               13   
23          NaN               2                       14               29   

    Unnamed: 9  cut_at_post  letzte_peaks_1_pre  letzte_peaks_2_pre  \
0          NaN  s6 rep > 26               127.5            

In [162]:

absolvierte_reps_l = pd.melt(absolvierte_reps[['total_reps_pre', 'total_reps_post', 'id', 'group']], 
                             id_vars=['id', 'group'], var_name = 'measurement', value_name='reps done')

In [163]:
(
    ggplot(absolvierte_reps_l, aes(x='measurement', y='reps done'))
    + geom_boxplot(aes(color='group', group='group'))
    + labs(title='Total absolvierte Wiederholungen im Fatigue Protokoll bis Abbruchkrit.')
    + ylab('Reps total')
)

In [164]:
rep_stat = pd.read_excel(r"C:\Users\bvenn\OneDrive\Desktop\Publikation\Zusammenfassung Arbeitssätze\Absolvierte_reps.xlsx", 
                         sheet_name = 'Sheet3')

reps_stat = pg.mixed_anova(dv='reps',between='group', within='experiment', subject='id', data=rep_stat, correction='auto', effsize='np2')
reps_stat

Source          SS  DF1  DF2          MS         F     p-unc  \
0        group  784.083333    1   22  784.083333  0.739588  0.399068   
1   experiment    2.083333    1   22    2.083333  0.006085  0.938527   
2  Interaction  108.000000    1   22  108.000000  0.315458  0.580028   

        np2  eps  
0  0.032524  NaN  
1  0.000277  1.0  
2  0.014136  NaN

## Gesamte Arbeit berechnen. Aufgeteilt nach Pre- und Post-Test. Arbeit als torque integral über die gesamte range of Motion. Nötige Schritte:

- Einzelnen Probanden aus iso herausfiltern
- Probandenframe nach Pre- und Posttest aufteilen und index resetten s.u.
- absolute Peak torque Werte berechnen mit .abs()
- Strecke berechenen mit Formel oder mit aufsummierten differenzen. Unterschiede Verstehen
- Arbeit als Integral des Drehmoments über der Strecke berechnen


## ab hier kann gelöscht werden

In [27]:
# frame für einzelnen probanden filtern

p15073 = iso[iso['id'] == 15073]

# Filtern des Probandenframes nach pre und posttest

p15073_pre = p15073[p15073['experiment'] == 'pretest'].copy()
p15073_post = p15073[p15073['experiment'] == 'posttest'].copy()

# Zeit-Spalte anpassen, um alle Messungen des Experimentes hintereinander betrachten zu können
# → Pausenzeiten werden nicht dargestellt
p15073_pre.loc[:, 'time_ms'] = p15073_pre.index * 5 + 5

# index reset, um wieder bei 5ms anzufangen
p15073_post.reset_index(drop=True, inplace=True)
p15073_post.loc[:, 'time_ms'] = p15073_post.index * 5 + 5

In [28]:
# Visualisierung der Kraft-Zeitverläufe im Pre-Test
# ACHTUNG: Spitzenwerte höchstwahrscheinlich exzentrisches torque

(
    ggplot(p15073_pre, aes(x='time_ms', y='torque_nm'))
    + geom_line(aes(color='measurement'))
)

In [29]:
# Visualisierung der Kraft-Stecken im Pre-Test
# ACHTUNG: ROM wird vor und zurück gefahren. 

(
    ggplot(p15073_pre, aes(x='pos_deg_or_mm', y='torque_nm'))
    + geom_line(aes(color='measurement'))
)

### Wie viel Strecke wird im experiment durchlaufen?
#### Die Strecke zwischen minimalen Gelenkwinkel bis maximalen Gelenkwinkel entspricht der Exzentrik. Von maximalen Gelenkwinkel zu minimalen Gelenkwinkel entspricht der Konzentrik. 
- Die Strecke zwischen min und max wird im warmup 40 Mal durchlaufen (20 exz. 20 konz), 
- im PT-Test 10 Mal 
- und in jedem Satz der Belastung 30 Mal

In [30]:
(
    ggplot(p15073_pre, aes(x='time_ms', y='pos_deg_or_mm'))
    + geom_line(aes(color='measurement'))
    + labs(title='Positions - Zeit Kurve')
)

In [31]:
p15073_pre['displacement_deg_or_mm'] = p15073_pre['pos_deg_or_mm'].diff()

# Filtere Werte über 0.7 aus der Spalte. Beim Satzübergang und in der letzten diff sind werte zu groß
p15073_pre['displacement_deg_or_mm'] = p15073_pre['displacement_deg_or_mm'].where(p15073_pre['displacement_deg_or_mm'].abs() <= 0.6, other=np.nan)

# Summierte Positionsänderungen als Gesamtstrecke
gesamtstrecke_mm = p15073_pre['displacement_deg_or_mm'].abs().sum()
print('Gesamtstrecke:', gesamtstrecke_mm, 'Millimeter')


Gesamtstrecke: 15635.999999999998 Millimeter


In [32]:
(
    ggplot(p15073_pre, aes(x='time_ms', y='displacement_deg_or_mm'))
    + geom_line(aes(color='measurement'))
    + labs(title='Displacement - Zeit Kurve')
)

In [33]:
p15073_pre['gesamtstrecke_m'] = p15073_pre.index * ((gesamtstrecke_mm / 1000) / (len(p15073_pre) - 1))

In [34]:
# Berechnung absoluter Torque Werte, um Drehmoment in jede Richtung zu erfassen
p15073_pre['torque_nm_abs'] = p15073_pre['torque_nm'].abs()

In [35]:
# Visualisierung der Kraft-Stecken im Pre-Test
# ACHTUNG: ROM wird vor und zurück gefahren. 

(
    ggplot(p15073_pre, aes(x='gesamtstrecke_m', y='torque_nm_abs'))
    + geom_line(aes(color='measurement'))
)

## Gesamt geleistete Arbeit berechnen als Fläche des Torque - Strecken Integrals. ACHTUNG: Die gesamte Arbeit ist sehr gering im Vergleich zu dem Beispiel von Uli. Chat GPT sagt das könne der Energie von 15-20 Minuten Fahrradergometer gleichkommen. Uli Fragen und überprüfen!

In [36]:
work_done = trapz(p15073_pre['torque_nm_abs'], p15073_pre['gesamtstrecke_m'])

print('Gesamte Arbeit:', work_done, 'Joule')

Gesamte Arbeit: 1386.9366052813973 Joule


## bis hier kann gelöscht werden

# Automatisierung zur Berechnung der Arbeit nach Gruppe und Pre-Post-Test

In [43]:
# Eindeutige Probanden-IDs extrahieren
probanden_ids = iso['id'].unique()

# DataFrame für die gesamte Arbeit erstellen
total_work_done = pd.DataFrame(columns=['id', 'experiment', 'group', 'work_done'])

for proband_id in probanden_ids:
    proband_data = iso[iso['id'] == proband_id]
    
    # Gruppeninfo abgreifen
    group = proband_data['group'].iloc[0]
    
    # Filtern des Probandenframes nach pre und posttest
    proband_data_pre = proband_data[proband_data['experiment'] == 'pretest'].copy()
    proband_data_post = proband_data[proband_data['experiment'] == 'posttest'].copy()

    # Zeit-Spalte anpassen für den Pretest
    proband_data_pre.loc[:, 'time_ms'] = proband_data_pre.index * 5 + 5

    # Index zurücksetzen, um wieder bei 5ms zu beginnen für den Posttest
    proband_data_post.reset_index(drop=True, inplace=True)
    proband_data_post.loc[:, 'time_ms'] = proband_data_post.index * 5 + 5

    # Berechnung der Positionsänderung für den Pretest
    proband_data_pre['displacement_deg_or_mm'] = proband_data_pre['pos_deg_or_mm'].diff()
    proband_data_post['displacement_deg_or_mm'] = proband_data_post['pos_deg_or_mm'].diff()

    # Filtere Werte über 0.7 aus der Spalte für den Pretest
    proband_data_pre['displacement_deg_or_mm'] = proband_data_pre['displacement_deg_or_mm'].where(proband_data_pre['displacement_deg_or_mm'].abs() <= 0.6, other=np.nan)
    proband_data_post['displacement_deg_or_mm'] = proband_data_post['displacement_deg_or_mm'].where(proband_data_post['displacement_deg_or_mm'].abs() <= 0.6, other=np.nan)
    
    # Summierte Positionsänderungen als Gesamtstrecke für den Pretest
    gesamtstrecke_mm_pre = proband_data_pre['displacement_deg_or_mm'].abs().sum()
    gesamtstrecke_m_pre = gesamtstrecke_mm_pre / 1000  # Auf Meter umgerechnet
    gesamtstrecke_mm_post = proband_data_post['displacement_deg_or_mm'].abs().sum()
    gesamtstrecke_m_post = gesamtstrecke_mm_post / 1000  # Auf Meter umgerechnet
    
    # Berechnung der normierten Zeit für den Pretest
    proband_data_pre['gesamtstrecke_m'] = proband_data_pre.index * (gesamtstrecke_m_pre / (len(proband_data_pre) - 1))
    proband_data_post['gesamtstrecke_m'] = proband_data_post.index * (gesamtstrecke_m_post / (len(proband_data_post) - 1))

    # Berechnung absoluter Torque Werte, um Drehmoment in jede Richtung zu erfassen
    proband_data_pre['torque_nm_abs'] = proband_data_pre['torque_nm'].abs()
    proband_data_post['torque_nm_abs'] = proband_data_post['torque_nm'].abs()

    # Berechnung der Arbeit für den Pretest
    work_done_pre = trapz(proband_data_pre['torque_nm_abs'], proband_data_pre['gesamtstrecke_m'])
    work_done_post = trapz(proband_data_post['torque_nm_abs'], proband_data_post['gesamtstrecke_m'])

    # Ergebnisse zum total_work_done DataFrame hinzufügen
    total_work_done = pd.concat([
        total_work_done,
        pd.DataFrame({
            'id': [proband_id, proband_id],
            'experiment': ['pretest', 'posttest'],
            'group': [group, group],
            'work_done': [work_done_pre, work_done_post]
        })
    ], ignore_index=True)



C:\Users\bvenn\AppData\Local\Temp\ipykernel_8444\2347857398.py:51: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  total_work_done = pd.concat([


In [44]:
total_work_done.head()

id experiment     group    work_done
0  15073    pretest  beta_ala  1386.936605
1  15073   posttest  beta_ala  1598.201652
2  20438    pretest  beta_ala  1042.867295
3  20438   posttest  beta_ala  1931.843694
4  25778    pretest  beta_ala  1196.424275

In [167]:
(
    ggplot(total_work_done, aes(x='experiment', y='work_done'))
    + geom_boxplot(aes(group='group', color='group'))
    + labs(title='Total Work Done: Warm-up bis Ende letzter Satz', subtitle='Achtung nicht bin Abbruchkriterium')
    + ylab('Arbeit in Joule')
    + xlab('Messung')
)

In [21]:
total_work_stat = pg.mixed_anova(dv='work_done',between='group', within='experiment', subject='id', data=total_work_done, correction='auto', effsize='np2')
total_work_stat

Source             SS  DF1  DF2             MS         F     p-unc  \
0        group  865257.509957    1   22  865257.509957  4.029210  0.057159   
1   experiment     197.207624    1   22     197.207624  0.004234  0.948708   
2  Interaction    6451.787662    1   22    6451.787662  0.138509  0.713329   

        np2  eps  
0  0.154796  NaN  
1  0.000192  1.0  
2  0.006256  NaN

# Arbeit berechnen von Warmup bis Abbruchkriterium

In [45]:
# Setze den Index zurück
iso_reset = iso.reset_index(drop=True)

# Definiere die Bedingungen für die Filterung
pretest_conditions = (
    # pretest
    (iso_reset['id'] == 20438) & (iso_reset['measurement'] == 's2') & (iso_reset['experiment'] == 'pretest') & (iso_reset['rep'] > 24) |
    (iso_reset['id'] == 27351) & (iso_reset['measurement'] == 's2') & (iso_reset['experiment'] == 'pretest') & (iso_reset['rep'] > 28) |
    (iso_reset['id'] == 39337) & (iso_reset['measurement'] == 's3') & (iso_reset['experiment'] == 'pretest') & (iso_reset['rep'] > 28) |
    (iso_reset['id'] == 44858) & (iso_reset['measurement'] == 's3') & (iso_reset['experiment'] == 'pretest') & (iso_reset['rep'] > 28) |
    (iso_reset['id'] == 49444) & (iso_reset['measurement'] == 's3') & (iso_reset['experiment'] == 'pretest') & (iso_reset['rep'] > 28) |
    (iso_reset['id'] == 50843) & (iso_reset['measurement'] == 's3') & (iso_reset['experiment'] == 'pretest') & (iso_reset['rep'] > 24) |
    (iso_reset['id'] == 54145) & (iso_reset['measurement'] == 's3') & (iso_reset['experiment'] == 'pretest') & (iso_reset['rep'] > 26) |
    (iso_reset['id'] == 54658) & (iso_reset['measurement'] == 's4') & (iso_reset['experiment'] == 'pretest') & (iso_reset['rep'] > 22) |
    (iso_reset['id'] == 58046) & (iso_reset['measurement'] == 's3') & (iso_reset['experiment'] == 'pretest') & (iso_reset['rep'] > 28) |
    (iso_reset['id'] == 59289) & (iso_reset['measurement'] == 's4') & (iso_reset['experiment'] == 'pretest') & (iso_reset['rep'] > 20) |
    (iso_reset['id'] == 61104) & (iso_reset['measurement'] == 's2') & (iso_reset['experiment'] == 'pretest') & (iso_reset['rep'] > 26) |
    (iso_reset['id'] == 71620) & (iso_reset['measurement'] == 's2') & (iso_reset['experiment'] == 'pretest') & (iso_reset['rep'] > 22) |
    (iso_reset['id'] == 73162) & (iso_reset['measurement'] == 's3') & (iso_reset['experiment'] == 'pretest') & (iso_reset['rep'] > 20) |
    (iso_reset['id'] == 76847) & (iso_reset['measurement'] == 's2') & (iso_reset['experiment'] == 'pretest') & (iso_reset['rep'] > 22)
)

posttest_conditions = (
    # posttest
    (iso_reset['id'] == 15073) & (iso_reset['measurement'] == 's6') & (iso_reset['experiment'] == 'posttest') & (iso_reset['rep'] > 26) |
    (iso_reset['id'] == 20438) & (iso_reset['measurement'] == 's7') & (iso_reset['experiment'] == 'posttest') & (iso_reset['rep'] > 26) |
    (iso_reset['id'] == 25778) & (iso_reset['measurement'] == 's2') & (iso_reset['experiment'] == 'posttest') & (iso_reset['rep'] > 28) |
    (iso_reset['id'] == 26107) & (iso_reset['measurement'] == 's6') & (iso_reset['experiment'] == 'posttest') & (iso_reset['rep'] > 28) |
    (iso_reset['id'] == 27351) & (iso_reset['measurement'] == 's1') & (iso_reset['experiment'] == 'posttest') & (iso_reset['rep'] > 28) |
    (iso_reset['id'] == 28514) & (iso_reset['measurement'] == 's7') & (iso_reset['experiment'] == 'posttest') & (iso_reset['rep'] > 18) |
    (iso_reset['id'] == 33468) & (iso_reset['measurement'] == 's2') & (iso_reset['experiment'] == 'posttest') & (iso_reset['rep'] > 28) |
    (iso_reset['id'] == 39750) & (iso_reset['measurement'] == 's4') & (iso_reset['experiment'] == 'posttest') & (iso_reset['rep'] > 24) |
    (iso_reset['id'] == 44858) & (iso_reset['measurement'] == 's4') & (iso_reset['experiment'] == 'posttest') & (iso_reset['rep'] > 26) |
    (iso_reset['id'] == 49830) & (iso_reset['measurement'] == 's4') & (iso_reset['experiment'] == 'posttest') & (iso_reset['rep'] > 22) |
    (iso_reset['id'] == 50843) & (iso_reset['measurement'] == 's3') & (iso_reset['experiment'] == 'posttest') & (iso_reset['rep'] > 26) |
    (iso_reset['id'] == 54145) & (iso_reset['measurement'] == 's3') & (iso_reset['experiment'] == 'posttest') & (iso_reset['rep'] > 28) |
    (iso_reset['id'] == 59289) & (iso_reset['measurement'] == 's3') & (iso_reset['experiment'] == 'posttest') & (iso_reset['rep'] > 16) |
    (iso_reset['id'] == 61104) & (iso_reset['measurement'] == 's2') & (iso_reset['experiment'] == 'posttest') & (iso_reset['rep'] > 22) |
    (iso_reset['id'] == 76847) & (iso_reset['measurement'] == 's2') & (iso_reset['experiment'] == 'posttest') & (iso_reset['rep'] > 26) |
    (iso_reset['id'] == 93302) & (iso_reset['measurement'] == 's1') & (iso_reset['experiment'] == 'posttest') & (iso_reset['rep'] > 26) |
    (iso_reset['id'] == 93672) & (iso_reset['measurement'] == 's2') & (iso_reset['experiment'] == 'posttest') & (iso_reset['rep'] > 28)
)

# Kombiniere die Bedingungen
combined_conditions = pretest_conditions | posttest_conditions

# Wende die Bedingungen an und filtere den DataFrame
warmup_abbruch = iso_reset[~combined_conditions].reset_index(drop=True)


In [46]:
def calculate_work_done(df):
    # Eindeutige Probanden-IDs extrahieren
    probanden_ids = df['id'].unique()

    # DataFrame für die gesamte Arbeit erstellen
    total_work_done = pd.DataFrame(columns=['id', 'experiment', 'group', 'work_done'])

    for proband_id in probanden_ids:
        proband_data = df[df['id'] == proband_id]

        # Gruppeninfo abgreifen
        group = proband_data['group'].iloc[0]
    
        # Filtern des Probandenframes nach pre und posttest
        proband_data_pre = proband_data[proband_data['experiment'] == 'pretest'].copy()
        proband_data_post = proband_data[proband_data['experiment'] == 'posttest'].copy()

        # Zeit-Spalte anpassen für den Pretest
        proband_data_pre.loc[:, 'time_ms'] = proband_data_pre.index * 5 + 5

        # Index zurücksetzen, um wieder bei 5ms zu beginnen für den Posttest
        proband_data_post.reset_index(drop=True, inplace=True)
        proband_data_post.loc[:, 'time_ms'] = proband_data_post.index * 5 + 5

        # Berechnung der Positionsänderung für den Pretest
        proband_data_pre['displacement_deg_or_mm'] = proband_data_pre['pos_deg_or_mm'].diff()
        proband_data_post['displacement_deg_or_mm'] = proband_data_post['pos_deg_or_mm'].diff()

        # Filtere Werte über 0.7 aus der Spalte für den Pretest
        proband_data_pre['displacement_deg_or_mm'] = proband_data_pre['displacement_deg_or_mm'].where(proband_data_pre['displacement_deg_or_mm'].abs() <= 0.6, other=np.nan)
        proband_data_post['displacement_deg_or_mm'] = proband_data_post['displacement_deg_or_mm'].where(proband_data_post['displacement_deg_or_mm'].abs() <= 0.6, other=np.nan)
        
        # Summierte Positionsänderungen als Gesamtstrecke für den Pretest
        gesamtstrecke_mm_pre = proband_data_pre['displacement_deg_or_mm'].abs().sum()
        gesamtstrecke_m_pre = gesamtstrecke_mm_pre / 1000  # Auf Meter umgerechnet
        gesamtstrecke_mm_post = proband_data_post['displacement_deg_or_mm'].abs().sum()
        gesamtstrecke_m_post = gesamtstrecke_mm_post / 1000  # Auf Meter umgerechnet
        
        # Berechnung der normierten Zeit für den Pretest
        proband_data_pre['gesamtstrecke_m'] = proband_data_pre.index * (gesamtstrecke_m_pre / (len(proband_data_pre) - 1))
        proband_data_post['gesamtstrecke_m'] = proband_data_post.index * (gesamtstrecke_m_post / (len(proband_data_post) - 1))

        # Berechnung absoluter Torque Werte, um Drehmoment in jede Richtung zu erfassen
        proband_data_pre['torque_nm_abs'] = proband_data_pre['torque_nm'].abs()
        proband_data_post['torque_nm_abs'] = proband_data_post['torque_nm'].abs()

        # Berechnung der Arbeit für den Pretest
        work_done_pre = trapz(proband_data_pre['torque_nm_abs'], proband_data_pre['gesamtstrecke_m'])
        work_done_post = trapz(proband_data_post['torque_nm_abs'], proband_data_post['gesamtstrecke_m'])

        # Ergebnisse zum total_work_done DataFrame hinzufügen
        total_work_done = pd.concat([
            total_work_done,
            pd.DataFrame({
                'id': [proband_id, proband_id],
                'experiment': ['pretest', 'posttest'],
                'group': [group, group],
                'work_done': [work_done_pre, work_done_post]
            })
        ], ignore_index=True)

    return total_work_done

# Anwenden auf warmup_abbruch
total_work_done_warmup_abbruch = calculate_work_done(warmup_abbruch)


C:\Users\bvenn\AppData\Local\Temp\ipykernel_8444\3791908521.py:52: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  total_work_done = pd.concat([


In [47]:
total_work_done_warmup_abbruch.head()

id experiment     group    work_done
0  15073    pretest  beta_ala  1386.936605
1  15073   posttest  beta_ala  1582.154194
2  20438    pretest  beta_ala  1013.765596
3  20438   posttest  beta_ala  1914.849472
4  25778    pretest  beta_ala  1196.424275

In [48]:
work_pre = total_work_done_warmup_abbruch[total_work_done_warmup_abbruch['experiment']=='pretest'].reset_index(drop=True)
work_post = total_work_done_warmup_abbruch[total_work_done_warmup_abbruch['experiment']=='posttest'].reset_index(drop=True)

In [49]:
work_pre['work_diff'] = work_post['work_done'] - work_pre['work_done']
work_pre

id experiment     group    work_done   work_diff
0   15073    pretest  beta_ala  1386.936605  195.217589
1   20438    pretest  beta_ala  1013.765596  901.083876
2   25778    pretest  beta_ala  1196.424275 -457.670353
3   26107    pretest  beta_ala  1902.483669 -339.155712
4   27351    pretest  beta_ala   487.111735 -113.342275
5   28514    pretest   placebo  1018.591019   14.309825
6   93672    pretest  beta_ala   909.051376   -6.835908
7   33468    pretest   placebo   694.327348 -137.898801
8   39337    pretest   placebo  1102.417785  204.866518
9   39750    pretest   placebo   584.580110  207.182604
10  44858    pretest  beta_ala   702.136362  133.161934
11  49444    pretest   placebo   525.525198   87.150999
12  49830    pretest  beta_ala   899.440328  -51.836585
13  50843    pretest   placebo  1276.216938  -58.198350
14  54145    pretest  beta_ala  1050.220275   30.071572
15  54658    pretest   placebo   928.362821   88.556166
16  58046    pretest  beta_ala  1347.752949 -244.174711
17  59289    pretest  beta_ala  1739.705425 -418.698061
18  61104    pretest   placebo   970.831016   -7.613598
19  71620    pretest   placebo   698.554002  -91.661216
20  73162    pretest  beta_ala   959.184024  559.595275
21  76847    pretest   placebo   721.109961   72.908297
22  82556    pretest   placebo  1439.678951 -496.885992
23  93302    pretest   placebo   697.091367 -188.035523

In [50]:
(
    ggplot(work_pre, aes(x='group', y='work_diff', color='group'))
    + geom_boxplot()
    + ylab('Work Difference [J]')
)

In [199]:
x = work_pre.query('group == "placebo"')['work_diff']
y = work_pre.query('group == "beta_ala"')['work_diff']

In [200]:
work_stat = pg.ttest(x, y, paired=False, alternative='less', correction='auto')
work_stat

T  dof alternative     p-val           CI95%   cohen-d   BF10  \
T-test -0.320611   22        less  0.375765  [-inf, 178.86]  0.130889  0.775   

           power  
T-test  0.091104

In [188]:
total_work_done_warmup_abbruch.to_

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 48 entries, 0 to 47
Data columns (total 4 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   id          48 non-null     object 
 1   experiment  48 non-null     object 
 2   group       48 non-null     object 
 3   work_done   48 non-null     float64
dtypes: float64(1), object(3)
memory usage: 1.6+ KB


In [172]:
(
    ggplot(total_work_done_warmup_abbruch, aes(x='experiment', y='work_done'))
    + geom_boxplot(aes(group='group', color='group'))
    + labs(title='Total Work Done: Warm-up bis Abbruchkriterium')
    + ylab('Work [J]')
    + xlab('Messung')
)

In [173]:
work_wu_abb_stat = pg.mixed_anova(dv='work_done',between='group', within='experiment', subject='id', data=total_work_done_warmup_abbruch, correction='auto', effsize='np2')
work_wu_abb_stat

Source             SS  DF1  DF2             MS         F     p-unc  \
0        group  844446.702052    1   22  844446.702052  4.103884  0.055082   
1   experiment     289.603811    1   22     289.603811  0.005885  0.939543   
2  Interaction    5058.093390    1   22    5058.093390  0.102792  0.751530   

        np2  eps  
0  0.157214  NaN  
1  0.000267  1.0  
2  0.004651  NaN

In [175]:
posthoc_work_wu_abb = pg.pairwise_tests(data=total_work_done_warmup_abbruch, dv='work_done', between='group', subject='id', parametric=True, padjust='bonf', effsize='cohen')
posthoc_work_wu_abb

Contrast         A        B  Paired  Parametric         T   dof alternative  \
0    group  beta_ala  placebo   False        True  2.630256  46.0   two-sided   

      p-unc   BF10    cohen  
0  0.011567  4.342  0.75929

## Plot für die geleistete Arbeit aller Probanden in den jeweiligen Messzeitpunkten

In [176]:
def calculate_work_done_per_measurement(df):
    # Eindeutige Probanden-IDs extrahieren
    probanden_ids = df['id'].unique()

    # DataFrame für die gesamte Arbeit erstellen
    total_work_done = pd.DataFrame(columns=['id', 'experiment', 'group', 'measurement', 'work_done'])

    for proband_id in probanden_ids:
        proband_data = df[df['id'] == proband_id]

        # Gruppeninfo abgreifen
        group = proband_data['group'].iloc[0]

        # Eindeutige Messzeitpunkte extrahieren
        measurements = proband_data['measurement'].unique()

        for measurement in measurements:
            measurement_data = proband_data[proband_data['measurement'] == measurement].copy()

            # Zeit-Spalte anpassen für den Messzeitpunkt
            measurement_data.loc[:, 'time_ms'] = measurement_data.index * 5 + 5

            # Index zurücksetzen, um wieder bei 5ms zu beginnen
            measurement_data.reset_index(drop=True, inplace=True)
            measurement_data.loc[:, 'time_ms'] = measurement_data.index * 5 + 5

            # Berechnung der Positionsänderung
            measurement_data['displacement_deg_or_mm'] = measurement_data['pos_deg_or_mm'].diff()

            # Filtere Werte über 0.7 aus der Spalte
            measurement_data['displacement_deg_or_mm'] = measurement_data['displacement_deg_or_mm'].where(
                measurement_data['displacement_deg_or_mm'].abs() <= 0.6, other=np.nan
            )

            # Summierte Positionsänderungen als Gesamtstrecke
            gesamtstrecke_mm = measurement_data['displacement_deg_or_mm'].abs().sum()
            gesamtstrecke_m = gesamtstrecke_mm / 1000  # Auf Meter umgerechnet

            # Berechnung der normierten Zeit
            measurement_data['gesamtstrecke_m'] = measurement_data.index * (gesamtstrecke_m / (len(measurement_data) - 1))

            # Berechnung absoluter Torque Werte, um Drehmoment in jede Richtung zu erfassen
            measurement_data['torque_nm_abs'] = measurement_data['torque_nm'].abs()

            # Berechnung der Arbeit
            work_done = trapz(measurement_data['torque_nm_abs'], measurement_data['gesamtstrecke_m'])

            # Ergebnisse zum total_work_done DataFrame hinzufügen
            total_work_done = pd.concat([
                total_work_done,
                pd.DataFrame({
                    'id': [proband_id],
                    'experiment': [measurement_data['experiment'].iloc[0]],
                    'group': [group],
                    'measurement': [measurement],
                    'work_done': [work_done]
                })
            ], ignore_index=True)

    return total_work_done

# Anwenden auf warmup_abbruch
total_work_done_per_measurement = calculate_work_done_per_measurement(warmup_abbruch)


C:\Users\bvenn\AppData\Local\Temp\ipykernel_7280\680265839.py:49: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  total_work_done = pd.concat([


In [177]:
total_work_done_posttest = calculate_work_done_per_measurement(warmup_abbruch[warmup_abbruch['experiment'] == 'posttest'])

C:\Users\bvenn\AppData\Local\Temp\ipykernel_7280\680265839.py:49: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  total_work_done = pd.concat([


In [178]:
total_work_done_pretest = total_work_done_per_measurement.query('experiment == "pretest"')

In [179]:
# mittelwerte und Standartabweichungen der Arbeit in Pretest und Posttest berechnen

grouped_means_pre = total_work_done_pretest.groupby(['group', 'measurement'], observed=False).agg({'work_done':'mean'}).reset_index()
grouped_std_pre = total_work_done_pretest.groupby(['group', 'measurement'], observed=False).agg({'work_done':'std'}).reset_index()

grouped_means_post = total_work_done_posttest.groupby(['group', 'measurement'], observed=False).agg({'work_done':'mean'}).reset_index()
grouped_std_post = total_work_done_posttest.groupby(['group', 'measurement'], observed=False).agg({'work_done':'std'}).reset_index()

#spalten der mittelwerte umbennen
grouped_means_pre.rename(columns={
    'work_done': 'work_done_mean',
}, inplace=True)

grouped_means_post.rename(columns={
    'work_done': 'work_done_mean',
}, inplace=True)

# spalten der std umbennen
grouped_std_pre.rename(columns={
    'work_done': 'work_done_std',
}, inplace=True)

grouped_std_post.rename(columns={
    'work_done': 'work_done_std',
}, inplace=True)

In [180]:
# frame mit arbeits-mittelwerten die std hinzufügen. pretest
grouped_means_pre = pd.concat([grouped_means_pre, grouped_std_pre.drop(['group', 'measurement'], axis=1)], axis=1)
grouped_means_post = pd.concat([grouped_means_post, grouped_std_post.drop(['group', 'measurement'], axis=1)], axis=1)

In [181]:
# Zuerst die Anzahl der Werte pro Gruppe und Messung berechnen
count_data = total_work_done_pretest.groupby(['group', 'measurement'])['work_done'].count().reset_index(name='count')

# Merge der Anzahl der Werte mit den gruppierten Mittelwerten
grouped_means_pre_with_count = pd.merge(grouped_means_pre, count_data, on=['group', 'measurement'])

# Plot erstellen
(
    ggplot(grouped_means_pre_with_count, aes(x='measurement', y='work_done_mean', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(
            ymin=grouped_means_pre_with_count['work_done_mean'] - grouped_means_pre_with_count['work_done_std'],
            ymax=grouped_means_pre_with_count['work_done_mean'] + grouped_means_pre_with_count['work_done_std'],
            fill='group'
        ),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + geom_text(
        aes(label='count'),
        position=position_dodge(width=0.4),
        nudge_x=0.4,
        vjust=-0.5,
        size=8
    )
    + labs(
        title='Pre-Test: Mittelwerte und Std geleisteter Arbeit nach Zeitpunkt und Gruppe',
        subtitle='Zahlen im Plot entsprechen der Anzahl der Probanden, die den jeweiligen Satz\n absolviert haben'
    )
    + ylab('Work Done [J]')
    + xlab('Messung')
    + scale_x_discrete(limits=['warmup', 'pt', 's1', 's2', 's3', 's4', 's5', 's6', 's7', 's8'])
)


In [182]:
# Zuerst die Anzahl der Werte pro Gruppe und Messung berechnen
count_data = total_work_done_posttest.groupby(['group', 'measurement'])['work_done'].count().reset_index(name='count')

# Merge der Anzahl der Werte mit den gruppierten Mittelwerten
grouped_means_post_with_count = pd.merge(grouped_means_post, count_data, on=['group', 'measurement'])

# Plot erstellen
(
    ggplot(grouped_means_post_with_count, aes(x='measurement', y='work_done_mean', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(
            ymin=grouped_means_post_with_count['work_done_mean'] - grouped_means_post_with_count['work_done_std'],
            ymax=grouped_means_post_with_count['work_done_mean'] + grouped_means_post_with_count['work_done_std'],
            fill='group'
        ),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + geom_text(
        aes(label='count'),
        position=position_dodge(width=0.4),
        nudge_x=0.4,
        vjust=-0.5,
        size=8
    )
    + labs(
        title='Post-Test: Mittelwerte und Std geleisteter Arbeit nach Zeitpunkt und Gruppe',
        subtitle='Zahlen im Plot entsprechen der Anzahl der Probanden, die den jeweiligen Satz\n absolviert haben'
    )
    + ylab('Work Done [J]')
    + xlab('Messung')
    + scale_x_discrete(limits=['warmup', 'pt', 's1', 's2', 's3', 's4', 's5', 's6', 's7'])
)


In [183]:
my_colors = ['#FF5733', '#33FF57', '#3366FF', '#FFFF33', '#33FFFF', '#FF33FF', '#33CC00',
             '#FF33CC', '#FF6633', '#33FF00', '#6600CC', '#33CC33', '#FF00FF', '#6600FF',
             '#00CCFF', '#CC33CC', '#0066FF', '#33CC99', '#66CC00', '#996633', '#00FF33',
             '#CC0033', '#33CC66', '#CC66FF']

(
    ggplot(total_work_done_per_measurement.query('experiment == "pretest"'), aes(x='measurement', y='work_done', color='id', group='id'))
    + geom_point()
    + geom_line()
    + scale_color_manual(values=my_colors)
    + labs(title='Arbeit der Probanden für jeden Messzeitpunkt im Pre-Test', subtitle = 'Farben entsprechen ids')
    + theme(legend_position='none')
    + ylab('Work Done [J]')
    + xlab('Messzeitpunkt')
)

In [184]:
my_colors = ['#FF5733', '#33FF57', '#3366FF', '#FFFF33', '#33FFFF', '#FF33FF', '#33CC00',
             '#FF33CC', '#FF6633', '#33FF00', '#6600CC', '#33CC33', '#FF00FF', '#6600FF',
             '#00CCFF', '#CC33CC', '#0066FF', '#33CC99', '#66CC00', '#996633', '#00FF33',
             '#CC0033', '#33CC66', '#CC66FF']

(
    ggplot(total_work_done_posttest, aes(x='measurement', y='work_done', color='id', group='id'))
    + geom_point()
    + geom_line()
    + scale_color_manual(values=my_colors)
    + labs(title='Arbeit der Probanden für jeden Messzeitpunkt im Post-Test', subtitle = 'Farben entsprechen ids')
    + theme(legend_position='none')
    + ylab('Work Done [J]')
    + xlab('Messzeitpunkt')
)

In [185]:
participants_count_per_measurement = total_work_done_per_measurement.query('experiment == "pretest"').groupby('measurement')['id'].nunique().reset_index()

# Benenne die Spalten um
participants_count_per_measurement.columns = ['measurement', 'num_participants']

# Zeige den DataFrame an
print(participants_count_per_measurement)

  measurement  num_participants
0          pt                24
1          s1                24
2          s2                24
3          s3                16
4          s4                 8
5          s5                 4
6          s6                 3
7          s7                 2
8          s8                 1
9      warmup                24


## Berechnung der Arbeit von Paek Torque - Test zu Abbruchkriterium

In [51]:
# aus dem frame total_work_done_warmup_abbruch das Warmup herausfiltern

total_work_done_filtered = warmup_abbruch[warmup_abbruch['measurement'] != 'warmup'].reset_index(drop=True)

# funktion zur Arbeitanalyse anwenden
total_work_done_pt_abbruch = calculate_work_done(total_work_done_filtered)

C:\Users\bvenn\AppData\Local\Temp\ipykernel_8444\3791908521.py:52: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  total_work_done = pd.concat([


In [52]:
(
    ggplot(total_work_done_pt_abbruch, aes(x='experiment', y='work_done'))
    + geom_boxplot(aes(group='group', color='group'))
    + labs(title='Total Work Done: Peak Torque Test bis Abbruchkriterium')
    + ylab('Arbeit in Joule')
    + xlab('Messung')
)

In [53]:
work_pt_abb_stat = pg.mixed_anova(dv='work_done',between='group', within='experiment', subject='id', data=total_work_done_pt_abbruch, correction='auto', effsize='np2')
work_pt_abb_stat

Source             SS  DF1  DF2             MS         F     p-unc  \
0        group  766708.186452    1   22  766708.186452  4.988162  0.036011   
1   experiment      12.960312    1   22      12.960312  0.000256  0.987370   
2  Interaction    7790.756492    1   22    7790.756492  0.154103  0.698422   

        np2  eps  
0  0.184828  NaN  
1  0.000012  1.0  
2  0.006956  NaN

In [54]:
posthoc_pt_abb_stat = pg.pairwise_tests(data=total_work_done_pt_abbruch, dv='work_done', between='group', subject='id', parametric=True, padjust='bonf', effsize='cohen')
posthoc_pt_abb_stat

Contrast         A        B  Paired  Parametric         T   dof alternative  \
0    group  beta_ala  placebo   False        True  2.799066  46.0   two-sided   

      p-unc   BF10     cohen  
0  0.007465  6.113  0.808021

## S1- Abbruch

In [53]:
# frame mit S1 fatigue Protokoll bis Abbruchkriterium erstellen

# aus dem frame total_work_done_warmup_abbruch das Warmup herausfiltern

# Filtere die Zeilen mit 'measurement' != 'warmup' und 'pt'
s1_abbruch = warmup_abbruch[(warmup_abbruch['measurement'] != 'warmup') & (warmup_abbruch['measurement'] != 'pt')].reset_index(drop=True)

# funktion zur Arbeitsanalyse anwenden
total_work_done_s1_abbruch = calculate_work_done(s1_abbruch)

C:\Users\bvenn\AppData\Local\Temp\ipykernel_8444\3791908521.py:52: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  total_work_done = pd.concat([


In [202]:
(
    ggplot(total_work_done_s1_abbruch, aes(x='experiment', y='work_done'))
    + geom_boxplot(aes(group='group', color='group'))
    + labs(title='Total Work Done: S1 bis Abbruchkriterium')
    + ylab('Arbeit in Joule')
    + xlab('Messung')
)

In [203]:
work_s1_abb_stat = pg.mixed_anova(dv='work_done',between='group', within='experiment', subject='id', data=total_work_done_s1_abbruch, correction='auto', effsize='np2')
work_s1_abb_stat

Source             SS  DF1  DF2             MS         F     p-unc  \
0        group  628394.706537    1   22  628394.706537  4.297731  0.050079   
1   experiment     252.883635    1   22     252.883635  0.005241  0.942940   
2  Interaction   13794.991770    1   22   13794.991770  0.285916  0.598213   

        np2  eps  
0  0.163426  NaN  
1  0.000238  1.0  
2  0.012829  NaN

In [204]:
posthoc_work_s1_abb = pg.pairwise_tests(data=total_work_done_s1_abbruch, dv='work_done', between='group', subject='id', parametric=True, padjust='bonf', effsize='cohen')
posthoc_work_s1_abb

Contrast         A        B  Paired  Parametric         T   dof alternative  \
0    group  beta_ala  placebo   False        True  2.595091  46.0   two-sided   

      p-unc   BF10     cohen  
0  0.012648  4.052  0.749138

# Fatigue index bestimmen - Anhand von konzentrischem torque. Orientieren an Umgang Satzdiffernz notebook

In [54]:
# frame mit daten S1 bis Abbruch
s1_abbruch

id measurement  time_ms  pos_deg_or_mm  torque_nm  \
0        15073          s1        5           11.4       21.8   
1        15073          s1       10           11.6       21.8   
2        15073          s1       15           11.6       22.5   
3        15073          s1       20           11.4       24.0   
4        15073          s1       25           11.4       26.7   
...        ...         ...      ...            ...        ...   
1473081  93672          s2    43210           11.3       15.5   
1473082  93672          s2    43215           11.1       20.3   
1473083  93672          s2    43220           11.1       25.2   
1473084  93672          s2    43225           11.1       30.0   
1473085  93672          s2    43230           11.1       32.0   

         speed_deg/s_or_mm/s  torque_without_comp  rep  set  torque_dyn  \
0                        0.0                   72    1    1        -218   
1                        0.3                   68    1    1        -218   
2                        1.8                   65    1    1        -225   
3                        4.3                   57    1    1        -240   
4                        5.8                   53    1    1        -267   
...                      ...                  ...  ...  ...         ...   
1473081                -15.3                  150   28    1        -155   
1473082                -10.0                  102   28    1        -203   
1473083                 -8.3                   53   28    1        -252   
1473084                 -8.0                    5   28    1        -300   
1473085                 -7.8                  -15   28    1        -320   

         force_right  force_left experiment     group  
0                  0           0    pretest  beta_ala  
1                  0           0    pretest  beta_ala  
2                  0           0    pretest  beta_ala  
3                  0           0    pretest  beta_ala  
4                  0           0    pretest  beta_ala  
...              ...         ...        ...       ...  
1473081            0           0   posttest  beta_ala  
1473082            0           0   posttest  beta_ala  
1473083            0           0   posttest  beta_ala  
1473084            0           0   posttest  beta_ala  
1473085            0           0   posttest  beta_ala  

[1473086 rows x 14 columns]

### Top 3 peaks ermitteln und Mittwelwert aus diesen berechnen

In [55]:
# Erstellen Sie eine leere Liste, um die Ergebnisse zu speichern
peaks_largest = []

# Iterieren Sie über jeden Probanden und jeden Experimenttyp (Pretest und Posttest)
for _, sub_df in iso.groupby(['id', 'experiment', 'group']):
    proband_id, experiment_type, group = _
    
    # Filtern Sie den Frame für den aktuellen Probanden und Experimenttyp
    px = sub_df.query('rep % 2 == 0').copy()
    
    # Berechnungen durchführen (wie im vorherigen Code)
    px['torque_nm_abs'] = px['torque_nm'].abs()
    px.loc[:, 'time_ms'] = px.index * 5 + 5
    peaks, properties = find_peaks(px['torque_nm_abs'], height=50, distance=200)
    top_three_peaks = px['torque_nm_abs'].iloc[peaks].nlargest(3)
    mean_top_three = top_three_peaks.mean()
    
    
    # Ergebnisse speichern
    peaks_largest.append({
        'id': proband_id,
        'experiment': experiment_type,
        'group': group,
        'top_three_peaks': top_three_peaks.tolist(),
        'mean_top_three': mean_top_three,
    })

# Ergebnisse in ein DataFrame umwandeln
peaks_largest = pd.DataFrame(peaks_largest)



C:\Users\bvenn\AppData\Local\Temp\ipykernel_8444\2241818459.py:5: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  for _, sub_df in iso.groupby(['id', 'experiment', 'group']):


### Letzte drei peaks unter Berücksichtigung des Abbruchkriteriums ermitteln. Gesichtet und mit find peaks ermittelt. In Tabelle absolvierte_reps

In [56]:
# frames mit Dremomenten der letzten drei reps und deren Mittelwerte einlesen
means_last_reps = pd.read_excel(r"C:\Users\bvenn\OneDrive\Desktop\Publikation\Zusammenfassung Arbeitssätze\Absolvierte_reps.xlsx", sheet_name='Sheet2')

In [57]:
# Ausgabe des resultierenden DataFrame
peaks_largest = pd.merge(peaks_largest, means_last_reps[['experiment', 'id', 'group', 'Mean_peaks']], 
                         on=['experiment', 'id', 'group'], how='left')



### fatigue Index berechnen

In [58]:
peaks_largest['fatigue_index'] = ((peaks_largest['mean_top_three'] - peaks_largest['Mean_peaks']) / 
                                peaks_largest['mean_top_three']) * 100
peaks_largest

id experiment     group        top_three_peaks  mean_top_three  \
0   15073   posttest  beta_ala  [269.0, 264.8, 249.0]      260.933333   
1   15073    pretest  beta_ala  [249.5, 248.0, 243.0]      246.833333   
2   20438   posttest  beta_ala  [291.0, 284.7, 284.0]      286.566667   
3   20438    pretest  beta_ala  [306.8, 294.0, 292.2]      297.666667   
4   25778   posttest  beta_ala  [155.7, 152.3, 147.5]      151.833333   
5   25778    pretest  beta_ala  [163.2, 154.5, 145.5]      154.400000   
6   26107   posttest  beta_ala  [195.0, 194.0, 186.5]      191.833333   
7   26107    pretest  beta_ala  [201.5, 186.8, 182.0]      190.100000   
8   27351   posttest  beta_ala  [166.5, 161.0, 156.0]      161.166667   
9   27351    pretest  beta_ala  [162.8, 162.8, 155.0]      160.200000   
10  28514   posttest   placebo  [139.2, 130.2, 124.2]      131.200000   
11  28514    pretest   placebo  [121.2, 119.0, 118.2]      119.466667   
12  33468   posttest   placebo  [171.0, 164.0, 152.7]      162.566667   
13  33468    pretest   placebo  [158.0, 157.5, 156.5]      157.333333   
14  39337   posttest   placebo  [261.5, 258.5, 251.3]      257.100000   
15  39337    pretest   placebo  [296.7, 274.2, 268.5]      279.800000   
16  39750   posttest   placebo  [131.3, 130.5, 127.2]      129.666667   
17  39750    pretest   placebo  [139.2, 135.5, 131.7]      135.466667   
18  44858   posttest  beta_ala  [152.3, 147.5, 145.5]      148.433333   
19  44858    pretest  beta_ala  [143.3, 142.2, 140.7]      142.066667   
20  49444   posttest   placebo  [146.0, 141.0, 140.7]      142.566667   
21  49444    pretest   placebo  [137.0, 136.5, 134.0]      135.833333   
22  49830   posttest  beta_ala  [194.0, 192.0, 190.5]      192.166667   
23  49830    pretest  beta_ala  [185.3, 175.2, 174.8]      178.433333   
24  50843   posttest   placebo  [273.0, 266.3, 266.0]      268.433333   
25  50843    pretest   placebo  [272.0, 269.7, 267.8]      269.833333   
26  54145   posttest  beta_ala  [200.3, 192.8, 186.8]      193.300000   
27  54145    pretest  beta_ala  [213.5, 210.0, 201.0]      208.166667   
28  54658   posttest   placebo  [176.7, 175.5, 170.0]      174.066667   
29  54658    pretest   placebo  [184.5, 177.0, 170.7]      177.400000   
30  58046   posttest  beta_ala  [305.0, 293.3, 278.0]      292.100000   
31  58046    pretest  beta_ala  [307.2, 293.7, 291.5]      297.466667   
32  59289   posttest  beta_ala  [343.5, 338.0, 337.5]      339.666667   
33  59289    pretest  beta_ala  [341.3, 330.8, 328.5]      333.533333   
34  61104   posttest   placebo  [286.5, 271.2, 263.3]      273.666667   
35  61104    pretest   placebo  [274.5, 268.5, 261.8]      268.266667   
36  71620   posttest   placebo  [271.5, 258.5, 252.5]      260.833333   
37  71620    pretest   placebo  [230.7, 226.5, 222.0]      226.400000   
38  73162   posttest  beta_ala  [240.0, 224.3, 219.5]      227.933333   
39  73162    pretest  beta_ala  [252.8, 244.2, 240.8]      245.933333   
40  76847   posttest   placebo  [234.0, 230.3, 220.2]      228.166667   
41  76847    pretest   placebo  [225.0, 224.0, 222.8]      223.933333   
42  82556   posttest   placebo  [194.0, 187.2, 186.5]      189.233333   
43  82556    pretest   placebo  [179.7, 175.2, 170.7]      175.200000   
44  93302   posttest   placebo  [182.7, 181.2, 167.7]      177.200000   
45  93302    pretest   placebo  [178.2, 174.0, 170.3]      174.166667   
46  93672   posttest  beta_ala  [338.3, 325.2, 302.3]      321.933333   
47  93672    pretest  beta_ala  [294.5, 288.0, 287.3]      289.933333   

    Mean_peaks  fatigue_index  
0   121.666667      53.372509  
1   123.033333      50.155300  
2   128.433333      55.182040  
3   145.566667      51.097424  
4    67.166667      55.762898  
5    77.833333      49.589810  
6    92.166667      51.954822  
7    94.166667      50.464668  
8    70.200000      56.442606  
9    68.033333      57.532251  
10   57.833333      55.919715  
11   62.433333      47.739955  
12   79.30000

## differenzen im Fatigue index

In [59]:
fatigue_pre = peaks_largest[peaks_largest['experiment'] == 'pretest'].reset_index(drop=True)
fatigue_post = peaks_largest[peaks_largest['experiment'] == 'posttest'].reset_index(drop=True)

In [60]:
fatigue_pre['diff_fatigue_index'] = fatigue_post['fatigue_index'] - fatigue_pre['fatigue_index']
fatigue_pre

id experiment     group        top_three_peaks  mean_top_three  \
0   15073    pretest  beta_ala  [249.5, 248.0, 243.0]      246.833333   
1   20438    pretest  beta_ala  [306.8, 294.0, 292.2]      297.666667   
2   25778    pretest  beta_ala  [163.2, 154.5, 145.5]      154.400000   
3   26107    pretest  beta_ala  [201.5, 186.8, 182.0]      190.100000   
4   27351    pretest  beta_ala  [162.8, 162.8, 155.0]      160.200000   
5   28514    pretest   placebo  [121.2, 119.0, 118.2]      119.466667   
6   33468    pretest   placebo  [158.0, 157.5, 156.5]      157.333333   
7   39337    pretest   placebo  [296.7, 274.2, 268.5]      279.800000   
8   39750    pretest   placebo  [139.2, 135.5, 131.7]      135.466667   
9   44858    pretest  beta_ala  [143.3, 142.2, 140.7]      142.066667   
10  49444    pretest   placebo  [137.0, 136.5, 134.0]      135.833333   
11  49830    pretest  beta_ala  [185.3, 175.2, 174.8]      178.433333   
12  50843    pretest   placebo  [272.0, 269.7, 267.8]      269.833333   
13  54145    pretest  beta_ala  [213.5, 210.0, 201.0]      208.166667   
14  54658    pretest   placebo  [184.5, 177.0, 170.7]      177.400000   
15  58046    pretest  beta_ala  [307.2, 293.7, 291.5]      297.466667   
16  59289    pretest  beta_ala  [341.3, 330.8, 328.5]      333.533333   
17  61104    pretest   placebo  [274.5, 268.5, 261.8]      268.266667   
18  71620    pretest   placebo  [230.7, 226.5, 222.0]      226.400000   
19  73162    pretest  beta_ala  [252.8, 244.2, 240.8]      245.933333   
20  76847    pretest   placebo  [225.0, 224.0, 222.8]      223.933333   
21  82556    pretest   placebo  [179.7, 175.2, 170.7]      175.200000   
22  93302    pretest   placebo  [178.2, 174.0, 170.3]      174.166667   
23  93672    pretest  beta_ala  [294.5, 288.0, 287.3]      289.933333   

    Mean_peaks  fatigue_index  diff_fatigue_index  
0   123.033333      50.155300            3.217208  
1   145.566667      51.097424            4.084616  
2    77.833333      49.589810            6.173088  
3    94.166667      50.464668            1.490154  
4    68.033333      57.532251           -1.089645  
5    62.433333      47.739955            8.179760  
6    72.533333      53.898305           -2.678293  
7   145.700000      47.927091            7.408058  
8    65.700000      51.500984           -0.061396  
9    65.766667      53.707180           -3.606124  
10   68.566667      49.521472            9.024237  
11   78.833333      55.819167           -4.700346  
12  125.833333      53.366275            4.040902  
13   98.966667      52.457966            1.327169  
14   87.066667      50.920707            2.009205  
15  140.433333      52.790229            1.106839  
16  121.300000      63.631821          -12.630840  
17  119.833333      55.330517           -5.452320  
18   88.666667      60.836278           -4.734042  
19  122.166667      50.325291            3.096762  
20  108.200000      51.682048            5.688295  
21   86.770000      50.473744            2.353453  
22   78.800000      54.755981           -0.730398  
23  139.100000      52.023454            0.420116

In [61]:
(
    ggplot(fatigue_pre, aes(x='group', y='diff_fatigue_index', color='group'))
    + geom_boxplot()
    + ylab('Difference of Fatigue Index')
)

In [218]:
x = fatigue_pre.query('group == "placebo"')['diff_fatigue_index']
y = fatigue_pre.query('group == "beta_ala"')['diff_fatigue_index']

work_stat = pg.ttest(x, y, paired=False, alternative='less', correction='auto')
work_stat

T  dof alternative    p-val         CI95%   cohen-d   BF10  \
T-test  1.072912   22        less  0.85253  [-inf, 5.67]  0.438014  0.884   

           power  
T-test  0.003619

# ACHTUNG. Fatigue Index Werte sind nicht bei genau 50% (Abbruchkriterium 50 PT im Eigentlichen Test) weil der fatigue index die Sätze S1 -Abbruch berücksichtigt und nicht Peak Torque Test - Abbruch.
- fatigue index: Je größer die Differenz zwischen Anfang und Ende (Ermüdung), desto größer der Index und desto größer die Ermüdung.
- macht das Sinn? Wir haben doch 50% PT als Abbruch/Ermüdungskriterium definiert

In [210]:
(
    ggplot(peaks_largest, aes(x='experiment', y='fatigue_index'))
    + geom_boxplot(aes(group='group', color='group'))
    + labs(title = 'Fatigue Index, aufgeteilt nach Gruppen und Messzeitpunkten', subtitle='Je größer der Index, desto größer die Ermüdung innerhalb S1-S[abbruch]')
)

In [71]:
fatigue_index_stat = pg.mixed_anova(dv='fatigue_index',between='group', within='experiment', subject='id', data=peaks_largest, correction='auto', effsize='np2')
fatigue_index_stat

Source         SS  DF1  DF2         MS         F     p-unc       np2  \
0        group   0.172328    1   22   0.172328  0.021013  0.886062  0.000954   
1   experiment  11.936544    1   22  11.936544  0.963881  0.336885  0.041974   
2  Interaction  14.255529    1   22  14.255529  1.151140  0.294939  0.049723   

   eps  
0  NaN  
1  1.0  
2  NaN

# TMG Analyse

In [2]:
tmg_raw = pd.read_csv(r"C:\Users\bvenn\OneDrive\Desktop\Publikation\TMG Rohdaten Frame\tmg_raw_data.csv")
tmg_raw.rename(columns={'Unnamed: 0': 'index', 'value': 'displacement'}, inplace=True)

# Datatypes anpasssen
tmg_raw = tmg_raw.astype({'group': 'string', 'experiment': 'string', 'measurement': 'string'})

# Zeit für jede Messung hinzufügen
millisekenden_pro_datenpunkt = 1

# Gruppieren nach 'measurement' und Zeit in Millisekunden berechnen
# Gruppieren nach 'id', 'experiment' und 'measurement' und Zeit in Millisekunden normalisieren
tmg_raw['time_ms'] = tmg_raw.groupby(['id', 'experiment', 'measurement'])['index'].transform(lambda x: (x - x.min()) * millisekenden_pro_datenpunkt)

tmg_raw

index     id     group experiment measurement  displacement  time_ms
0            0  15073  beta_ala   posttest    supine_1      0.000000        0
1            1  15073  beta_ala   posttest    supine_1     -0.000108        1
2            2  15073  beta_ala   posttest    supine_1     -0.000600        2
3            3  15073  beta_ala   posttest    supine_1     -0.001181        3
4            4  15073  beta_ala   posttest    supine_1     -0.001808        4
...        ...    ...       ...        ...         ...           ...      ...
500995  501995  93672  beta_ala    pretest    supine_4      0.008989      995
500996  501996  93672  beta_ala    pretest    supine_4      0.004278      996
500997  501997  93672  beta_ala    pretest    supine_4      0.001684      997
500998  501998  93672  beta_ala    pretest    supine_4      0.000508      998
500999  501999  93672  beta_ala    pretest    supine_4      0.000103      999

[501000 rows x 7 columns]

In [10]:
example_data = tmg_raw.query('id == 25778 and experiment == "pretest" and measurement == "s4"')

# Schwellenwert für die Peaks
threshold = 0.04

# Wert des ersten Peaks der Kurve für dieses spezifische Beispiel
peaks, _ = find_peaks(example_data['displacement'].values, height=threshold)
dm = example_data['displacement'].iloc[peaks[0]] if len(peaks) > 0 else np.nan
time_of_dm = example_data['time_ms'].iloc[peaks[0]] if len(peaks) > 0 else np.nan

# Td berechnen: Schwellenwert für Td
threshold_td = 0.1 * dm
# Index von Td berechnen
index_td = example_data.index[example_data['displacement'] >= threshold_td].min()
# Zeit für Td berechnen
time_td = example_data.loc[index_td, 'time_ms'] if pd.notna(index_td) else np.nan

# Schwellenwert für Tc
threshold_tc = 0.9 * dm
# Index von Td berechnen
index_tc = example_data.index[example_data['displacement'] >= threshold_tc].min()
# Zeit für Td berechnen
time_tc = example_data.loc[index_tc, 'time_ms'] if pd.notna(index_tc) else np.nan


# Finde den ersten Wert, der 50% von dm entspricht
threshold_ts = 0.5 * dm
erster_wert_index = None

for i, wert in enumerate(example_data['displacement'].values):
    if wert >= threshold_ts:
        erster_wert_index = i
        break

# Iteriere weiter ab diesem Wert und finde den nächsten Wert, der 50% von dm entspricht
zweiter_wert_index = None

if erster_wert_index is not None:
    for y, wert in enumerate(example_data['displacement'].values[erster_wert_index + 1:]):
        if wert <= threshold_ts:
            zweiter_wert_index = erster_wert_index + 1 + y
            break

# Überprüfe, ob die Indizes gültig sind
if erster_wert_index is not None and zweiter_wert_index is not None:
    erster_wert_index += example_data.index[0]
    zweiter_wert_index += example_data.index[0]

# Berechne die Zeiten für ts_start und ts_end
time_ts_start = example_data.loc[erster_wert_index, 'time_ms'] if erster_wert_index is not None else np.nan
time_ts_end = example_data.loc[zweiter_wert_index, 'time_ms'] if zweiter_wert_index is not None else np.nan

# Finde den ersten Wert, der 90% von dm entspricht
threshold_tr = 0.9 * dm
erste_zahl_index = None

for i, zahl in enumerate(example_data['displacement'].values):
    if zahl >= threshold_tr:
        erste_zahl_index = i
        break

# Iteriere weiter ab diesem Wert und finde den nächsten Wert, der 90% von dm entspricht
zweite_zahl_index = None

if erste_zahl_index is not None:
    for y, zahl in enumerate(example_data['displacement'].values[erste_zahl_index + 1:]):
        if zahl <= threshold_tr:
            zweite_zahl_index = erste_zahl_index + 1 + y
            break

# Überprüfe, ob die Indizes gültig sind
if zweite_zahl_index is not None and zweite_zahl_index is not None:
    erste_zahl_index += example_data.index[0]
    zweite_zahl_index += example_data.index[0]
    
index_tr_end = example_data.index[example_data['time_ms'] == time_ts_end].min()
    
time_tr_start = example_data.loc[zweite_zahl_index, 'time_ms'] if zweite_zahl_index is not None else np.nan
time_tr_end = example_data.loc[index_tr_end, 'time_ms'] if index_tr_end is not None else np.nan

print("Dm:", dm, 'mm')
print("Td:", time_td, 'ms')
print("Tc:", time_tc, 'ms')
print("Ts:", time_ts_end - time_ts_start, 'ms')
print('Tr:', time_tr_end - time_tr_start, 'ms')
print('Vc:', (dm / (time_td + time_tc)), 'mm/ms')


# Deine ggplot-Grafik bleibt unverändert, füge einfach die Punkte für ts_start und ts_end hinzu
(
    ggplot(example_data, aes(x='time_ms', y='displacement'))
    + geom_line()
    + geom_point(data=example_data.iloc[[peaks[0]]], mapping=aes(x='time_ms', y='displacement'), color='red', size=3)
    + geom_point(aes(x='time_tc', y='displacement'), data=pd.DataFrame({'time_tc': [time_tc], 'displacement': [dm * 0.9]}), color='green', size=3)
    + geom_point(aes(x='time_td', y='displacement'), data=pd.DataFrame({'time_td': [time_td], 'displacement': [dm * 0.1]}), color='blue', size=3)
    + geom_point(aes(x='time_ts_start', y='displacement'), data=pd.DataFrame({'time_ts_start': [time_ts_start], 'displacement': [dm * 0.5]}), color='orange', size=3)
    + geom_point(aes(x='time_ts_end', y='displacement'), data=pd.DataFrame({'time_ts_end': [time_ts_end], 'displacement': [dm * 0.5]}), color='orange', size=3)
    + geom_point(aes(x='time_tr_start', y='displacement'), data=pd.DataFrame({'time_tr_start': [time_tr_start], 'displacement': [dm * 0.9]}), color='black', size=3)
    + geom_point(aes(x='time_tr_end', y='displacement'), data=pd.DataFrame({'time_tr_end': [time_tr_end], 'displacement': [dm * 0.9]}), color='black', size=3)
)


Dm: 0.415878055549873 mm
Td: 8 ms
Tc: 29 ms
Ts: 22 ms
Tr: 5 ms
Vc: 0.011239947447293865 mm/ms


# Automatisierung zur TMG Parameter-Berechnung

In [3]:
# Erstelle einen leeren DataFrame für die Ergebnisse
tmg_parameter = pd.DataFrame(columns=['id', 'group', 'experiment', 'measurement', 'Dm', 'Td', 'Tc', 'Ts', 'Tr', 'Vc'])

# Schwellenwert für die Peaks
threshold = 0.04

# Iteriere über jede einzigartige ID
for unique_id in tmg_raw['id'].unique():
    # Iteriere über jedes einzigartige Experiment (pretest und posttest)
    for unique_experiment in tmg_raw['experiment'].unique():
        # Iteriere über jedes einzigartige Messzeitpunkt
        for unique_measurement in tmg_raw['measurement'].unique():
            # Filtere die Daten für die aktuelle ID, das aktuelle Experiment und den aktuellen Messzeitpunkt
            subset = tmg_raw[(tmg_raw['id'] == unique_id) & 
                             (tmg_raw['experiment'] == unique_experiment) & 
                             (tmg_raw['measurement'] == unique_measurement)].copy()
            
            # Prüfe, ob Daten vorhanden sind, bevor die Parameterberechnung durchgeführt wird
            if not subset.empty:
                # Hier kannst du deine Parameterberechnung durchführen, ich verwende hier den Durchschnitt als Beispiel
                parameter_value = subset['displacement'].mean()
                
                # Hol dir die Gruppe des Probanden
                group = subset['group'].iloc[0]

                # Wert des ersten Peaks der Kurve für dieses spezifische Beispiel
                peaks, _ = find_peaks(subset['displacement'].values, height=threshold)
                dm = subset['displacement'].iloc[peaks[0]] if len(peaks) > 0 else np.nan

                # Td berechnen: Schwellenwert für Td
                threshold_td = 0.1 * dm
                # Index von Td berechnen
                index_td = subset.index[subset['displacement'] >= threshold_td].min()
                # Zeit für Td berechnen
                time_td = subset.loc[index_td, 'time_ms'] if pd.notna(index_td) and pd.notna(subset.loc[index_td, 'time_ms']) else np.nan

                # Schwellenwert für Tc
                threshold_tc = 0.9 * dm
                # Index von Td berechnen
                index_tc = subset.index[subset['displacement'] >= threshold_tc].min()
                # Zeit für Tc berechnen
                time_tc = subset.loc[index_tc, 'time_ms'] if pd.notna(index_tc) and pd.notna(subset.loc[index_tc, 'time_ms']) else np.nan

                # Finde den ersten Wert, der 50% von dm entspricht
                threshold_ts = 0.5 * dm
                erster_wert_index = None

                for i, wert in enumerate(subset['displacement'].values):
                    if wert >= threshold_ts:
                        erster_wert_index = i
                        break

                # Iteriere weiter ab diesem Wert und finde den nächsten Wert, der 50% von dm entspricht
                zweiter_wert_index = None

                if erster_wert_index is not None:
                    for y, wert in enumerate(subset['displacement'].values[erster_wert_index + 1:]):
                        if wert <= threshold_ts:
                            zweiter_wert_index = erster_wert_index + 1 + y
                            break

                # Überprüfe, ob die Indizes gültig sind
                if erster_wert_index is not None and zweiter_wert_index is not None:
                    erster_wert_index += subset.index[0]
                    zweiter_wert_index += subset.index[0]

                # Berechne die Zeiten für ts_start und ts_end
                time_ts_start = subset.loc[erster_wert_index, 'time_ms'] if pd.notna(erster_wert_index) and pd.notna(subset.loc[erster_wert_index, 'time_ms']) else np.nan
                time_ts_end = subset.loc[zweiter_wert_index, 'time_ms'] if pd.notna(zweiter_wert_index) and pd.notna(subset.loc[zweiter_wert_index, 'time_ms']) else np.nan

                # Finde den ersten Wert, der 90% von dm entspricht
                threshold_tr = 0.9 * dm
                erste_zahl_index = None

                for i, zahl in enumerate(subset['displacement'].values):
                    if zahl >= threshold_tr:
                        erste_zahl_index = i
                        break

                # Iteriere weiter ab diesem Wert und finde den nächsten Wert, der 90% von dm entspricht
                zweite_zahl_index = None

                if erste_zahl_index is not None:
                    for y, zahl in enumerate(subset['displacement'].values[erste_zahl_index + 1:]):
                        if zahl <= threshold_tr:
                            zweite_zahl_index = erste_zahl_index + 1 + y
                            break

                # Überprüfe, ob die Indizes gültig sind
                if zweite_zahl_index is not None and zweite_zahl_index is not None:
                    erste_zahl_index += subset.index[0]
                    zweite_zahl_index += subset.index[0]

                index_tr_end = subset.index[subset['time_ms'] == time_ts_end].min()

                # Berechne die Zeiten für tr_start und tr_end
                time_tr_start = subset.loc[zweite_zahl_index, 'time_ms'] if pd.notna(zweite_zahl_index) and pd.notna(subset.loc[zweite_zahl_index, 'time_ms']) else np.nan
                time_tr_end = subset.loc[index_tr_end, 'time_ms'] if pd.notna(index_tr_end) and pd.notna(subset.loc[index_tr_end, 'time_ms']) else np.nan

                tmg_parameter = pd.concat([tmg_parameter, pd.DataFrame({
                    'id': [unique_id],
                    'group':[group],
                    'experiment': [unique_experiment],
                    'measurement': [unique_measurement],
                    'Dm': [dm],
                    'Td': [time_td],
                    'Tc': [time_tc],
                    'Ts': [time_ts_end - time_ts_start],
                    'Tr': [time_tr_end - time_tr_start],
                    'Vc': [dm / (time_td + time_tc)]
                })], ignore_index=True)

# Drucke den DataFrame mit den berechneten Parametern
tmg_parameter


C:\Users\bvenn\AppData\Local\Temp\ipykernel_8444\2704293734.py:100: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  tmg_parameter = pd.concat([tmg_parameter, pd.DataFrame({


id     group experiment    measurement         Dm  Td  Tc   Ts   Tr  \
0    15073  beta_ala   posttest       supine_1   9.949456  31  56   77   46   
1    15073  beta_ala   posttest  before_warmup   2.989571  23  49  179  146   
2    15073  beta_ala   posttest   after_warmup   2.272929  20  43  194   36   
3    15073  beta_ala   posttest       after_pt   1.812468  19  40  167  138   
4    15073  beta_ala   posttest             s1   0.742931  16  33   26    7   
..     ...       ...        ...            ...        ...  ..  ..  ...  ...   
496  93672  beta_ala    pretest             s1   3.199221  22  41   28    8   
497  93672  beta_ala    pretest             s2   2.277724  24  43   30    9   
498  93672  beta_ala    pretest       supine_2   8.410425  25  51  137  103   
499  93672  beta_ala    pretest       supine_3  11.591811  25  54  144  111   
500  93672  beta_ala    pretest       supine_4  11.039604  26  55  177  142   

           Vc  
0    0.114362  
1    0.041522  
2    0.036078  
3    0.030720  
4    0.015162  
..        ...  
496  0.050781  
497  0.033996  
498  0.110663  
499  0.146732  
500  0.136291  

[501 rows x 10 columns]

In [4]:
tmg_parameter = tmg_parameter.astype({'group': 'category', 'experiment': 'category', 'measurement': 'category', 
                                       'Td': 'float64', 'Tc': 'float64', 'Dm': 'float64', 'Ts': 'float64', 'Tr': 'float64',
                                      'Vc': 'float64'})

tmg_parameter['experiment'] = pd.Categorical(tmg_parameter['experiment'], categories=['pretest', 'posttest'], ordered=True)

tmg_parameter.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 501 entries, 0 to 500
Data columns (total 10 columns):
 #   Column       Non-Null Count  Dtype   
---  ------       --------------  -----   
 0   id           501 non-null    object  
 1   group        501 non-null    category
 2   experiment   501 non-null    category
 3   measurement  501 non-null    category
 4   Dm           501 non-null    float64 
 5   Td           501 non-null    float64 
 6   Tc           501 non-null    float64 
 7   Ts           501 non-null    float64 
 8   Tr           501 non-null    float64 
 9   Vc           501 non-null    float64 
dtypes: category(3), float64(6), object(1)
memory usage: 29.9+ KB


In [5]:
# Pre- oder Posttest Info den Zeitpunkten hinzufügen
tmg_parameter['measurement'] = tmg_parameter.apply(lambda row: row['measurement']
                                                   + '_pre' if 'pretest' in row['experiment'] else row['measurement'], axis=1)
tmg_parameter['measurement'] = tmg_parameter.apply(lambda row: row['measurement']
                                                   + '_post' if 'posttest' in row['experiment'] else row['measurement'], axis=1)

In [6]:
tmg_parameter.head(-1)

id     group experiment         measurement         Dm    Td    Tc  \
0    15073  beta_ala   posttest       supine_1_post   9.949456  31.0  56.0   
1    15073  beta_ala   posttest  before_warmup_post   2.989571  23.0  49.0   
2    15073  beta_ala   posttest   after_warmup_post   2.272929  20.0  43.0   
3    15073  beta_ala   posttest       after_pt_post   1.812468  19.0  40.0   
4    15073  beta_ala   posttest             s1_post   0.742931  16.0  33.0   
..     ...       ...        ...                 ...        ...   ...   ...   
495  93672  beta_ala    pretest        after_pt_pre   5.181711  20.0  37.0   
496  93672  beta_ala    pretest              s1_pre   3.199221  22.0  41.0   
497  93672  beta_ala    pretest              s2_pre   2.277724  24.0  43.0   
498  93672  beta_ala    pretest        supine_2_pre   8.410425  25.0  51.0   
499  93672  beta_ala    pretest        supine_3_pre  11.591811  25.0  54.0   

        Ts     Tr        Vc  
0     77.0   46.0  0.114362  
1    179.0  146.0  0.041522  
2    194.0   36.0  0.036078  
3    167.0  138.0  0.030720  
4     26.0    7.0  0.015162  
..     ...    ...       ...  
495   27.0    9.0  0.090907  
496   28.0    8.0  0.050781  
497   30.0    9.0  0.033996  
498  137.0  103.0  0.110663  
499  144.0  111.0  0.146732  

[500 rows x 10 columns]

# TMG Parameter Auswertung: ACHTUNG nur der within subject factor time
# Td

In [19]:
# tmg_parameter.to_excel(r"C:\Users\bvenn\OneDrive\Desktop\Publikation\TMG Rohdaten Frame\tmg_parameter.xlsx")

In [26]:
(
    ggplot(tmg_parameter, aes(x='experiment', y='Td'))
    + geom_boxplot(aes(group='group', color='group'))
    + labs(title='Td Verteilung nach Zeitpunkt und Gruppe')
    + ylab('Td [ms]')
    + xlab('Messung')
)

In [27]:
# nach ausreißern schauen
tmg_parameter.query('Td < 10')

id     group experiment measurement        Dm   Td    Tc    Ts   Tr  \
64  25778  beta_ala    pretest      s4_pre  0.415878  8.0  29.0  22.0  5.0   

         Vc  
64  0.01124

In [28]:
# Daten zum Plotten vorbereiten: Pretest
tmg_pretest = tmg_parameter[tmg_parameter['experiment'] == 'pretest']

grouped_means = tmg_pretest.groupby(['group', 'measurement'], observed=False).agg({
    'Dm': 'mean', 'Td': 'mean', 'Tc': 'mean', 'Ts': 'mean', 'Tr': 'mean', 'Vc': 'mean'
}).reset_index()

grouped_std = tmg_pretest.groupby(['group', 'measurement'], observed=False).agg({
    'Dm': 'std', 'Td': 'std', 'Tc': 'std', 'Ts': 'std', 'Tr': 'std', 'Vc': 'std'
}).reset_index()

grouped_std.rename(columns={
    'Dm': 'Dm_std', 'Td': 'Td_std', 'Tc': 'Tc_std', 'Ts': 'Ts_std', 'Tr': 'Tr_std', 'Vc': 'Vc_std'
}, inplace=True)

# Füge die Standardabweichungen zu den gemittelten Werten hinzu
grouped_means = pd.concat([grouped_means, grouped_std.drop(['group', 'measurement'], axis=1)], axis=1)

# Daten zum Plotten vorbereiten: Posttest
tmg_posttest = tmg_parameter[tmg_parameter['experiment'] == 'posttest']

grouped_means_post = tmg_posttest.groupby(['group', 'measurement'], observed=False).agg({
    'Dm': 'mean', 'Td': 'mean', 'Tc': 'mean', 'Ts': 'mean', 'Tr': 'mean', 'Vc': 'mean'
}).reset_index()

grouped_std_post = tmg_posttest.groupby(['group', 'measurement'], observed=False).agg({
    'Dm': 'std', 'Td': 'std', 'Tc': 'std', 'Ts': 'std', 'Tr': 'std', 'Vc': 'std'
}).reset_index()

grouped_std_post.rename(columns={
    'Dm': 'Dm_std', 'Td': 'Td_std', 'Tc': 'Tc_std', 'Ts': 'Ts_std', 'Tr': 'Tr_std', 'Vc': 'Vc_std'
}, inplace=True)

# Füge die Standardabweichungen zu den gemittelten Werten hinzu
grouped_means_post = pd.concat([grouped_means_post, grouped_std_post.drop(['group', 'measurement'], axis=1)], axis=1)


In [29]:
grouped_means = grouped_means.astype({'group':'category', 'measurement':'category'})
grouped_means.head()

group        measurement        Dm         Td         Tc          Ts  \
0  beta_ala       after_pt_pre  3.533491  19.833333  37.166667   72.833333   
1  beta_ala   after_warmup_pre  3.386012  19.750000  37.666667  104.416667   
2  beta_ala  before_warmup_pre  4.400203  22.666667  44.250000  118.833333   
3  beta_ala             s1_pre  2.894438  21.000000  39.583333  104.250000   
4  beta_ala             s2_pre  2.571748  21.666667  40.333333   77.333333   

          Tr        Vc    Dm_std    Td_std    Tc_std      Ts_std      Tr_std  \
0  53.666667  0.060129  1.917201  1.466804  3.563281   75.710974   72.694045   
1  85.166667  0.057340  1.815753  1.712255  3.892495  110.513231  106.676089   
2  92.666667  0.064226  2.020803  2.015095  5.446016   85.870763   80.212596   
3  84.333333  0.045575  1.901133  2.449490  5.418123   75.228289   73.295583   
4  56.750000  0.039124  1.893910  2.774341  6.596602   70.587577   68.271017   

     Vc_std  
0  0.029988  
1  0.028555  
2  0.025625  
3  0.028137  
4  0.028092

In [30]:
# Spalte hinzufügen, die anzeigt, ob es sich um eine liegende oder sitzende Messung handelt

grouped_means['category'] = ''

# Benutzerdefinierte Funktion zum Festlegen der Werte in der 'category'-Spalte basierend auf 'measurement'
def set_category(row):
    if row['measurement'] in ['before_warmup_pre', 'after_warmup_pre', 'after_pt_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                               's5_pre', 's6_pre', 's7_pre', 's8_pre']:
        return 'Pre-Test: Sitting'
    else:
        return 'Pre-Test: Supine'

# Die Funktion auf jede Zeile der 'grouped_means'-Spalte anwenden
grouped_means['category'] = grouped_means.apply(set_category, axis=1)

# Ergebnisse anzeigen
grouped_means

group        measurement         Dm         Td         Tc          Ts  \
0   beta_ala       after_pt_pre   3.533491  19.833333  37.166667   72.833333   
1   beta_ala   after_warmup_pre   3.386012  19.750000  37.666667  104.416667   
2   beta_ala  before_warmup_pre   4.400203  22.666667  44.250000  118.833333   
3   beta_ala             s1_pre   2.894438  21.000000  39.583333  104.250000   
4   beta_ala             s2_pre   2.571748  21.666667  40.333333   77.333333   
5   beta_ala             s3_pre   2.203173  22.000000  41.333333   82.666667   
6   beta_ala             s4_pre   1.494490  18.400000  38.200000   67.400000   
7   beta_ala             s5_pre   1.766564  21.500000  43.000000  106.000000   
8   beta_ala             s6_pre   2.124360  24.000000  47.000000  160.000000   
9   beta_ala             s7_pre   3.147331  25.000000  47.000000  187.000000   
10  beta_ala             s8_pre   2.968527  24.000000  45.000000  170.000000   
11  beta_ala       supine_1_pre  10.390159  28.083333  55.250000   96.833333   
12  beta_ala       supine_2_pre   7.615728  27.250000  53.000000   80.250000   
13  beta_ala       supine_3_pre  10.081916  28.500000  57.416667   98.833333   
14  beta_ala       supine_4_pre   9.888181  27.916667  55.500000   94.416667   
15   placebo       after_pt_pre   2.812309  18.916667  35.666667   56.333333   
16   placebo   after_warmup_pre   3.037717  19.083333  37.250000   86.000000   
17   placebo  before_warmup_pre   3.829941  22.000000  43.583333  228.083333   
18   placebo             s1_pre   2.472695  21.000000  40.083333   76.166667   
19   placebo             s2_pre   2.039166  21.083333  41.916667   69.666667   
20   placebo             s3_pre   2.303125  22.142857  43.571429   76.285714   
21   placebo             s4_pre   1.769553  22.666667  41.000000   74.000000   
22   placebo             s5_pre   1.856557  21.500000  39.500000   93.000000   
23   placebo             s6_pre   1.914523  22.000000  40.000000   86.000000   
24   placebo             s7_pre   1.622107  19.000000  33.000000   21.000000   
25   placebo             s8_pre        NaN        NaN        NaN         NaN   
26   placebo       supine_1_pre   9.084233  26.666667  55.166667  115.833333   
27   placebo       supine_2_pre   6.935313  26.000000  54.083333   97.500000   
28   placebo       supine_3_pre   8.770231  27.250000  56.916667  108.166667   
29   placebo       supine_4_pre   8.792722  27.416667  55.416667  123.833333   

            Tr        Vc    Dm_std    Td_std     Tc_std      Ts_std  \
0    53.666667  0.060129  1.917201  1.466804   3.563281   75.710974   
1    85.166667  0.057340  1.815753  1.712255   3.892495  110.513231   
2    92.666667  0.064226  2.020803  2.015095   5.446016   85.870763   
3    84.333333  0.045575  1.901133  2.449490   5.418123   75.228289   
4    56.750000  0.039124  1.893910  2.774341   6.596602   70.587577   
5    58.222222  0.032551  1.469762  3.201562   6.344289   77.773710   
6    48.400000  0.023015  1.340598  6.877500   9.038805   70.358368   
7    82.000000  0.024877  2.037388  4.949747   7.071068  108.894444   
8   134.000000  0.029921       NaN       NaN        NaN         NaN   
9   161.000000  0.043713       NaN       NaN        NaN         NaN   
10  147.000000  0.043022       NaN       NaN        NaN         NaN   
11   63.166667  0.125299  2.699960  1.621354   4.555217   57.735814   
12   46.583333  0.095259  3.050658  2.734460   5.410428   30.721994   
13   62.750000  0.118265  2.492171  1.783765   4.907477   51.884195   
14   60.250000  0.119029  2.941237  1.564279   5.143398   52.633308   
15   29.416667  0.050662  0.972532  1.831955   4.030189   64.428020   
16   59.416667  0.053011  1.170326  1.781640   7.581377  105.293529   
17  179.666667  0.056699  1.417819  2.044949   6.986459  244.134634   
18   45.500000  0.040016  1.029785  2.662876   5.035480   69.331658   
19   44.916667  0.030314  1.399479  3.146667  10.013249   67.910815   
20   45.142857  0.032993  1.535326 

In [31]:
grouped_means_post['category'] = ''

# Benutzerdefinierte Funktion zum Festlegen der Werte in der 'category'-Spalte basierend auf 'measurement'
def set_category(row):
    if row['measurement'] in ['before_warmup_post', 'after_warmup_post','after_pt_post', 's1_post', 's2_post', 's3_post', 's4_post',
                               's5_post', 's6_post', 's7_post', 's8_post']:
        return 'Post-Test: Sitting'
    else:
        return 'Post-Test: Supine'

# Die Funktion auf jede Zeile der 'grouped_means'-Spalte anwenden
grouped_means_post['category'] = grouped_means_post.apply(set_category, axis=1)

# Ergebnisse anzeigen
grouped_means_post.head()

group         measurement        Dm         Td         Tc          Ts  \
0  beta_ala       after_pt_post  3.266084  19.750000  36.833333   65.666667   
1  beta_ala   after_warmup_post  3.410634  19.583333  37.000000   87.916667   
2  beta_ala  before_warmup_post  4.208709  21.833333  42.666667  107.083333   
3  beta_ala             s1_post  2.933943  20.833333  39.166667   66.416667   
4  beta_ala             s2_post  1.986138  21.363636  40.000000   72.727273   

          Tr        Vc    Dm_std    Td_std    Tc_std     Ts_std     Tr_std  \
0  46.750000  0.056031  2.180164  1.864745  3.613946  67.794252  63.738279   
1  57.833333  0.058786  2.132961  1.378954  4.177864  87.951907  77.954338   
2  83.333333  0.064373  2.045399  2.790677  5.015129  75.646857  69.678917   
3  47.000000  0.046393  1.929888  3.128559  5.621927  67.996602  64.457174   
4  53.454545  0.030944  1.192695  2.693426  5.495453  80.506013  76.955005   

     Vc_std            category  
0  0.034796  Post-Test: Sitting  
1  0.033816  Post-Test: Sitting  
2  0.029027  Post-Test: Sitting  
3  0.027012  Post-Test: Sitting  
4  0.016209  Post-Test: Sitting

In [32]:
# Mögliche Überschrift: Keine Interaktionseffekte vorhanden. 

(
    ggplot(grouped_means, aes(x='measurement', y='Td', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means['Td'] - grouped_means['Td_std'],
            ymax=grouped_means['Td'] + grouped_means['Td_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + facet_wrap(facets='category')
    + ylab('Td [ms]')
    + scale_x_discrete(limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 'after_pt_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                               's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre'],
                      labels=['Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                'After S5', 'After S6', 'After S7', 'After S8', 'Supine 2', 'Supine 3', 'Supine 4'])
    + theme(axis_title_x=element_blank())
)


In [33]:
(
    ggplot(grouped_means_post, aes(x='measurement', y='Td', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means_post['Td'] - grouped_means_post['Td_std'],
            ymax=grouped_means_post['Td'] + grouped_means_post['Td_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + facet_wrap(facets='category')
    + ylab('Td [ms]')
    + scale_x_discrete(
        limits=['supine_1_post', 'before_warmup_post', 'after_warmup_post', 'after_pt_post','s1_post', 's2_post', 's3_post',
                's4_post', 's5_post', 's6_post', 's7_post', 'supine_2_post', 'supine_3_post', 'supine_4_post'],
        labels=['Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                'After S5', 'After S6', 'After S7', 'Supine 2', 'Supine 3', 'Supine 4']
    )
    + theme(axis_title_x=element_blank())
)


## Tc interaktion

In [168]:
# Mögliche Überschrift: Keine Interaktionseffekte vorhanden. 

(
    ggplot(grouped_means, aes(x='measurement', y='Tc', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means['Tc'] - grouped_means['Tc_std'],
            ymax=grouped_means['Tc'] + grouped_means['Tc_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + facet_wrap(facets='category')
    + labs(title='Pre-Test: Tc Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='Punkte ohne Standartabweichung entsprechen Daten eines Probanden')
    + ylab('Tc [ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                               's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre'])
)


In [17]:
(
    ggplot(grouped_means_post, aes(x='measurement', y='Tc', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means_post['Tc'] - grouped_means_post['Tc_std'],
            ymax=grouped_means_post['Tc'] + grouped_means_post['Tc_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + facet_wrap(facets='category')
    + labs(title='Post-Test: Tc Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='Punkte ohne Standartabweichung entsprechen Daten eines Probanden')
    + ylab('Tc [ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1_post', 'before_warmup_post', 'after_warmup_post', 's1_post', 's2_post', 's3_post',
                               's4_post', 's5_post', 's6_post', 's7_post', 'supine_2_post', 'supine_3_post', 'supine_4_post'])
)


## Dm interaktion

In [18]:
# Mögliche Überschrift: Keine Interaktionseffekte vorhanden. 

(
    ggplot(grouped_means, aes(x='measurement', y='Dm', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means['Dm'] - grouped_means['Dm_std'],
            ymax=grouped_means['Dm'] + grouped_means['Dm_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + facet_wrap(facets='category')
    + labs(title='Pre-Test: Dm Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='Punkte ohne Standartabweichung entsprechen Daten eines Probanden')
    + ylab('Dm [mm]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                               's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre'])
)


In [19]:
(
    ggplot(grouped_means_post, aes(x='measurement', y='Dm', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means_post['Dm'] - grouped_means_post['Dm_std'],
            ymax=grouped_means_post['Dm'] + grouped_means_post['Dm_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + facet_wrap(facets='category')
    + labs(title='Post-Test: Dm Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='Punkte ohne Standartabweichung entsprechen Daten eines Probanden')
    + ylab('Dm [mm]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1_post', 'before_warmup_post', 'after_warmup_post', 's1_post', 's2_post', 's3_post',
                               's4_post', 's5_post', 's6_post', 's7_post', 'supine_2_post', 'supine_3_post', 'supine_4_post'])
)


## Ts interaktion

In [20]:
# Mögliche Überschrift: Keine Interaktionseffekte vorhanden. 

(
    ggplot(grouped_means, aes(x='measurement', y='Ts', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means['Ts'] - grouped_means['Ts_std'],
            ymax=grouped_means['Ts'] + grouped_means['Ts_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + facet_wrap(facets='category')
    + labs(title='Pre-Test: Ts Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='Punkte ohne Standartabweichung entsprechen Daten eines Probanden')
    + ylab('Ts [ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                               's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre'])
)


In [21]:
(
    ggplot(grouped_means_post, aes(x='measurement', y='Ts', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means_post['Ts'] - grouped_means_post['Ts_std'],
            ymax=grouped_means_post['Ts'] + grouped_means_post['Ts_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + facet_wrap(facets='category')
    + labs(title='Post-Test: Ts Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='Punkte ohne Standartabweichung entsprechen Daten eines Probanden')
    + ylab('Ts [ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1_post', 'before_warmup_post', 'after_warmup_post', 's1_post', 's2_post', 's3_post',
                               's4_post', 's5_post', 's6_post', 's7_post', 'supine_2_post', 'supine_3_post', 'supine_4_post'])
)


## Tr interaction

In [22]:
# Mögliche Überschrift: Keine Interaktionseffekte vorhanden. 

(
    ggplot(grouped_means, aes(x='measurement', y='Tr', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means['Tr'] - grouped_means['Tr_std'],
            ymax=grouped_means['Tr'] + grouped_means['Tr_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + facet_wrap(facets='category')
    + labs(title='Pre-Test: Tr Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='Punkte ohne Standartabweichung entsprechen Daten eines Probanden')
    + ylab('Tr [ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                               's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre'])
)


In [23]:
(
    ggplot(grouped_means_post, aes(x='measurement', y='Tr', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means_post['Tr'] - grouped_means_post['Tr_std'],
            ymax=grouped_means_post['Tr'] + grouped_means_post['Tr_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + facet_wrap(facets='category')
    + labs(title='Post-Test: Tr Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='Punkte ohne Standartabweichung entsprechen Daten eines Probanden')
    + ylab('Tr [ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1_post', 'before_warmup_post', 'after_warmup_post', 's1_post', 's2_post', 's3_post',
                               's4_post', 's5_post', 's6_post', 's7_post', 'supine_2_post', 'supine_3_post', 'supine_4_post'])
)


## Vc interaction

In [24]:
# Mögliche Überschrift: Keine Interaktionseffekte vorhanden. 

(
    ggplot(grouped_means, aes(x='measurement', y='Vc', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means['Vc'] - grouped_means['Vc_std'],
            ymax=grouped_means['Vc'] + grouped_means['Vc_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + facet_wrap(facets='category')
    + labs(title='Pre-Test: Vc Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='Punkte ohne Standartabweichung entsprechen Daten eines Probanden')
    + ylab('Vc [mm/ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                               's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre'])
)


In [25]:
(
    ggplot(grouped_means_post, aes(x='measurement', y='Vc', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means_post['Vc'] - grouped_means_post['Vc_std'],
            ymax=grouped_means_post['Vc'] + grouped_means_post['Vc_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + facet_wrap(facets='category')
    + labs(title='Post-Test: Vc Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='Punkte ohne Standartabweichung entsprechen Daten eines Probanden')
    + ylab('Vc [mm/ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1_post', 'before_warmup_post', 'after_warmup_post', 's1_post', 's2_post', 's3_post',
                               's4_post', 's5_post', 's6_post', 's7_post', 'supine_2_post', 'supine_3_post', 'supine_4_post'])
)


### Stat Auswertung für liegende Parameter

In [37]:
# frame für stat Auswertung: supine_tmg_parameter
desired_measurements = ['supine_1_pre', 'supine_2_pre', 'supine_3_pre', 'supine_4_pre', 'supine_1_post', 'supine_2_post', 'supine_3_post', 'supine_4_post']

supine_tmg_parameter = tmg_parameter[tmg_parameter['measurement'].isin(desired_measurements)]
supine_tmg_parameter.head()

id     group experiment    measurement        Dm    Td    Tc     Ts  \
0   15073  beta_ala   posttest  supine_1_post  9.949456  31.0  56.0   77.0   
10  15073  beta_ala   posttest  supine_2_post  6.965459  28.0  57.0   86.0   
11  15073  beta_ala   posttest  supine_3_post  8.982938  30.0  57.0  140.0   
12  15073  beta_ala   posttest  supine_4_post  9.926545  30.0  56.0  124.0   
13  15073  beta_ala    pretest   supine_1_pre  9.726150  31.0  57.0  106.0   

       Tr        Vc  
0    46.0  0.114362  
10   46.0  0.081947  
11  104.0  0.103252  
12   88.0  0.115425  
13   72.0  0.110524

In [125]:
td_stat_l = pg.mixed_anova(dv='Td',between='group', within='measurement', subject='id',
                         data=supine_tmg_parameter,
                         correction='auto', effsize='np2')
td_stat_l

Source         SS  DF1  DF2         MS         F     p-unc  p-GG-corr  \
0        group  78.796875    1   22  78.796875  4.380024  0.048112        NaN   
1  measurement  47.411458    7  154   6.773065  3.414595  0.002021   0.010761   
2  Interaction   8.744792    7  154   1.249256  0.629804  0.730716        NaN   

        np2       eps sphericity   W-spher   p-spher  
0  0.166036       NaN        NaN       NaN       NaN  
1  0.134356  0.575403      False  0.055675  0.000412  
2  0.027831       NaN        NaN       NaN       NaN

In [132]:
# Signifikante Gruppenunterschiede?

group_diff = pg.anova(data=supine_tmg_parameter, dv='Td', between='group', detailed=True, effsize='np2')
group_diff

Source          SS   DF         MS          F     p-unc       np2
0   group   78.796875    1  78.796875  19.766679  0.000015  0.094232
1  Within  757.406250  190   3.986349        NaN       NaN       NaN

In [134]:
posthoc_supine_measurement = pg.pairwise_tests(data=supine_tmg_parameter, dv='Td',
                                                           between='group', subject='id', parametric=True, padjust='bonf',
                                                           effsize='cohen', correction='auto')
posthoc_supine_measurement

Contrast         A        B  Paired  Parametric         T    dof  \
0    group  beta_ala  placebo   False        True  4.445973  190.0   

  alternative     p-unc      BF10     cohen  
0   two-sided  0.000015  1155.406  0.641721

In [130]:
# Keine Interaktioneffekte, also rm_anova zum checken ob es untschiede in den verschiedenen Messzeitpunkten gibt

time_diff = pg.rm_anova(data=supine_tmg_parameter, dv='Td', within='measurement', subject='id', detailed=True, effsize='np2',
                       correction='auto')
time_diff

Source          SS   DF        MS         F     p-unc  p-GG-corr  \
0  measurement   47.411458    7  6.773065  3.470454  0.001724   0.010761   
1        Error  314.213542  161  1.951637       NaN       NaN        NaN   

        np2       eps sphericity   W-spher   p-spher  
0  0.131107  0.575403      False  0.055675  0.000412  
1       NaN       NaN        NaN       NaN       NaN

In [46]:
posthoc_supine_measurement = pg.pairwise_tests(data=supine_tmg_parameter, dv='Td',
                                                           within='measurement', subject='id', parametric=True, padjust='bonf',
                                                           effsize='cohen', correction='auto')
def color_cells(value):
    color = 'background-color: yellow' if value < 0.05 else ''
    return color

# Wende die Funktion auf den relevanten Bereich des DataFrame an
posthoc_supine_measurement = posthoc_supine_measurement.style.applymap(color_cells, subset=pd.IndexSlice[:, ['p-corr']])

# Zeige das gestylte DataFrame an
posthoc_supine_measurement

C:\Users\bvenn\AppData\Local\Temp\ipykernel_2020\5862885.py:9: FutureWarning: Styler.applymap has been deprecated. Use Styler.map instead.
  posthoc_supine_measurement = posthoc_supine_measurement.style.applymap(color_cells, subset=pd.IndexSlice[:, ['p-corr']])


In [47]:
# frame der Mittelwerte und Stds der einzelnen Messzeitpunkte enthält

means_supine = supine_tmg_parameter.groupby('measurement').agg({
    'Dm': 'mean', 'Td': 'mean', 'Tc': 'mean', 'Ts': 'mean', 'Tr': 'mean', 'Vc': 'mean'
}).reset_index()

means_supine.rename(columns={
    'Dm': 'Dm_mean', 'Td': 'Td_mean', 'Tc': 'Tc_mean', 'Ts': 'Ts_mean', 'Tr': 'Tr_mean', 'Vc': 'Vc_mean'
}, inplace=True)

std_supine = supine_tmg_parameter.groupby('measurement').agg({
    'Dm': 'std', 'Td': 'std', 'Tc': 'std', 'Ts': 'std', 'Tr': 'std', 'Vc': 'std'
}).reset_index()

std_supine.rename(columns={
    'Dm': 'Dm_std', 'Td': 'Td_std', 'Tc': 'Tc_std', 'Ts': 'Ts_std', 'Tr': 'Tr_std', 'Vc': 'Vc_std'
}, inplace=True)

means_supine = pd.concat([means_supine, std_supine], axis=1)

means_supine['experiment'] = ['posttest', 'pretest', 'posttest', 'pretest', 'posttest', 'pretest', 'posttest', 'pretest']

means_supine

measurement   Dm_mean    Td_mean    Tc_mean     Ts_mean    Tr_mean  \
0  supine_1_post  9.431582  27.333333  53.708333   99.750000  66.708333   
1   supine_1_pre  9.737196  27.375000  55.208333  106.333333  70.041667   
2  supine_2_post  7.594565  26.500000  53.416667   90.458333  53.541667   
3   supine_2_pre  7.275520  26.625000  53.541667   88.875000  52.375000   
4  supine_3_post  9.001847  27.875000  56.750000   96.791667  58.583333   
5   supine_3_pre  9.426073  27.875000  57.166667  103.500000  62.250000   
6  supine_4_post  9.321070  27.625000  54.916667   99.833333  64.333333   
7   supine_4_pre  9.340451  27.666667  55.458333  109.125000  72.791667   

    Vc_mean    measurement    Dm_std    Td_std    Tc_std     Ts_std  \
0  0.116699  supine_1_post  2.495500  1.970801  4.534689  53.175877   
1  0.118045   supine_1_pre  2.864526  1.636871  3.833255  50.285850   
2  0.095172  supine_2_post  2.704275  2.874173  5.777894  36.220315   
3  0.090844   supine_2_pre  2.634284  2.203012  4.333682  33.057674   
4  0.107105  supine_3_post  2.273707  2.290102  4.627423  41.537808   
5  0.111119   supine_3_pre  2.507372  1.752328  4.546061  46.411206   
6  0.113291  supine_4_post  2.471751  1.555146  4.689643  45.065813   
7  0.112769   supine_4_pre  2.517078  1.970801  4.872096  55.035414   

      Tr_std    Vc_std experiment  
0  52.880077  0.029970   posttest  
1  46.765352  0.034477    pretest  
2  33.942380  0.034478   posttest  
3  31.658246  0.032614    pretest  
4  38.812724  0.028348   posttest  
5  43.526354  0.030517    pretest  
6  41.937497  0.030257   posttest  
7  53.034836  0.030861    pretest

In [48]:
hight_y1 = 31
start_x1 = 5
end_x1 = 6

(
    ggplot(means_supine, aes(x='measurement', y='Td_mean', color='experiment')) +
    geom_point() +
    geom_line() +
    geom_errorbar(
        aes(ymin=means_supine['Td_mean'] - means_supine['Td_std'],
            ymax=means_supine['Td_mean'] + means_supine['Td_std'],
            fill='group'),
        position=position_dodge(),
        linetype="blank",
        width=0.2
    ) +
    geom_segment(
        x=start_x1, y=hight_y1, xend=end_x1, yend=hight_y1,
        linetype='solid', color='black'
    ) +
    geom_text(
        x=end_x1, y=hight_y1, label="|", color='black', size=8
    ) +
     geom_text(
        x=start_x1, y=hight_y1, label="|", color='black', size=8
    ) +
    geom_text(
        x=5.5, y=31.5, label="*", color='black', size=12
    ) +
    labs(title='Td: Unterschiede liegender TMG Messungen \nzwischen den verschiedenen Messzeitpunkten') +
    ylab('Td [ms]') +
    xlab('Messung') +
    scale_x_discrete(limits=['supine_1_pre', 'supine_2_pre', 'supine_3_pre', 'supine_4_pre',
                             'supine_1_post','supine_2_post', 'supine_3_post', 'supine_4_post'])
)

## Tc supine stat

In [49]:
tc_stat_l = pg.mixed_anova(dv='Tc',between='group', within='measurement', subject='id',
                         data=supine_tmg_parameter,
                         correction='auto', effsize='np2')
tc_stat_l

Source          SS  DF1  DF2         MS         F     p-unc  \
0        group    1.333333    1   22   1.333333  0.011479  0.915648   
1  measurement  343.583333    7  154  49.083333  5.286514  0.000020   
2  Interaction   43.833333    7  154   6.261905  0.674438  0.693471   

   p-GG-corr       np2      eps sphericity   W-spher   p-spher  
0        NaN  0.000522      NaN        NaN       NaN       NaN  
1   0.000543  0.193741  0.58854      False  0.085221  0.004649  
2        NaN  0.029744      NaN        NaN       NaN       NaN

Source          SS  DF1  DF2         MS         F     p-unc  \
0        group    1.333333    1   22   1.333333  0.011479  0.915648   
1  measurement  343.583333    7  154  49.083333  5.286514  0.000020   
2  Interaction   43.833333    7  154   6.261905  0.674438  0.693471   

   p-GG-corr       np2      eps sphericity   W-spher   p-spher  
0        NaN  0.000522      NaN        NaN       NaN       NaN  
1   0.000543  0.193741  0.58854      False  0.085221  0.004649  
2        NaN  0.029744      NaN        NaN       NaN       NaN

In [50]:
# keine Interaktion. rm anova über Zeitpunkte
time_diff_tc = pg.rm_anova(data=supine_tmg_parameter, dv='Tc', within='measurement', subject='id', detailed=True, effsize='np2')
time_diff_tc

Source           SS   DF         MS         F     p-unc  p-GG-corr  \
0  measurement   343.583333    7  49.083333  5.362418  0.000015   0.000543   
1        Error  1473.666667  161   9.153209       NaN       NaN        NaN   

        np2      eps sphericity   W-spher   p-spher  
0  0.189068  0.58854      False  0.085221  0.004649  
1       NaN      NaN        NaN       NaN       NaN

In [51]:
posthoc_supine_tc = pg.pairwise_tests(data=supine_tmg_parameter, dv='Tc',
                                                           within='measurement', subject='id', parametric=True, padjust='bonf',
                                                           effsize='cohen', correction='auto')
posthoc_supine_tc = posthoc_supine_tc.style.applymap(color_cells, subset=pd.IndexSlice[:, ['p-corr']])

# Zeige das gestylte DataFrame an
posthoc_supine_tc

C:\Users\bvenn\AppData\Local\Temp\ipykernel_2020\2406880991.py:4: FutureWarning: Styler.applymap has been deprecated. Use Styler.map instead.
  posthoc_supine_tc = posthoc_supine_tc.style.applymap(color_cells, subset=pd.IndexSlice[:, ['p-corr']])


In [52]:
hight_y1 = 65
start_x1 = 4
end_x1 = 6

hight_y2 = 62.5
start_x2 = 5
end_x2 = 6

hight_y3 = 65
start_x3 = 1
end_x3 = 2

(
    ggplot(means_supine, aes(x='measurement', y='Tc_mean', color='experiment')) +
    geom_point() +
    geom_line() +
    geom_errorbar(
        aes(ymin=means_supine['Tc_mean'] - means_supine['Tc_std'],
            ymax=means_supine['Tc_mean'] + means_supine['Tc_std'],
            fill='group'),
        position=position_dodge(),
        linetype="blank",
        width=0.2
    ) +
    geom_segment(
        x=start_x1, y=hight_y1, xend=end_x1, yend=hight_y1,
        linetype='solid', color='black'
    ) +
    geom_text(
        x=end_x1, y=hight_y1, label="|", color='black', size=8
    ) +
     geom_text(
        x=start_x1, y=hight_y1, label="|", color='black', size=8
    ) +
    geom_text(
        x=5, y=65.5, label="*", color='black', size=12
    ) + # start neuer balken
        geom_segment(
        x=start_x2, y=hight_y2, xend=end_x2, yend=hight_y2,
        linetype='solid', color='black'
    ) +
    geom_text(
        x=end_x2, y=hight_y2, label="|", color='black', size=8
    ) +
     geom_text(
        x=start_x2, y=hight_y2, label="|", color='black', size=8
    ) +
    geom_text(
        x=5.5, y=63, label="*", color='black', size=12
    ) + # start balken 3
            geom_segment(
        x=start_x3, y=hight_y3, xend=end_x3, yend=hight_y3,
        linetype='solid', color='black'
    ) +
    geom_text(
        x=end_x3, y=hight_y3, label="|", color='black', size=8
    ) +
     geom_text(
        x=start_x3, y=hight_y3, label="|", color='black', size=8
    ) +
    geom_text(
        x=1.5, y=65.5, label="*", color='black', size=12
    ) +
    labs(title='Tc: Unterschiede liegender TMG Messungen \nzwischen den verschiedenen Messzeitpunkten') +
    ylab('Tc [ms]') +
    xlab('Messung') +
    scale_x_discrete(limits=['supine_1_pre', 'supine_2_pre', 'supine_3_pre', 'supine_4_pre',
                             'supine_1_post','supine_2_post', 'supine_3_post', 'supine_4_post'])
)

## Dm stat supine

In [53]:
dm_stat_l = pg.mixed_anova(dv='Dm',between='group', within='measurement', subject='id',
                         data=supine_tmg_parameter,
                         correction='auto', effsize='np2')
dm_stat_l.round(3)

Source       SS  DF1  DF2      MS       F  p-unc  p-GG-corr    np2  \
0        group   50.975    1   22  50.975   1.180  0.289        NaN  0.051   
1  measurement  143.624    7  154  20.518  15.411  0.000        0.0  0.412   
2  Interaction    2.993    7  154   0.428   0.321  0.944        NaN  0.014   

     eps sphericity  W-spher  p-spher  
0    NaN        NaN      NaN      NaN  
1  0.455      False     0.02      0.0  
2    NaN        NaN      NaN      NaN

In [54]:
# keine Interaktion. rm anova über Zeitpunkte
time_diff_dm = pg.rm_anova(data=supine_tmg_parameter, dv='Dm', within='measurement', subject='id', detailed=True, effsize='np2')
time_diff_dm

Source          SS   DF         MS          F         p-unc  \
0  measurement  143.624479    7  20.517783  15.879328  9.122491e-16   
1        Error  208.029148  161   1.292107        NaN           NaN   

      p-GG-corr       np2      eps sphericity  W-spher       p-spher  
0  2.543826e-08  0.408426  0.45532      False   0.0197  4.595632e-07  
1           NaN       NaN      NaN        NaN      NaN           NaN

In [55]:
posthoc_supine_dm = pg.pairwise_tests(data=supine_tmg_parameter, dv='Dm',
                                                           within='measurement', subject='id', parametric=True, padjust='bonf',
                                                           effsize='cohen', correction='auto')
posthoc_supine_dm = posthoc_supine_dm.style.applymap(color_cells, subset=pd.IndexSlice[:, ['p-corr']])

posthoc_supine_dm

C:\Users\bvenn\AppData\Local\Temp\ipykernel_2020\2915635409.py:4: FutureWarning: Styler.applymap has been deprecated. Use Styler.map instead.
  posthoc_supine_dm = posthoc_supine_dm.style.applymap(color_cells, subset=pd.IndexSlice[:, ['p-corr']])


In [56]:
hight_y1 = 13.5
start_x1 = 4
end_x1 = 4.9

hight_y2 = 13.5
start_x2 = 0
end_x2 = 1

hight_y3 = 13.5
start_x3 = 5.1
end_x3 = 6

hight_y4 = 14.75
start_x4 = 5.1
end_x4 = 7

hight_y5 = 13.5
start_x5 = 1.1
end_x5 = 2

hight_y6 = 14.75
start_x6 = 1.1
end_x6 = 3

(
    ggplot(means_supine, aes(x='measurement', y='Dm_mean', color='experiment')) +
    geom_point() +
    geom_line() +
    geom_errorbar(
        aes(ymin=means_supine['Dm_mean'] - means_supine['Dm_std'],
            ymax=means_supine['Dm_mean'] + means_supine['Dm_std'],
            fill='group'),
        position=position_dodge(),
        linetype="blank",
        width=0.2
    ) +
    geom_segment(
        x=start_x1, y=hight_y1, xend=end_x1, yend=hight_y1,
        linetype='solid', color='black'
    ) +
    geom_text(
        x=end_x1, y=hight_y1, label="|", color='black', size=8
    ) +
     geom_text(
        x=start_x1, y=hight_y1, label="|", color='black', size=8
    ) +
    geom_text(
        x=4.5, y=14, label="*", color='black', size=12
    ) + # start neuer balken
        geom_segment(
        x=start_x2, y=hight_y2, xend=end_x2, yend=hight_y2,
        linetype='solid', color='black'
    ) +
    geom_text(
        x=end_x2, y=hight_y2, label="|", color='black', size=8
    ) +
     geom_text(
        x=start_x2, y=hight_y2, label="|", color='black', size=8
    ) +
    geom_text(
        x=0.5, y=14, label="*", color='black', size=12
    ) + # start balken 3
    geom_segment(
        x=start_x3, y=hight_y3, xend=end_x3, yend=hight_y3,
        linetype='solid', color='black'
    ) +
    geom_text(
        x=end_x3, y=hight_y3, label="|", color='black', size=8
    ) +
     geom_text(
        x=start_x3, y=hight_y3, label="|", color='black', size=8
    ) +
    geom_text(
        x=5.5, y=14, label="*", color='black', size=12
    ) + # start balken 4
    geom_segment(
        x=start_x4, y=hight_y4, xend=end_x4, yend=hight_y4,
        linetype='solid', color='black'
    ) +
    geom_text(
        x=end_x4, y=hight_y4, label="|", color='black', size=8
    ) +
     geom_text(
        x=start_x4, y=hight_y4, label="|", color='black', size=8
    ) +
    geom_text(
        x=6, y=15.25, label="*", color='black', size=12
    ) + # start balken 5
    geom_segment(
        x=start_x5, y=hight_y5, xend=end_x5, yend=hight_y5,
        linetype='solid', color='black'
    ) +
    geom_text(
        x=end_x5, y=hight_y5, label="|", color='black', size=8
    ) +
     geom_text(
        x=start_x5, y=hight_y5, label="|", color='black', size=8
    ) +
    geom_text(
        x=1.5, y=14, label="*", color='black', size=12
    ) + # start balken 6
    geom_segment(
        x=start_x6, y=hight_y6, xend=end_x6, yend=hight_y6,
        linetype='solid', color='black'
    ) +
    geom_text(
        x=end_x6, y=hight_y6, label="|", color='black', size=8
    ) +
     geom_text(
        x=start_x6, y=hight_y6, label="|", color='black', size=8
    ) +
    geom_text(
        x=2, y=15.25, label="*", color='black', size=12
    ) +
    labs(title='Dm: Unterschiede liegender TMG Messungen \nzwischen den verschiedenen Messzeitpunkten') +
    ylab('Dm [mm]') +
    xlab('Messung') +
    scale_x_discrete(limits=['supine_1_pre', 'supine_2_pre', 'supine_3_pre', 'supine_4_pre',
                             'supine_1_post','supine_2_post', 'supine_3_post', 'supine_4_post'])
)

## Ts stat supine

In [57]:
ts_stat_l = pg.mixed_anova(dv='Ts',between='group', within='measurement', subject='id',
                         data=supine_tmg_parameter,
                         correction='auto', effsize='np2')
ts_stat_l.round(3)

Source        SS  DF1  DF2        MS      F  p-unc  p-GG-corr    np2  \
0        group  5590.083    1   22  5590.083  0.477  0.497        NaN  0.021   
1  measurement  8574.333    7  154  1224.905  1.664  0.122      0.168  0.070   
2  Interaction  7444.083    7  154  1063.440  1.444  0.191        NaN  0.062   

    eps sphericity  W-spher  p-spher  
0   NaN        NaN      NaN      NaN  
1  0.61      False    0.057      0.0  
2   NaN        NaN      NaN      NaN

In [58]:

(
    ggplot(means_supine, aes(x='measurement', y='Ts_mean', color='experiment')) +
    geom_point() +
    geom_line() +
    geom_errorbar(
        aes(ymin=means_supine['Ts_mean'] - means_supine['Ts_std'],
            ymax=means_supine['Ts_mean'] + means_supine['Ts_std'],
            fill='group'),
        position=position_dodge(),
        linetype="blank",
        width=0.2
    ) +
    labs(title='Ts: Unterschiede liegender TMG Messungen \nzwischen den verschiedenen Messzeitpunkten') +
    ylab('Ts [ms]') +
    xlab('Messung') +
    scale_x_discrete(limits=['supine_1_pre', 'supine_2_pre', 'supine_3_pre', 'supine_4_pre',
                             'supine_1_post','supine_2_post', 'supine_3_post', 'supine_4_post'])
)

## Tr stat supine

In [59]:
tr_stat_l = pg.mixed_anova(dv='Tr',between='group', within='measurement', subject='id',
                         data=supine_tmg_parameter,
                         correction='auto', effsize='np2')
tr_stat_l.round(3)

Source        SS  DF1  DF2        MS      F  p-unc  p-GG-corr    np2  \
0        group  1868.755    1   22  1868.755  0.184  0.672        NaN  0.008   
1  measurement  9167.703    7  154  1309.672  1.741  0.103      0.142  0.073   
2  Interaction  6758.786    7  154   965.541  1.284  0.262        NaN  0.055   

     eps sphericity  W-spher  p-spher  
0    NaN        NaN      NaN      NaN  
1  0.653      False    0.083    0.004  
2    NaN        NaN      NaN      NaN

In [60]:

(
    ggplot(means_supine, aes(x='measurement', y='Tr_mean', color='experiment')) +
    geom_point() +
    geom_line() +
    geom_errorbar(
        aes(ymin=means_supine['Tr_mean'] - means_supine['Tr_std'],
            ymax=means_supine['Tr_mean'] + means_supine['Tr_std'],
            fill='group'),
        position=position_dodge(),
        linetype="blank",
        width=0.2
    ) +
    labs(title='Tr: Unterschiede liegender TMG Messungen \nzwischen den verschiedenen Messzeitpunkten') +
    ylab('Tr [ms]') +
    xlab('Messung') +
    scale_x_discrete(limits=['supine_1_pre', 'supine_2_pre', 'supine_3_pre', 'supine_4_pre',
                             'supine_1_post','supine_2_post', 'supine_3_post', 'supine_4_post'])
)

## Vc stat supine

In [61]:
supine_tmg_parameter['Vc']

0      0.114362
10     0.081947
11     0.103252
12     0.115425
13     0.110524
         ...   
491    0.140047
492    0.142133
498    0.110663
499    0.146732
500    0.136291
Name: Vc, Length: 192, dtype: float64

In [62]:

vc_stat_l = pg.mixed_anova(dv='Vc',between='group', within='measurement', subject='id',
                         data=supine_tmg_parameter,
                         correction='auto', effsize='np2')
vc_stat_l.round(3)

C:\Users\bvenn\AppData\Roaming\Python\Python311\site-packages\pingouin\distribution.py:1006: RuntimeWarning: divide by zero encountered in scalar divide
  W = np.product(eig) / (eig.sum() / d) ** d


Source     SS  DF1  DF2     MS       F  p-unc    np2    eps
0        group  0.006    1   22  0.006   0.988  0.331  0.043    NaN
1  measurement  0.017    7  154  0.002  10.090  0.000  0.314  0.469
2  Interaction  0.001    7  154  0.000   0.307  0.950  0.014    NaN

In [63]:
# keine Interaktion. rm anova über Zeitpunkte
time_diff_vc = pg.rm_anova(data=supine_tmg_parameter, dv='Vc', within='measurement', subject='id', detailed=True, effsize='np2', correction='auto')
time_diff_vc

C:\Users\bvenn\AppData\Roaming\Python\Python311\site-packages\pingouin\distribution.py:1006: RuntimeWarning: divide by zero encountered in scalar divide
  W = np.product(eig) / (eig.sum() / d) ** d


Source        SS   DF        MS          F         p-unc       np2  \
0  measurement  0.016718    7  0.002388  10.403388  9.621926e-11  0.311447   
1        Error  0.036959  161  0.000230        NaN           NaN       NaN   

        eps  
0  0.469022  
1       NaN

In [64]:
posthoc_supine_vc = pg.pairwise_tests(data=supine_tmg_parameter, dv='Vc',
                                                           within='measurement', subject='id', parametric=True, padjust='bonf',
                                                           effsize='cohen', correction='auto')
posthoc_supine_vc = posthoc_supine_vc.style.applymap(color_cells, subset=pd.IndexSlice[:, ['p-corr']])

posthoc_supine_vc

C:\Users\bvenn\AppData\Local\Temp\ipykernel_2020\2269520366.py:4: FutureWarning: Styler.applymap has been deprecated. Use Styler.map instead.
  posthoc_supine_vc = posthoc_supine_vc.style.applymap(color_cells, subset=pd.IndexSlice[:, ['p-corr']])


In [65]:

hight_y1 = 0.16
start_x1 = 4
end_x1 = 4.9

hight_y2 = 0.16
start_x2 = 0
end_x2 = 0.9

hight_y3 = 0.16
start_x3 = 5.1
end_x3 = 7

hight_y4 = 0.16
start_x4 = 1.1
end_x4 = 2

hight_y5 = 0.18
start_x5 = 1.1
end_x5 = 3


(
    ggplot(means_supine, aes(x='measurement', y='Vc_mean', color='experiment')) +
    geom_point() +
    geom_line() +
    geom_errorbar(
        aes(ymin=means_supine['Vc_mean'] - means_supine['Vc_std'],
            ymax=means_supine['Vc_mean'] + means_supine['Vc_std'],
            fill='group'),
        position=position_dodge(),
        linetype="blank",
        width=0.2
    ) +
    geom_segment(
        x=start_x1, y=hight_y1, xend=end_x1, yend=hight_y1,
        linetype='solid', color='black'
    ) +
    geom_text(
        x=end_x1, y=hight_y1, label="|", color='black', size=8
    ) +
     geom_text(
        x=start_x1, y=hight_y1, label="|", color='black', size=8
    ) +
    geom_text(
        x=4.5, y=0.17, label="*", color='black', size=12
    ) + # start neuer balken
        geom_segment(
        x=start_x2, y=hight_y2, xend=end_x2, yend=hight_y2,
        linetype='solid', color='black'
    ) +
    geom_text(
        x=end_x2, y=hight_y2, label="|", color='black', size=8
    ) +
     geom_text(
        x=start_x2, y=hight_y2, label="|", color='black', size=8
    ) +
    geom_text(
        x=0.5, y=0.17, label="*", color='black', size=12
    ) + # start balken 3
    geom_segment(
        x=start_x3, y=hight_y3, xend=end_x3, yend=hight_y3,
        linetype='solid', color='black'
    ) +
    geom_text(
        x=end_x3, y=hight_y3, label="|", color='black', size=8
    ) +
     geom_text(
        x=start_x3, y=hight_y3, label="|", color='black', size=8
    ) +
    geom_text(
        x=6, y=0.17, label="*", color='black', size=12
    ) + # start balken 4
    geom_segment(
        x=start_x4, y=hight_y4, xend=end_x4, yend=hight_y4,
        linetype='solid', color='black'
    ) +
    geom_text(
        x=end_x4, y=hight_y4, label="|", color='black', size=8
    ) +
     geom_text(
        x=start_x4, y=hight_y4, label="|", color='black', size=8
    ) +
    geom_text(
        x=1.5, y=0.17, label="*", color='black', size=12
    ) + # start balken 5
    geom_segment(
        x=start_x5, y=hight_y5, xend=end_x5, yend=hight_y5,
        linetype='solid', color='black'
    ) +
    geom_text(
        x=end_x5, y=hight_y5, label="|", color='black', size=8
    ) +
     geom_text(
        x=start_x5, y=hight_y5, label="|", color='black', size=8
    ) +
    geom_text(
        x=2, y=0.19, label="*", color='black', size=12
    ) +
    labs(title='Vc: Unterschiede liegender TMG Messungen \nzwischen den verschiedenen Messzeitpunkten') +
    ylab('Vc [ms/mm]') +
    xlab('Messung') +
    scale_x_discrete(limits=['supine_1_pre', 'supine_2_pre', 'supine_3_pre', 'supine_4_pre',
                             'supine_1_post','supine_2_post', 'supine_3_post', 'supine_4_post'])
)

# Spielerei
### Stat Auswertung Pre/Posttest Vergleich für sitzende Parameter before_warmup bis s1

In [33]:
desired_measurements = ['before_warmup_pre', 'after_warmup_pre', 'after_pt_pre', 's1_pre',
                       'before_warmup_post', 'after_warmup_post', 'after_pt_post', 's1_post']
sitting_tmg_parameter = tmg_parameter[tmg_parameter['measurement'].isin(desired_measurements)]

td_stat_s = pg.mixed_anova(dv='Td',between='group', within='measurement', subject='id',
                         data=sitting_tmg_parameter,
                         correction='auto', effsize='np2')
td_stat_s.round(3)

Source       SS  DF1  DF2      MS       F  p-unc  p-GG-corr    np2  \
0        group   13.021    1   22  13.021   0.557  0.464        NaN  0.025   
1  measurement  252.083    7  154  36.012  16.933  0.000        0.0  0.435   
2  Interaction    4.646    7  154   0.664   0.312  0.948        NaN  0.014   

     eps sphericity  W-spher  p-spher  
0    NaN        NaN      NaN      NaN  
1  0.421      False     0.01      0.0  
2    NaN        NaN      NaN      NaN

In [ ]:
# Keine Interaktion. Also zur Analyse der Differenzen in den Belastungssätzen

In [34]:
my_colors = ['#FF5733', '#33FF57', '#3366FF', '#FFFF33', '#33FFFF', '#FF33FF', '#33CC00',
             '#FF33CC', '#FF6633', '#33FF00', '#6600CC', '#33CC33', '#FF00FF', '#6600FF',
             '#00CCFF', '#CC33CC', '#0066FF', '#33CC99', '#66CC00', '#996633', '#00FF33',
             '#CC0033', '#33CC66', '#CC66FF']

(
    ggplot(tmg_parameter.query('experiment == "pretest"'), aes(x='measurement', y='Td', color='id', group='id'))
    + geom_line()
    + geom_point()
    + scale_color_manual(values=my_colors)
    + labs(title='Td jeden Messzeitpunkt im Pre-Test', subtitle = 'Farben entsprechen ids')
    + theme(legend_position='none')
    + ylab('Td [ms]')
    + xlab('Messzeitpunkt')
    + scale_x_discrete(limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                               's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre'])
)

In [35]:
my_colors = ['#FF5733', '#33FF57', '#3366FF', '#FFFF33', '#33FFFF', '#FF33FF', '#33CC00',
             '#FF33CC', '#FF6633', '#33FF00', '#6600CC', '#33CC33', '#FF00FF', '#6600FF',
             '#00CCFF', '#CC33CC', '#0066FF', '#33CC99', '#66CC00', '#996633', '#00FF33',
             '#CC0033', '#33CC66', '#CC66FF']

(
    ggplot(tmg_parameter.query('experiment == "posttest"'), aes(x='measurement', y='Td', color='id', group='id'))
    + geom_line()
    + geom_point()
    + scale_color_manual(values=my_colors)
    + labs(title='Td jeden Messzeitpunkt im Post-Test', subtitle = 'Farben entsprechen ids')
    + theme(legend_position='none')
    + ylab('Td [ms]')
    + xlab('Messzeitpunkt')
    + scale_x_discrete(limits=['supine_1_post', 'before_warmup_post', 'after_warmup_post', 's1_post', 's2_post', 's3_post',
                               's4_post', 's5_post', 's6_post', 's7_post', 'supine_2_post', 'supine_3_post', 'supine_4_post'])
)

# Alte Auswertung über alle Messzeitpunkte

# Tc

In [17]:
(
    ggplot(tmg_parameter, aes(x='experiment', y='Tc'))
    + geom_boxplot(aes(group='group', color='group'))
    + labs(title='Tc Verteilung nach Zeitpunkt und Gruppe')
    + ylab('Tc [ms]')
    + xlab('Messung')
)

In [235]:
tc_pre = (
    ggplot(grouped_means, aes(x='measurement', y='Tc', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means['Tc'] - grouped_means['Tc_std'],
            ymax=grouped_means['Tc'] + grouped_means['Tc_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + labs(title='Pre-Test: Tc Mittelwert und Std nach Zeitpunkt und Gruppe')
    + ylab('Tc [ms]')
    + xlab('Messung')
    + scale_x_discrete(
        limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 'after_pt_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre'])
)

tc_pre.show()

In [236]:
#ggsave(tc_pre, filename='tc_pre.svg')

'C:\\Users\\bvenn\\lets-plot-images\\tc_pre.svg'

### Versuche eines neu Tc Pre Test Plots ohne Linien

In [238]:
tc_post = (
    ggplot(grouped_means_post, aes(x='measurement', y='Tc', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means_post['Tc'] - grouped_means_post['Tc_std'],
            ymax=grouped_means_post['Tc'] + grouped_means_post['Tc_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + labs(title='Post-Test: Tc Mittelwert und Std nach Zeitpunkt und Gruppe')
    + ylab('Tc [ms]')
    + xlab('Messung')
    + scale_x_discrete(
        limits=['supine_1_post', 'before_warmup_post', 'after_warmup_post', 'after_pt_post', 's1_post', 's2_post', 's3_post', 's4_post',
                's5_post', 's6_post', 's7_post', 's8_post','supine_2_post', 'supine_3_post', 'supine_4_post'])
)

tc_post.show()


In [239]:
#ggsave(tc_post, filename='tc_post.svg')

'C:\\Users\\bvenn\\lets-plot-images\\tc_post.svg'

In [22]:
(
    ggplot(grouped_means_post, aes(x='measurement', y='Tc', color='group', group='group'))
    + geom_point()
    + geom_line()
    + geom_ribbon(aes(ymin=grouped_means_post['Tc'] - grouped_means_post['Tc_std'], ymax=grouped_means_post['Tc'] + 
                      grouped_means_post['Tc_std'], fill='group'), alpha=0.2, linetype="blank")
    + labs(title='Post-Test: Tc Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='Sitzende Messungen')
    + ylab('Tc [ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7'])
)


In [25]:
tc_stat = pg.mixed_anova(dv='Tc',between='group', within='experiment', subject='id', data=tmg_parameter, correction='auto', effsize='np2')
tc_stat

Source        SS  DF1  DF2        MS         F     p-unc       np2  \
0        group  0.427374    1   22  0.427374  0.013092  0.909944  0.000595   
1   experiment  7.840842    1   22  7.840842  3.068968  0.093730  0.122421   
2  Interaction  0.453606    1   22  0.453606  0.177545  0.677580  0.008006   

   eps  
0  NaN  
1  1.0  
2  NaN

In [73]:
my_colors = ['#FF5733', '#33FF57', '#3366FF', '#FFFF33', '#33FFFF', '#FF33FF', '#33CC00',
             '#FF33CC', '#FF6633', '#33FF00', '#6600CC', '#33CC33', '#FF00FF', '#6600FF',
             '#00CCFF', '#CC33CC', '#0066FF', '#33CC99', '#66CC00', '#996633', '#00FF33',
             '#CC0033', '#33CC66', '#CC66FF']

(
    ggplot(tmg_parameter.query('experiment == "pretest"'), aes(x='measurement', y='Tc', color='id', group='id'))
    + geom_line()
    + geom_point()
    + scale_color_manual(values=my_colors)
    + labs(title='Individuelle Tc Werte im Pre-Test', subtitle = 'Farben entsprechen ids')
    + theme(legend_position='none')
    + ylab('Tc [ms]')
    + xlab('Messzeitpunkt')
    + scale_x_discrete(limits=['supine_1', 'before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7', 's8'])
)

In [79]:
my_colors = ['#FF5733', '#33FF57', '#3366FF', '#FFFF33', '#33FFFF', '#FF33FF', '#33CC00',
             '#FF33CC', '#FF6633', '#33FF00', '#6600CC', '#33CC33', '#FF00FF', '#6600FF',
             '#00CCFF', '#CC33CC', '#0066FF', '#33CC99', '#66CC00', '#996633', '#00FF33',
             '#CC0033', '#33CC66', '#CC66FF']

(
    ggplot(tmg_parameter.query('experiment == "posttest"'), aes(x='measurement', y='Tc', color='id', group='id'))
    + geom_line()
    + geom_point()
    + scale_color_manual(values=my_colors)
    + labs(title='Individuelle Tc Werte im Post-Test', subtitle = 'Farben entsprechen ids')
    + theme(legend_position='none')
    + ylab('Tc [ms]')
    + xlab('Messzeitpunkt')
    + scale_x_discrete(limits=['supine_1', 'before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7', 's8'])
)

# Dm

In [75]:
(
    ggplot(tmg_parameter, aes(x='experiment', y='Dm'))
    + geom_boxplot(aes(group='group', color='group'))
    + labs(title='Dm Verteilung nach Zeitpunkt und Gruppe')
    + ylab('Dm [mm]')
    + xlab('Messung')
)

In [140]:
(
    ggplot(grouped_means, aes(x='measurement', y='Dm', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means['Dm'] - grouped_means['Dm_std'],
            ymax=grouped_means['Dm'] + grouped_means['Dm_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + labs(title='Pre-Test: Dm Mittelwert und Std nach Zeitpunkt und Gruppe')
    + ylab('Dm [mm]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1', 'before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7', 's8',
                              'supine_2', 'supine_3', 'supine_4'])
)


In [110]:
(
    ggplot(grouped_means, aes(x='measurement', y='Dm', color='group', group='group'))
    + geom_point()
    + geom_line()
    + geom_ribbon(aes(ymin=grouped_means['Dm'] - grouped_means['Dm_std'], ymax=grouped_means['Dm'] + grouped_means['Dm_std'], fill='group'), alpha=0.2, linetype="blank")
    + labs(title='Pre-Test: Dm Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='mean und std probleme')
    + ylab('Dm [mm]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1', 'before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7', 's8',
                              'supine_2', 'supine_3', 'supine_4'])
)


In [108]:
(
    ggplot(grouped_means, aes(x='measurement', y='Dm', color='group', group='group'))
    + geom_point()
    + geom_line()
    + geom_ribbon(aes(ymin=grouped_means['Dm'] - grouped_means['Dm_std'], ymax=grouped_means['Dm'] + grouped_means['Dm_std'], fill='group'), alpha=0.2, linetype="blank")
    + labs(title='Pre-Test: Dm Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='Liegende Messungen')
    + ylab('Dm [mm]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1','supine_2', 'supine_3', 'supine_4'])
)


In [111]:
(
    ggplot(grouped_means, aes(x='measurement', y='Dm', color='group', group='group'))
    + geom_point()
    + geom_line()
    + geom_ribbon(aes(ymin=grouped_means['Dm'] - grouped_means['Dm_std'], ymax=grouped_means['Dm'] + grouped_means['Dm_std'], fill='group'), alpha=0.2, linetype="blank")
    + labs(title='Pre-Test: Dm Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='Sitzende Messungen')
    + ylab('Dm [mm]')
    + xlab('Messung')
    + scale_x_discrete(limits=['before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7', 's8'])
)


In [141]:
(
    ggplot(grouped_means_post, aes(x='measurement', y='Dm', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means_post['Dm'] - grouped_means_post['Dm_std'],
            ymax=grouped_means_post['Dm'] + grouped_means_post['Dm_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + labs(title='Post-Test: Tc Mittelwert und Std nach Zeitpunkt und Gruppe')
    + ylab('Dm [mm]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1', 'before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7',
                              'supine_2', 'supine_3', 'supine_4'])
)


In [114]:
(
    ggplot(grouped_means_post, aes(x='measurement', y='Dm', color='group', group='group'))
    + geom_point()
    + geom_line()
    + geom_ribbon(aes(ymin=grouped_means_post['Dm'] - grouped_means_post['Dm_std'], ymax=grouped_means_post['Dm'] + 
                      grouped_means_post['Dm_std'], fill='group'), alpha=0.2, linetype="blank")
    + labs(title='Post-Test: Dm Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='mean und std Probleme')
    + ylab('Dm [mm]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1', 'before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7', 's8',
                              'supine_2', 'supine_3', 'supine_4'])
)


In [115]:
(
    ggplot(grouped_means_post, aes(x='measurement', y='Dm', color='group', group='group'))
    + geom_point()
    + geom_line()
    + geom_ribbon(aes(ymin=grouped_means_post['Dm'] - grouped_means_post['Dm_std'], ymax=grouped_means_post['Dm'] + 
                      grouped_means_post['Dm_std'], fill='group'), alpha=0.2, linetype="blank")
    + labs(title='Post-Test: Dm Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='Liegende Messungen')
    + ylab('Dm [mm]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1','supine_2', 'supine_3', 'supine_4'])
)


In [116]:
(
    ggplot(grouped_means_post, aes(x='measurement', y='Dm', color='group', group='group'))
    + geom_point()
    + geom_line()
    + geom_ribbon(aes(ymin=grouped_means_post['Dm'] - grouped_means_post['Dm_std'], ymax=grouped_means_post['Dm'] + 
                      grouped_means_post['Dm_std'], fill='group'), alpha=0.2, linetype="blank")
    + labs(title='Post-Test: Dm Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='Sitzende Messungen')
    + ylab('Dm [mm]')
    + xlab('Messung')
    + scale_x_discrete(limits=['before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7'])
)


In [56]:
dm_stat = pg.mixed_anova(dv='Dm',between='group', within='experiment', subject='id', data=tmg_parameter, correction='auto', effsize='np2')
dm_stat

Source        SS  DF1  DF2        MS         F     p-unc       np2  \
0        group  2.971148    1   22  2.971148  0.416595  0.525316  0.018584   
1   experiment  0.065040    1   22  0.065040  0.208026  0.652790  0.009367   
2  Interaction  0.260784    1   22  0.260784  0.834103  0.370990  0.036529   

   eps  
0  NaN  
1  1.0  
2  NaN

# Vc

In [81]:
(
    ggplot(tmg_parameter, aes(x='experiment', y='Vc'))
    + geom_boxplot(aes(group='group', color='group'))
    + labs(title='Vc Verteilung nach Zeitpunkt und Gruppe')
    + ylab('Vc [mm/ms]')
    + xlab('Messung')
)

In [143]:
(
    ggplot(grouped_means, aes(x='measurement', y='Vc', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means['Vc'] - grouped_means['Vc_std'],
            ymax=grouped_means['Vc'] + grouped_means['Vc_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + labs(title='Pre-Test: Vc Mittelwert und Std nach Zeitpunkt und Gruppe')
    + ylab('Vc [mm/ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1', 'before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7', 's8',
                              'supine_2', 'supine_3', 'supine_4'])
)


In [117]:
(
    ggplot(grouped_means, aes(x='measurement', y='Vc', color='group', group='group'))
    + geom_point()
    + geom_line()
    + geom_ribbon(aes(ymin=grouped_means['Vc'] - grouped_means['Vc_std'], ymax=grouped_means['Vc'] + grouped_means['Vc_std'], fill='group'), alpha=0.2, linetype="blank")
    + labs(title='Pre-Test: Vc Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='mean und std Probleme')
    + ylab('Vc [mm/ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1', 'before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7', 's8',
                              'supine_2', 'supine_3', 'supine_4'])
)


In [118]:
(
    ggplot(grouped_means, aes(x='measurement', y='Vc', color='group', group='group'))
    + geom_point()
    + geom_line()
    + geom_ribbon(aes(ymin=grouped_means['Vc'] - grouped_means['Vc_std'], ymax=grouped_means['Vc'] + grouped_means['Vc_std'], fill='group'), alpha=0.2, linetype="blank")
    + labs(title='Pre-Test: Vc Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='Liegende Messungen')
    + ylab('Vc [mm/ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1','supine_2', 'supine_3', 'supine_4'])
)


In [119]:
(
    ggplot(grouped_means, aes(x='measurement', y='Vc', color='group', group='group'))
    + geom_point()
    + geom_line()
    + geom_ribbon(aes(ymin=grouped_means['Vc'] - grouped_means['Vc_std'], ymax=grouped_means['Vc'] + grouped_means['Vc_std'], fill='group'), alpha=0.2, linetype="blank")
    + labs(title='Pre-Test: Vc Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='Sitzende Messungen')
    + ylab('Vc [mm/ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7', 's8'])
)


In [144]:
(
    ggplot(grouped_means_post, aes(x='measurement', y='Vc', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means_post['Vc'] - grouped_means_post['Vc_std'],
            ymax=grouped_means_post['Vc'] + grouped_means_post['Vc_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + labs(title='Post-Test: Vc Mittelwert und Std nach Zeitpunkt und Gruppe')
    + ylab('Vc [mm/ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1', 'before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7',
                              'supine_2', 'supine_3', 'supine_4'])
)


In [124]:
(
    ggplot(grouped_means_post, aes(x='measurement', y='Vc', color='group', group='group'))
    + geom_point()
    + geom_line()
    + geom_ribbon(aes(ymin=grouped_means_post['Vc'] - grouped_means_post['Vc_std'], ymax=grouped_means_post['Vc'] + 
                      grouped_means_post['Vc_std'], fill='group'), alpha=0.2, linetype="blank")
    + labs(title='Post-Test: Vc Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='mean und std Probleme')
    + ylab('Vc [mm/ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1', 'before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7', 's8',
                              'supine_2', 'supine_3', 'supine_4'])
)


In [121]:
(
    ggplot(grouped_means_post, aes(x='measurement', y='Vc', color='group', group='group'))
    + geom_point()
    + geom_line()
    + geom_ribbon(aes(ymin=grouped_means_post['Vc'] - grouped_means_post['Vc_std'], ymax=grouped_means_post['Vc'] + 
                      grouped_means_post['Vc_std'], fill='group'), alpha=0.2, linetype="blank")
    + labs(title='Post-Test: Vc Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='Liegende Messungen')
    + ylab('Vc [mm/ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1', 'supine_2', 'supine_3', 'supine_4'])
)


In [122]:
(
    ggplot(grouped_means_post, aes(x='measurement', y='Vc', color='group', group='group'))
    + geom_point()
    + geom_line()
    + geom_ribbon(aes(ymin=grouped_means_post['Vc'] - grouped_means_post['Vc_std'], ymax=grouped_means_post['Vc'] + 
                      grouped_means_post['Vc_std'], fill='group'), alpha=0.2, linetype="blank")
    + labs(title='Post-Test: Vc Mittelwert und Std nach Zeitpunkt und Gruppe', subtitle='Sitzende Messungen')
    + ylab('Vc [mm/ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7', 's8'])
)


In [58]:
vc_stat = pg.mixed_anova(dv='Vc',between='group', within='experiment', subject='id', data=tmg_parameter, correction='auto', effsize='np2')
vc_stat

Source            SS  DF1  DF2            MS         F     p-unc  \
0        group  4.297159e-04    1   22  4.297159e-04  0.350047  0.560118   
1   experiment  9.387113e-08    1   22  9.387113e-08  0.001518  0.969268   
2  Interaction  5.502415e-05    1   22  5.502415e-05  0.890039  0.355713   

        np2  eps  
0  0.015662  NaN  
1  0.000069  1.0  
2  0.038883  NaN

# Ts

In [84]:
(
    ggplot(tmg_parameter, aes(x='experiment', y='Ts'))
    + geom_boxplot(aes(group='group', color='group'))
    + labs(title='Ts Verteilung nach Zeitpunkt und Gruppe')
    + ylab('Ts [ms]')
    + xlab('Messung')
)

In [145]:
(
    ggplot(grouped_means, aes(x='measurement', y='Ts', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means['Ts'] - grouped_means['Ts_std'],
            ymax=grouped_means['Ts'] + grouped_means['Ts_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + labs(title='Pre-Test: Ts Mittelwert und Std nach Zeitpunkt und Gruppe')
    + ylab('Ts [ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1', 'before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7', 's8',
                              'supine_2', 'supine_3', 'supine_4'])
)


In [69]:
# nach ausreißern schauen
tmg_parameter.query('Ts > 310')

id     group experiment    measurement        Dm    Td    Tc     Ts  \
106  27351  beta_ala    pretest   after_warmup  6.512383  21.0  40.0  313.0   
128  28514   placebo    pretest  before_warmup  2.085678  21.0  36.0  962.0   
161  39337   placebo   posttest  before_warmup  4.529190  24.0  49.0  448.0   
318  54658   placebo    pretest   after_warmup  1.406583  19.0  36.0  346.0   
467  93302   placebo   posttest  before_warmup  4.016112  20.0  46.0  313.0   

        Tr        Vc  
106  286.0  0.106760  
128  944.0  0.036591  
161  236.0  0.062044  
318  328.0  0.025574  
467  281.0  0.060850

In [85]:
(
    ggplot(grouped_means, aes(x='measurement', y='Ts', color='group', group='group'))
    + geom_point()
    + geom_line()
    + geom_ribbon(aes(ymin=grouped_means['Ts'] - grouped_means['Ts_std'], ymax=grouped_means['Ts'] + grouped_means['Ts_std'], fill='group'), alpha=0.2, linetype="blank")
    + labs(title='Pre-Test: Ts Mittelwert und Std nach Zeitpunkt und Gruppe')
    + ylab('Ts [ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1', 'before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7', 's8',
                              'supine_2', 'supine_3', 'supine_4'])
)


In [146]:
(
    ggplot(grouped_means_post, aes(x='measurement', y='Ts', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means_post['Ts'] - grouped_means_post['Ts_std'],
            ymax=grouped_means_post['Ts'] + grouped_means_post['Ts_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + labs(title='Post-Test: Ts Mittelwert und Std nach Zeitpunkt und Gruppe')
    + ylab('Ts [ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1', 'before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7',
                              'supine_2', 'supine_3', 'supine_4'])
)


In [86]:
(
    ggplot(grouped_means_post, aes(x='measurement', y='Ts', color='group', group='group'))
    + geom_point()
    + geom_line()
    + geom_ribbon(aes(ymin=grouped_means_post['Ts'] - grouped_means_post['Ts_std'], 
                      ymax=grouped_means_post['Ts'] + grouped_means_post['Ts_std'], fill='group'), alpha=0.2, linetype="blank")
    + labs(title='Post-Test: Ts Mittelwert und Std nach Zeitpunkt und Gruppe')
    + ylab('Ts [ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1', 'before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7', 's8',
                              'supine_2', 'supine_3', 'supine_4'])
)


In [60]:
ts_stat = pg.mixed_anova(dv='Ts',between='group', within='experiment', subject='id', data=tmg_parameter, correction='auto', effsize='np2')
ts_stat

Source          SS  DF1  DF2          MS         F     p-unc  \
0        group  453.705889    1   22  453.705889  0.102355  0.752040   
1   experiment  725.932164    1   22  725.932164  2.902314  0.102539   
2  Interaction  150.560316    1   22  150.560316  0.601948  0.446097   

        np2  eps  
0  0.004631  NaN  
1  0.116548  1.0  
2  0.026633  NaN

# Tr

In [87]:
(
    ggplot(tmg_parameter, aes(x='experiment', y='Tr'))
    + geom_boxplot(aes(group='group', color='group'))
    + labs(title='Tr Verteilung nach Zeitpunkt und Gruppe')
    + ylab('Tr [ms]')
    + xlab('Messung')
)

In [148]:
(
    ggplot(grouped_means, aes(x='measurement', y='Tr', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means['Tr'] - grouped_means['Tr_std'],
            ymax=grouped_means['Tr'] + grouped_means['Tr_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + labs(title='Pre-Test: Tr Mittelwert und Std nach Zeitpunkt und Gruppe')
    + ylab('Tr [ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1', 'before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7', 's8',
                              'supine_2', 'supine_3', 'supine_4'])
)


In [88]:
(
    ggplot(grouped_means, aes(x='measurement', y='Tr', color='group', group='group'))
    + geom_point()
    + geom_line()
    + geom_ribbon(aes(ymin=grouped_means['Tr'] - grouped_means['Tr_std'], ymax=grouped_means['Tr'] + grouped_means['Tr_std'], fill='group'), alpha=0.2, linetype="blank")
    + labs(title='Pre-Test: Tr Mittelwert und Std nach Zeitpunkt und Gruppe')
    + ylab('Tr [ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1', 'before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7', 's8',
                              'supine_2', 'supine_3', 'supine_4'])
)


In [147]:
(
    ggplot(grouped_means_post, aes(x='measurement', y='Tr', color='group', group='group'))
    + geom_point(position=position_dodge(width=0.4))  # Hier kannst du die Breite nach Bedarf anpassen
    + geom_line(position=position_dodge(width=0.4))
    + geom_errorbar(
        aes(ymin=grouped_means_post['Tr'] - grouped_means_post['Tr_std'],
            ymax=grouped_means_post['Tr'] + grouped_means_post['Tr_std'],
            fill='group'),
        position=position_dodge(width=0.4),
        linetype="blank"
    )
    + labs(title='Post-Test: Tr Mittelwert und Std nach Zeitpunkt und Gruppe')
    + ylab('Tr [ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1', 'before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7',
                              'supine_2', 'supine_3', 'supine_4'])
)


In [89]:
(
    ggplot(grouped_means_post, aes(x='measurement', y='Tr', color='group', group='group'))
    + geom_point()
    + geom_line()
    + geom_ribbon(aes(ymin=grouped_means_post['Tr'] - grouped_means_post['Tr_std'], 
                      ymax=grouped_means_post['Tr'] + grouped_means_post['Tr_std'], fill='group'), alpha=0.2, linetype="blank")
    + labs(title='Post-Test: Tr Mittelwert und Std nach Zeitpunkt und Gruppe')
    + ylab('Tr [ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['supine_1', 'before_warmup', 'after_warmup', 's1', 's2', 's3', 's4', 's5', 's6', 's7', 's8',
                              'supine_2', 'supine_3', 'supine_4'])
)


In [61]:
tr_stat = pg.mixed_anova(dv='Tr',between='group', within='experiment', subject='id', data=tmg_parameter, correction='auto', effsize='np2')
tr_stat

Source          SS  DF1  DF2          MS         F     p-unc  \
0        group   56.330483    1   22   56.330483  0.018320  0.893565   
1   experiment  826.029920    1   22  826.029920  5.277460  0.031490   
2  Interaction   94.414983    1   22   94.414983  0.603212  0.445626   

        np2  eps  
0  0.000832  NaN  
1  0.193473  1.0  
2  0.026687  NaN

In [68]:
posthoc_tr = pg.pairwise_tests(data=tmg_parameter, dv='Tr', within='experiment', subject='id', parametric=True, padjust='bonf', effsize='cohen')

# Print the post hoc test results
posthoc_tr

Contrast        A         B  Paired  Parametric         T   dof  \
0  experiment  pretest  posttest    True        True  2.317348  23.0   

  alternative     p-unc  BF10     cohen  
0   two-sided  0.029737  1.97  0.210825

# Bis hier kann gelöscht werden

# Sitzende Parameter Publikation

In [34]:
# berechnung in excel datei gemacht
diff_df = pd.read_excel(r"C:\Users\bvenn\OneDrive\Desktop\Publikation\TMG Rohdaten Frame\tmg_parameter.xlsx", sheet_name='tmg_diff')
diff_df = diff_df.astype({'group': 'category', 'experiment': 'category'})
diff_df = diff_df.sort_values(by='experiment', ascending=True)
diff_df

id     group experiment        Dm  Td  Tc   Ts   Tr        Vc
47  93672  beta_ala   posttest -3.647600   2   5    3    1 -0.070517
25  20438  beta_ala   posttest -1.236830   1   6   24   10 -0.026392
26  25778  beta_ala   posttest -1.067054   1   4    2    0 -0.021753
27  26107  beta_ala   posttest -0.706058   3   2 -202 -202 -0.013451
28  27351  beta_ala   posttest -0.525296   0   0   21   26 -0.008081
29  28514   placebo   posttest -1.429971   0   1  -69  -68 -0.028223
30  33468   placebo   posttest  0.393301   3   8  -58   29 -0.007598
31  39337   placebo   posttest -1.792409   2   4    3    1 -0.034555
32  39750   placebo   posttest -1.831496   0  -1   -3   -2 -0.035066
33  44858  beta_ala   posttest -0.295869   6  10  -91  -99 -0.017450
34  49444   placebo   posttest -0.042537   1   5    3    0 -0.002552
35  49830  beta_ala   posttest -0.873405   1   2    1    0 -0.017802
36  50843   placebo   posttest -1.951112   0   4    1    0 -0.041005
37  54145  beta_ala   posttest -0.260201   3   3    0    0 -0.006197
38  54658   placebo   posttest -1.442738   3   6 -220 -223 -0.030060
39  58046  beta_ala   posttest -0.470174   0   2    3    1 -0.010163
40  59289  beta_ala   posttest -3.117787   3   5   -3   -3 -0.059503
41  61104   placebo   posttest -1.098621   2   1   -5   -2 -0.019094
42  71620   placebo   posttest -1.131586   5  11    9    3 -0.033980
43  73126  beta_ala   posttest -2.342741   3   7    0  -13 -0.044005
44  76847   placebo   posttest -3.182726   2   3   15   71 -0.050021
45  82556   placebo   posttest -0.291189   5   5   75   71 -0.012829
24  15073  beta_ala   posttest -1.594417   1  -2  -23  110 -0.025134
46  93302   placebo   posttest -0.451045   0   0    1    0 -0.009021
0   15073  beta_ala    pretest -1.927345  -1  -1 -167 -166 -0.033029
21  82556   placebo    pretest -1.684138   3   6  118  109 -0.032631
1   20438  beta_ala    pretest -1.325736   0  -4   -5   -1 -0.025790
2   25778  beta_ala    pretest -1.234278  -9  -4    0   -1 -0.021763
3   26107  beta_ala    pretest -0.978542   2   2 -105 -103 -0.017702
4   27351  beta_ala    pretest -0.673070  -1  -1 -135 -132 -0.007789
5   28514   placebo    pretest -2.696394  -2  -8  -89  -72 -0.038459
6   33468   placebo    pretest  1.724444   4  28  -55 -140 -0.005704
7   39337   placebo    pretest -1.614100   4   6    2    0 -0.033655
8   39750   placebo    pretest -2.097513   0   0   -1   -2 -0.038843
9   44858  beta_ala    pretest -0.621867   2   4  -63  -63 -0.015609
22  93302   placebo    pretest -1.300348   0   0    0   -1 -0.024535
10  49444   placebo    pretest  0.073032   2   5    3    1 -0.000778
12  50843   placebo    pretest -1.869437   1   8   -1   -2 -0.042910
13  54145  beta_ala    pretest -0.704557   0   0    1    0 -0.012810
14  54658   placebo    pretest  0.277864   5   8 -313 -316 -0.000803
15  58046  beta_ala    pretest -2.333214   0   0    0    0 -0.037035
16  59289  beta_ala    pretest -2.519786   4   7   57   57 -0.048067
17  61104   placebo    pretest -1.464872  -1   0   -2   -1 -0.026911
18  71620   placebo    pretest -1.510096   3   9    6    2 -0.033808
19  73126  beta_ala    pretest  1.139305   7  10  -25  -66  0.002316
20  76847   placebo    pretest -2.151731   3 -12  -14   78 -0.022617
11  49830  beta_ala    pretest  0.222555   2   6    8    4  0.001024
23  93672  beta_ala    pretest -3.549914   4   5    0   -2 -0.066481

## diff Dm

In [36]:
(
    ggplot(diff_df, aes(x='experiment', y='Dm', color='group', group='group'))
    + geom_boxplot(width=0.5)
    + labs(title='Unterschiede der Differenzen zwischen after_warmup und letzter Messung')
    + ylab('Dm Difference [mm]')
    + xlab('Messung')
    + scale_x_discrete(limits=['pretest', 'posttest'], labels=['Pre-Test', 'Post-Test'])
)

In [137]:
dm_stat = pg.mixed_anova(dv='Dm',between='group', within='experiment', subject='id', data=diff_df, correction='auto', effsize='np2')
dm_stat

Source        SS  DF1  DF2        MS         F     p-unc       np2  \
0        group  0.090000    1   22  0.090000  0.043583  0.836551  0.001977   
1   experiment  0.051341    1   22  0.051341  0.080825  0.778841  0.003660   
2  Interaction  0.059653    1   22  0.059653  0.093911  0.762144  0.004251   

   eps  
0  NaN  
1  1.0  
2  NaN

## Diff Td

In [37]:
(
    ggplot(diff_df, aes(x='experiment', y='Td', color='group', group='group'))
    + geom_boxplot(width=0.5)
    + labs(title='Unterschiede der Differenzen zwischen after_warmup und letzter Messung')
    + ylab('Td Difference [ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['pretest', 'posttest'], labels=['Pre-Test', 'Post-Test'])
)

In [139]:
Td_stat = pg.mixed_anova(dv='Td',between='group', within='experiment', subject='id', data=diff_df, correction='auto', effsize='np2')
Td_stat

Source        SS  DF1  DF2        MS         F     p-unc       np2  \
0        group  2.520833    1   22  2.520833  0.270583  0.608136  0.012150   
1   experiment  4.687500    1   22  4.687500  1.209086  0.283401  0.052095   
2  Interaction  3.520833    1   22  3.520833  0.908158  0.350958  0.039643   

   eps  
0  NaN  
1  1.0  
2  NaN

## diff Tc

In [38]:
(
    ggplot(diff_df, aes(x='experiment', y='Tc', color='group', group='group'))
    + geom_boxplot(width=0.5)
    + labs(title='Unterschiede der Differenzen zwischen after_warmup und letzter Messung')
    + ylab('Tc Difference [ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['pretest', 'posttest'], labels=['Pre-Test', 'Post-Test'])
)

In [141]:
Tc_stat = pg.mixed_anova(dv='Tc',between='group', within='experiment', subject='id', data=diff_df, correction='auto', effsize='np2')
Tc_stat

Source         SS  DF1  DF2         MS         F     p-unc       np2  \
0        group  17.520833    1   22  17.520833  0.357637  0.555928  0.015996   
1   experiment   6.020833    1   22   6.020833  0.279768  0.602150  0.012557   
2  Interaction  11.020833    1   22  11.020833  0.512101  0.481758  0.022748   

   eps  
0  NaN  
1  1.0  
2  NaN

## diff Ts

In [39]:
(
    ggplot(diff_df, aes(x='experiment', y='Ts', color='group', group='group'))
    + geom_boxplot(width=0.5)
    + labs(title='Unterschiede der Differenzen zwischen after_warmup und letzter Messung')
    + ylab('Ts Difference [ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['pretest', 'posttest'], labels=['Pre-Test', 'Post-Test'])
)

In [144]:
Ts_stat = pg.mixed_anova(dv='Ts',between='group', within='experiment', subject='id', data=diff_df, correction='auto', effsize='np2')
Ts_stat

Source           SS  DF1  DF2           MS         F     p-unc  \
0        group   229.687500    1   22   229.687500  0.021952  0.883563   
1   experiment  1485.187500    1   22  1485.187500  0.947096  0.341039   
2  Interaction   105.020833    1   22   105.020833  0.066971  0.798205   

        np2  eps  
0  0.000997  NaN  
1  0.041273  1.0  
2  0.003035  NaN

## diff Tr

In [40]:
(
    ggplot(diff_df, aes(x='experiment', y='Tr', color='group', group='group'))
    + geom_boxplot(width=0.5)
    + labs(title='Unterschiede der Differenzen zwischen after_warmup und letzter Messung')
    + ylab('Tr Difference [ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['pretest', 'posttest'], labels=['Pre-Test', 'Post-Test'])
)

In [146]:
Tr_stat = pg.mixed_anova(dv='Tr',between='group', within='experiment', subject='id', data=diff_df, correction='auto', effsize='np2')
Tr_stat

Source           SS  DF1  DF2           MS         F     p-unc  \
0        group   660.083333    1   22   660.083333  0.062098  0.805523   
1   experiment  5808.000000    1   22  5808.000000  1.754691  0.198884   
2  Interaction   133.333333    1   22   133.333333  0.040282  0.842774   

        np2  eps  
0  0.002815  NaN  
1  0.073867  1.0  
2  0.001828  NaN

## diff Vc

In [41]:
(
    ggplot(diff_df, aes(x='experiment', y='Vc', color='group', group='group'))
    + geom_boxplot(width=0.5)
    + labs(title='Unterschiede der Differenzen zwischen after_warmup und letzter Messung')
    + ylab('Vc Difference [mm/ms]')
    + xlab('Messung')
    + scale_x_discrete(limits=['pretest', 'posttest'], labels=['Pre-Test', 'Post-Test'])
)

In [148]:
Vc_stat = pg.mixed_anova(dv='Vc',between='group', within='experiment', subject='id', data=diff_df, correction='auto', effsize='np2')
Vc_stat

Source            SS  DF1  DF2            MS         F     p-unc  \
0        group  1.273159e-07    1   22  1.273159e-07  0.000251  0.987497   
1   experiment  3.343757e-05    1   22  3.343757e-05  0.253255  0.619794   
2  Interaction  2.605676e-05    1   22  2.605676e-05  0.197353  0.661205   

        np2  eps  
0  0.000011  NaN  
1  0.011381  1.0  
2  0.008891  NaN

# Superplots

In [13]:
# Daten vorher kombinieren
combined_data = pd.concat([grouped_means, grouped_means_post], ignore_index=True)

# Reihenfolge der Kategorien anpassen
category_order = ['Pre-Test: Sitting', 'Post-Test: Sitting', 'Pre-Test: Supine', 'Post-Test: Supine']
combined_data['category'] = pd.Categorical(combined_data['category'], categories=category_order, ordered=True)

# Sortiere das DataFrame nach der Kategorie
combined_data.sort_values('category', inplace=True)
combined_data = combined_data.reset_index()


In [14]:
# Lets-Plot-Objekt erstellen
combined_plot = ggplot(combined_data, aes(x='measurement', y='Td', color='group', group='group')) \
        + geom_point(position=position_dodge(width=0.4)) \
        + geom_line(position=position_dodge(width=0.4)) \
        + geom_errorbar(
            aes(ymin=combined_data['Td'] - combined_data['Td_std'],
                ymax=combined_data['Td'] + combined_data['Td_std'],
                fill='group'),
            position=position_dodge(width=0.4),
            linetype="blank"
        ) \
        + facet_grid(y='category', scales='free_y') \
        + labs(title='Grouped Means Combined') \
        + ylab('Td [ms]') \
        + scale_x_discrete(
            limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 'after_pt_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                    's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre',
                    'supine_1_post', 'before_warmup_post', 'after_warmup_post', 'after_pt_post','s1_post', 's2_post', 's3_post',
                    's4_post', 's5_post', 's6_post', 's7_post', 'supine_2_post', 'supine_3_post', 'supine_4_post'],
            labels=['Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                    'After S5', 'After S6', 'After S7', 'After S8', 'Supine 2', 'Supine 3', 'Supine 4',
                    'Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                    'After S5', 'After S6', 'After S7', 'Supine 2', 'Supine 3', 'Supine 4']
        )

# Das kombinierte Plot anzeigen oder speichern
combined_plot.show()

In [15]:
# Lets-Plot-Objekt erstellen
combined_plot = ggplot(combined_data, aes(x='measurement', y='Td', color='group', group='group')) \
        + geom_point(position=position_dodge(width=0.4)) \
        + geom_line(position=position_dodge(width=0.4)) \
        + geom_errorbar(
            aes(ymin=combined_data['Td'] - combined_data['Td_std'],
                ymax=combined_data['Td'] + combined_data['Td_std'],
                fill='group'),
            position=position_dodge(width=0.4),
            linetype="blank"
        ) \
        + facet_grid(y='category', scales='free_y') \
        + labs(title='Grouped Means Combined') \
        + ylab('Td [ms]') \
        + scale_x_discrete(
            limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 'after_pt_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                    's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre',
                    'supine_1_post', 'before_warmup_post', 'after_warmup_post', 'after_pt_post','s1_post', 's2_post', 's3_post',
                    's4_post', 's5_post', 's6_post', 's7_post', 'supine_2_post', 'supine_3_post', 'supine_4_post'],
            labels=['Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                    'After S5', 'After S6', 'After S7', 'After S8', 'Supine 2', 'Supine 3', 'Supine 4',
                    'Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                    'After S5', 'After S6', 'After S7', 'Supine 2', 'Supine 3', 'Supine 4']
        ) \

combined_plot = combined_plot + ggsize(1000, 600)

# Das kombinierte Plot anzeigen oder speichern
combined_plot.show()

## frame mit means und std von pre und post über die gesamte Stichprobe

In [11]:
overall_means = grouped_means.groupby('measurement').agg({'Dm': 'mean', 'Td': 'mean', 'Tc': 'mean', 'Ts': 'mean',
                                                          'Tr': 'mean', 'Vc': 'mean', 
                                                         'Dm_std': 'mean', 'Td_std': 'mean', 'Tc_std': 'mean', 'Ts_std': 'mean',
                                                          'Tr_std': 'mean', 'Vc_std': 'mean',})
overall_means_post = grouped_means_post.groupby('measurement').agg({'Dm': 'mean', 'Td': 'mean', 'Tc': 'mean', 'Ts': 'mean',
                                                          'Tr': 'mean', 'Vc': 'mean', 
                                                         'Dm_std': 'mean', 'Td_std': 'mean', 'Tc_std': 'mean', 'Ts_std': 'mean',
                                                          'Tr_std': 'mean', 'Vc_std': 'mean',})

overall_means_pre_post = pd.concat([overall_means, overall_means_post])
overall_means_pre_post = overall_means_pre_post.rename(columns={'Dm': 'Dm_mean_total', 'Td': 'Td_mean_total', 'Tc': 'Tc_mean_total', 'Ts': 'Ts_mean_total',
                                                          'Tr': 'Tr_mean_total', 'Vc': 'Vc_mean_total', 
                                                         'Dm_std': 'Dm_std_total', 'Td_std': 'Td_std_total', 'Tc_std': 'Tc_std_total','Ts_std': 'Ts_std_total',
                                                          'Tr_std': 'Tr_std_total', 'Vc_std': 'Vc_std_total',})
overall_means_pre_post = overall_means_pre_post.reset_index()
overall_means_pre_post

C:\Users\bvenn\AppData\Local\Temp\ipykernel_9212\2424408066.py:1: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  overall_means = grouped_means.groupby('measurement').agg({'Dm': 'mean', 'Td': 'mean', 'Tc': 'mean', 'Ts': 'mean',


measurement  Dm_mean_total  Td_mean_total  Tc_mean_total  \
0         after_pt_pre       3.172900      19.375000      36.416667   
1     after_warmup_pre       3.211864      19.416667      37.458333   
2    before_warmup_pre       4.115072      22.333333      43.916667   
3               s1_pre       2.683566      21.000000      39.833333   
4               s2_pre       2.305457      21.375000      41.125000   
5               s3_pre       2.253149      22.071429      42.452381   
6               s4_pre       1.632021      20.533333      39.600000   
7               s5_pre       1.811561      21.500000      41.250000   
8               s6_pre       2.019441      23.000000      43.500000   
9               s7_pre       2.384719      22.000000      40.000000   
10              s8_pre       2.968527      24.000000      45.000000   
11        supine_1_pre       9.737196      27.375000      55.208333   
12        supine_2_pre       7.275520      26.625000      53.541667   
13        supine_3_pre       9.426073      27.875000      57.166667   
14        supine_4_pre       9.340451      27.666667      55.458333   
15       after_pt_post       3.126116      19.375000      36.041667   
16   after_warmup_post       3.219945      19.208333      36.125000   
17  before_warmup_post       4.007354      21.750000      42.833333   
18             s1_post       2.685903      20.708333      39.166667   
19             s2_post       2.203358      21.281818      40.600000   
20             s3_post       1.828111      21.071429      39.285714   
21             s4_post       1.615487      20.983333      39.016667   
22             s5_post       1.766647      19.250000      37.500000   
23             s6_post       1.742993      20.250000      37.250000   
24             s7_post       1.222272      18.500000      36.000000   
25       supine_1_post       9.431582      27.333333      53.708333   
26       supine_2_post       7.594565      26.500000      53.416667   
27       supine_3_post       9.001847      27.875000      56.750000   
28       supine_4_post       9.321070      27.625000      54.916667   

    Ts_mean_total  Tr_mean_total  Vc_mean_total  Dm_std_total  Td_std_total  \
0       64.583333      41.541667       0.055395      1.444866      1.649380   
1       95.208333      72.291667       0.055175      1.493040      1.746948   
2      173.458333     136.166667       0.060463      1.719311      2.030022   
3       90.208333      64.916667       0.042795      1.465459      2.556183   
4       73.500000      50.833333       0.034719      1.646694      2.960504   
5       79.476190      51.682540       0.032772      1.502544      3.319030   
6       70.700000      33.533333       0.025387      0.855167      5.046025   
7       99.500000      76.750000       0.027839      1.073021      4.242641   
8      123.000000      99.000000       0.030430      0.260022      2.828427   
9      104.000000      83.500000       0.037454           NaN           NaN   
10     170.000000     147.000000       0.043022           NaN           NaN   
11     106.333333      70.041667       0.118045      2.844717      1.496021   
12      88.875000      52.375000       0.090844      2.637840      2.041430   
13     103.500000      62.250000       0.111119      2.470420      1.664276   
14     109.125000      72.791667       0.112769      2.463330      1.958775   
15      68.000000      43.166667       0.055065      1.639752      1.758095   
16      82.208333      48.625000       0.056858      1.691264      1.589814   
17     137.500000      94.125000       0.060325      1.923727      2.680451   
18      69.666667      49.833333       0.043283      1.555577      2.985839   
19      75.963636      51.777273       0.033949      1.468409      2.993258   
20      64.910714      46.107143       0.029017      1.079012      3.032622   
21      63.616667      43.866667       0.025314      1.041814      2.791438   
22      74.375000      36.750000       0.030285      1.438007  

In [15]:
overall_means.info()

<class 'pandas.core.frame.DataFrame'>
CategoricalIndex: 15 entries, after_pt_pre to supine_4_pre
Data columns (total 12 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   Dm      15 non-null     float64
 1   Td      15 non-null     float64
 2   Tc      15 non-null     float64
 3   Ts      15 non-null     float64
 4   Tr      15 non-null     float64
 5   Vc      15 non-null     float64
 6   Dm_std  13 non-null     float64
 7   Td_std  13 non-null     float64
 8   Tc_std  13 non-null     float64
 9   Ts_std  13 non-null     float64
 10  Tr_std  13 non-null     float64
 11  Vc_std  13 non-null     float64
dtypes: float64(12)
memory usage: 2.1 KB


In [188]:
# Spalten 'Td' und 'Td_std' kombinieren
combined_data['Td_lower'] = combined_data['Td'] - combined_data['Td_std']
combined_data['Td_upper'] = combined_data['Td'] + combined_data['Td_std']

# Spalten für Fehlerbalken in overall_means_pre_post hinzufügen
overall_means_pre_post['lower'] = overall_means_pre_post['Td_mean_total'] - overall_means_pre_post['Td_std_total']
overall_means_pre_post['upper'] = overall_means_pre_post['Td_mean_total'] + overall_means_pre_post['Td_std_total']

width_combined_data = 0.6
width_overall_means = 0.3  # Ändern Sie dies, wenn nötig

# Plot erstellen
combined_plot = ggplot() \
    + geom_point(data=combined_data, mapping=aes(x='measurement', y='Td', color='group', group='group'),
                 position=position_dodge(width=width_combined_data)) \
    + geom_line(data=combined_data, mapping=aes(x='measurement', y='Td', color='group', group='group'),
                position=position_dodge(width=width_combined_data)) \
    + geom_errorbar(data=combined_data,
                    mapping=aes(x='measurement', y='Td', color='group', group='group', ymin='Td_lower', ymax='Td_upper'),
                    position=position_dodge(width=width_combined_data),
                    width=width_combined_data) \
    + labs(title='Grouped Means Combined') \
    + ylab('Td [ms]') \
    + scale_x_discrete(
        limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 'after_pt_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre',
                'supine_1_post', 'before_warmup_post', 'after_warmup_post', 'after_pt_post','s1_post', 's2_post', 's3_post',
                's4_post', 's5_post', 's6_post', 's7_post', 'supine_2_post', 'supine_3_post', 'supine_4_post'],
        labels=['Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                'After S5', 'After S6', 'After S7', 'After S8', 'Supine 2', 'Supine 3', 'Supine 4',
                'Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                'After S5', 'After S6', 'After S7', 'Supine 2', 'Supine 3', 'Supine 4']
    ) + theme_minimal()

# Größe des Plots anpassen
combined_plot = combined_plot + ggsize(1000, 400)  # Hier die Größe nach Ihren Bedürfnissen anpassen

# Das kombinierte Plot anzeigen oder speichern
combined_plot.show()


## Mit gut sichtbarem overall mean und std

In [197]:
# Spalten 'Td' und 'Td_std' kombinieren
combined_data['Td_lower'] = combined_data['Td'] - combined_data['Td_std']
combined_data['Td_upper'] = combined_data['Td'] + combined_data['Td_std']

# Spalten für Fehlerbalken in overall_means_pre_post hinzufügen
overall_means_pre_post['lower'] = overall_means_pre_post['Td_mean_total'] - overall_means_pre_post['Td_std_total']
overall_means_pre_post['upper'] = overall_means_pre_post['Td_mean_total'] + overall_means_pre_post['Td_std_total']

width_combined_data = 0.6
width_overall_means = 0.3  # Ändern Sie dies, wenn nötig

# Plot erstellen
combined_plot = ggplot() \
    + geom_point(data=combined_data, mapping=aes(x='measurement', y='Td', color='group', group='group'),
                 position=position_dodge(width=1.2)) \
    + geom_line(data=combined_data, mapping=aes(x='measurement', y='Td', color='group', group='group'),
                position=position_dodge(width=1.2)) \
    + geom_errorbar(data=combined_data,
                    mapping=aes(x='measurement', y='Td', color='group', group='group', ymin='Td_lower', ymax='Td_upper'),
                    position=position_dodge(width=1.2),
                    width=width_combined_data) \
    + geom_point(data=overall_means_pre_post,
                 mapping=aes(x='measurement', y='Td_mean_total')) \
    + geom_line(data=overall_means_pre_post, mapping=aes(x='measurement', y='Td_mean_total')) \
    + geom_errorbar(data=overall_means_pre_post,
                    mapping=aes(x='measurement', y='Td_mean_total', ymin='lower', ymax='upper'),
                    width=width_overall_means,
                    position=position_dodge(width=width_combined_data),  # Beachten Sie die Verwendung von width_combined_data hier
                    color='black') \
    + labs(title='Grouped Means Combined') \
    + ylab('Td [ms]') \
    + scale_x_discrete(
        limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 'after_pt_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre',
                'supine_1_post', 'before_warmup_post', 'after_warmup_post', 'after_pt_post','s1_post', 's2_post', 's3_post',
                's4_post', 's5_post', 's6_post', 's7_post', 'supine_2_post', 'supine_3_post', 'supine_4_post'],
        labels=['Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                'After S5', 'After S6', 'After S7', 'After S8', 'Supine 2', 'Supine 3', 'Supine 4',
                'Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                'After S5', 'After S6', 'After S7', 'Supine 2', 'Supine 3', 'Supine 4']
    ) + theme_minimal()

# Größe des Plots anpassen
combined_plot = combined_plot + ggsize(1000, 400)  # Hier die Größe nach Ihren Bedürfnissen anpassen

# Das kombinierte Plot anzeigen oder speichern
combined_plot.show()


## overall means und std ausgefadet

In [201]:
# Spalten 'Td' und 'Td_std' kombinieren
combined_data['Td_lower'] = combined_data['Td'] - combined_data['Td_std']
combined_data['Td_upper'] = combined_data['Td'] + combined_data['Td_std']

# Spalten für Fehlerbalken in overall_means_pre_post hinzufügen
overall_means_pre_post['lower'] = overall_means_pre_post['Td_mean_total'] - overall_means_pre_post['Td_std_total']
overall_means_pre_post['upper'] = overall_means_pre_post['Td_mean_total'] + overall_means_pre_post['Td_std_total']

width_combined_data = 0.6
width_overall_means = 0.3  # Ändern Sie dies, wenn nötig

# Plot erstellen
combined_plot = ggplot() \
    + geom_point(data=combined_data, mapping=aes(x='measurement', y='Td', color='group', group='group'),
                 position=position_dodge(width=1.2)) \
    + geom_line(data=combined_data, mapping=aes(x='measurement', y='Td', color='group', group='group'),
                position=position_dodge(width=1.2)) \
    + geom_errorbar(data=combined_data,
                    mapping=aes(x='measurement', y='Td', color='group', group='group', ymin='Td_lower', ymax='Td_upper'),
                    position=position_dodge(width=1.2),
                    width=width_combined_data) \
    + geom_point(data=overall_means_pre_post,
                 mapping=aes(x='measurement', y='Td_mean_total'), alpha=0.5) \
    + geom_line(data=overall_means_pre_post, mapping=aes(x='measurement', y='Td_mean_total'), alpha=0.5) \
    + geom_errorbar(data=overall_means_pre_post,
                    mapping=aes(x='measurement', y='Td_mean_total', ymin='lower', ymax='upper'),
                    width=width_overall_means,
                    position=position_dodge(width=width_combined_data),  # Beachten Sie die Verwendung von width_combined_data hier
                    color='black', alpha=0.5) \
    + labs(title='Grouped Means Combined') \
    + ylab('Td [ms]') \
    + scale_x_discrete(
        limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 'after_pt_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre',
                'supine_1_post', 'before_warmup_post', 'after_warmup_post', 'after_pt_post','s1_post', 's2_post', 's3_post',
                's4_post', 's5_post', 's6_post', 's7_post', 'supine_2_post', 'supine_3_post', 'supine_4_post'],
        labels=['Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                'After S5', 'After S6', 'After S7', 'After S8', 'Supine 2', 'Supine 3', 'Supine 4',
                'Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                'After S5', 'After S6', 'After S7', 'Supine 2', 'Supine 3', 'Supine 4']
    ) + theme_minimal()

# Größe des Plots anpassen
combined_plot = combined_plot + ggsize(1000, 400)  # Hier die Größe nach Ihren Bedürfnissen anpassen

# Das kombinierte Plot anzeigen oder speichern
combined_plot.show()


### mit Grupenunterschieden gedämpft

In [200]:
# Spalten 'Td' und 'Td_std' kombinieren
combined_data['Td_lower'] = combined_data['Td'] - combined_data['Td_std']
combined_data['Td_upper'] = combined_data['Td'] + combined_data['Td_std']

# Spalten für Fehlerbalken in overall_means_pre_post hinzufügen
overall_means_pre_post['lower'] = overall_means_pre_post['Td_mean_total'] - overall_means_pre_post['Td_std_total']
overall_means_pre_post['upper'] = overall_means_pre_post['Td_mean_total'] + overall_means_pre_post['Td_std_total']

width_combined_data = 0.6
width_overall_means = 0.3  # Ändern Sie dies, wenn nötig
alpha = 0.3

# Plot erstellen
combined_plot = ggplot() \
    + geom_point(data=combined_data, mapping=aes(x='measurement', y='Td', color='group', group='group'), alpha=alpha,
                 position=position_dodge(width=1.2)) \
    + geom_line(data=combined_data, mapping=aes(x='measurement', y='Td', color='group', group='group'), alpha=alpha,
                position=position_dodge(width=1.2)) \
    + geom_errorbar(data=combined_data,
                    mapping=aes(x='measurement', y='Td', color='group', group='group', ymin='Td_lower', ymax='Td_upper'), alpha=alpha,
                    position=position_dodge(width=1.2),
                    width=width_combined_data) \
    + geom_point(data=overall_means_pre_post,
                 mapping=aes(x='measurement', y='Td_mean_total')) \
    + geom_line(data=overall_means_pre_post, mapping=aes(x='measurement', y='Td_mean_total')) \
    + geom_errorbar(data=overall_means_pre_post,
                    mapping=aes(x='measurement', y='Td_mean_total', ymin='lower', ymax='upper'),
                    width=width_overall_means,
                    position=position_dodge(width=width_combined_data),  # Beachten Sie die Verwendung von width_combined_data hier
                    color='black') \
    + labs(title='Grouped Means Combined') \
    + ylab('Td [ms]') \
    + scale_x_discrete(
        limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 'after_pt_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre',
                'supine_1_post', 'before_warmup_post', 'after_warmup_post', 'after_pt_post','s1_post', 's2_post', 's3_post',
                's4_post', 's5_post', 's6_post', 's7_post', 'supine_2_post', 'supine_3_post', 'supine_4_post'],
        labels=['Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                'After S5', 'After S6', 'After S7', 'After S8', 'Supine 2', 'Supine 3', 'Supine 4',
                'Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                'After S5', 'After S6', 'After S7', 'Supine 2', 'Supine 3', 'Supine 4']
    ) + theme_minimal()

# Größe des Plots anpassen
combined_plot = combined_plot + ggsize(1000, 400)  # Hier die Größe nach Ihren Bedürfnissen anpassen

# Das kombinierte Plot anzeigen oder speichern
combined_plot.show()


In [158]:
overall_means_pre_post.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 29 entries, 0 to 28
Data columns (total 16 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   measurement     29 non-null     object 
 1   Dm_mean_total   29 non-null     float64
 2   Td_mean_total   29 non-null     float64
 3   Tc_mean_total   29 non-null     float64
 4   Ts_mean_total   29 non-null     float64
 5   Tr_mean_total   29 non-null     float64
 6   Vc_mean_total   29 non-null     float64
 7   Dm_std_total    26 non-null     float64
 8   Td_std_total    26 non-null     float64
 9   Tc_std_total    26 non-null     float64
 10  Ts_std_total    26 non-null     float64
 11  Tr_std_total    26 non-null     float64
 12  Vc_std_total    26 non-null     float64
 13  lower           26 non-null     float64
 14  upper           26 non-null     float64
 15  facet_variable  29 non-null     object 
dtypes: float64(14), object(2)
memory usage: 3.8+ KB


In [156]:
combined_data

index     group         measurement         Dm         Td         Tc  \
0       0  beta_ala        after_pt_pre   3.533491  19.833333  37.166667   
1      24   placebo              s7_pre   1.622107  19.000000  33.000000   
2      23   placebo              s6_pre   1.914523  22.000000  40.000000   
3      22   placebo              s5_pre   1.856557  21.500000  39.500000   
4      21   placebo              s4_pre   1.769553  22.666667  41.000000   
5      19   placebo              s2_pre   2.039166  21.083333  41.916667   
6      18   placebo              s1_pre   2.472695  21.000000  40.083333   
7      17   placebo   before_warmup_pre   3.829941  22.000000  43.583333   
8      16   placebo    after_warmup_pre   3.037717  19.083333  37.250000   
9      15   placebo        after_pt_pre   2.812309  18.916667  35.666667   
10     20   placebo              s3_pre   2.303125  22.142857  43.571429   
11     10  beta_ala              s8_pre   2.968527  24.000000  45.000000   
12      9  beta_ala              s7_pre   3.147331  25.000000  47.000000   
13      8  beta_ala              s6_pre   2.124360  24.000000  47.000000   
14      7  beta_ala              s5_pre   1.766564  21.500000  43.000000   
15      6  beta_ala              s4_pre   1.494490  18.400000  38.200000   
16      5  beta_ala              s3_pre   2.203173  22.000000  41.333333   
17      1  beta_ala    after_warmup_pre   3.386012  19.750000  37.666667   
18      4  beta_ala              s2_pre   2.571748  21.666667  40.333333   
19      3  beta_ala              s1_pre   2.894438  21.000000  39.583333   
20      2  beta_ala   before_warmup_pre   4.400203  22.666667  44.250000   
21     52   placebo             s7_post   1.993434  19.000000  34.000000   
22     33  beta_ala             s2_post   1.986138  21.363636  40.000000   
23     34  beta_ala             s3_post   1.851975  22.000000  41.000000   
24     35  beta_ala             s4_post   1.920227  22.166667  41.833333   
25     36  beta_ala             s5_post   1.720080  20.500000  42.000000   
26     37  beta_ala             s6_post   1.442091  21.500000  40.500000   
27     38  beta_ala             s7_post   0.451110  18.000000  38.000000   
28     32  beta_ala             s1_post   2.933943  20.833333  39.166667   
29     31  beta_ala  before_warmup_post   4.208709  21.833333  42.666667   
30     48   placebo             s3_post   1.804247  20.142857  37.571429   
31     29  beta_ala       after_pt_post   3.266084  19.750000  36.833333   
32     45   placebo  before_warmup_post   3.805998  21.666667  43.000000   
33     46   placebo             s1_post   2.437862  20.583333  39.166667   
34     47   placebo             s2_post   2.420578  21.200000  41.200000   
35     44   placebo   after_warmup_post   3.029256  18.833333  35.250000   
36     49   placebo             s4_post   1.310746  19.800000  36.200000   
37     50   placebo             s5_post   1.813214  18.000000  33.000000   
38     51   placebo             s6_post   2.043895  19.000000  34.000000   
39     30  beta_ala   after_warmup_post   3.410634  19.583333  37.000000   
40     43   placebo       after_pt_post   2.986148  19.000000  35.250000   
41     28   placebo        supine_4_pre   8.792722  27.416667  55.416667   
42     27   placebo        supine_3_pre   8.770231  27.250000  56.916667   
43     26   placebo        supine_2_pre   6.935313  26.000000  54.083333   
44     25   placebo        supine_1_pre   9.084233  26.666667  55.166667   
45     14  beta_ala        supine_4_pre   9.888181  27.916667  55.500000   
46     13  beta_ala        supine_3_pre  10.081916  28.500000  57.416667   
47     12  beta_ala        supine_2_pre   7.615728  27.250000  53.000000   
48     11  beta_ala        supine_1_pre  10.390159  28.083333  55.250000   
49     42  beta_ala       supine_4_post   9.920126  28.166667  54.083333   
50     40  beta_ala       supine_2_post   7.898109  27.583333  54.166667   
51     39  beta_ala       supine_1_post   9.977693  

# Plot Auswahl: Uns interessiert der Interaktionseffekt.

In [216]:
# Lets-Plot-Objekt erstellen
combined_td = ggplot(combined_data, aes(x='measurement', y='Td', color='group', group='group')) \
        + geom_point(position=position_dodge(width=0.4)) \
        + geom_line(position=position_dodge(width=0.4)) \
        + geom_errorbar(
            aes(ymin=combined_data['Td'] - combined_data['Td_std'],
                ymax=combined_data['Td'] + combined_data['Td_std'],
                fill='group'),
            position=position_dodge(width=0.4),
            linetype="blank"
        ) \
        + facet_grid(y='category', scales='free_y') \
        + labs(title='Grouped Means Combined') \
        + ylab('Td [ms]') \
        + scale_x_discrete(
            limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 'after_pt_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                    's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre',
                    'supine_1_post', 'before_warmup_post', 'after_warmup_post', 'after_pt_post','s1_post', 's2_post', 's3_post',
                    's4_post', 's5_post', 's6_post', 's7_post', 'supine_2_post', 'supine_3_post', 'supine_4_post'],
            labels=['Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                    'After S5', 'After S6', 'After S7', 'After S8', 'Supine 2', 'Supine 3', 'Supine 4',
                    'Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                    'After S5', 'After S6', 'After S7', 'Supine 2', 'Supine 3', 'Supine 4']
        ) \

combined_td = combined_td + ggsize(1000, 600)

# Das kombinierte Plot anzeigen oder speichern
combined_td.show()

In [217]:
# Lets-Plot-Objekt erstellen
combined_tc = ggplot(combined_data, aes(x='measurement', y='Tc', color='group', group='group')) \
        + geom_point(position=position_dodge(width=0.4)) \
        + geom_line(position=position_dodge(width=0.4)) \
        + geom_errorbar(
            aes(ymin=combined_data['Tc'] - combined_data['Tc_std'],
                ymax=combined_data['Tc'] + combined_data['Tc_std'],
                fill='group'),
            position=position_dodge(width=0.4),
            linetype="blank"
        ) \
        + facet_grid(y='category', scales='free_y') \
        + labs(title='Tc') \
        + ylab('Tc [ms]') \
        + scale_x_discrete(
            limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 'after_pt_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                    's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre',
                    'supine_1_post', 'before_warmup_post', 'after_warmup_post', 'after_pt_post','s1_post', 's2_post', 's3_post',
                    's4_post', 's5_post', 's6_post', 's7_post', 'supine_2_post', 'supine_3_post', 'supine_4_post'],
            labels=['Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                    'After S5', 'After S6', 'After S7', 'After S8', 'Supine 2', 'Supine 3', 'Supine 4',
                    'Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                    'After S5', 'After S6', 'After S7', 'Supine 2', 'Supine 3', 'Supine 4']
        ) \

combined_tc = combined_tc + ggsize(1000, 600)

# Das kombinierte Plot anzeigen oder speichern
combined_tc.show()

In [218]:
# Lets-Plot-Objekt erstellen
combined_ts = ggplot(combined_data, aes(x='measurement', y='Ts', color='group', group='group')) \
        + geom_point(position=position_dodge(width=0.4)) \
        + geom_line(position=position_dodge(width=0.4)) \
        + geom_errorbar(
            aes(ymin=combined_data['Ts'] - combined_data['Ts_std'],
                ymax=combined_data['Ts'] + combined_data['Ts_std'],
                fill='group'),
            position=position_dodge(width=0.4),
            linetype="blank"
        ) \
        + facet_grid(y='category', scales='free_y') \
        + labs(title='Ts') \
        + ylab('Ts [ms]') \
        + scale_x_discrete(
            limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 'after_pt_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                    's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre',
                    'supine_1_post', 'before_warmup_post', 'after_warmup_post', 'after_pt_post','s1_post', 's2_post', 's3_post',
                    's4_post', 's5_post', 's6_post', 's7_post', 'supine_2_post', 'supine_3_post', 'supine_4_post'],
            labels=['Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                    'After S5', 'After S6', 'After S7', 'After S8', 'Supine 2', 'Supine 3', 'Supine 4',
                    'Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                    'After S5', 'After S6', 'After S7', 'Supine 2', 'Supine 3', 'Supine 4']
        ) \

combined_ts = combined_ts + ggsize(1000, 600)

# Das kombinierte Plot anzeigen oder speichern
combined_ts.show()

In [219]:
# Lets-Plot-Objekt erstellen
combined_tr = ggplot(combined_data, aes(x='measurement', y='Tr', color='group', group='group')) \
        + geom_point(position=position_dodge(width=0.4)) \
        + geom_line(position=position_dodge(width=0.4)) \
        + geom_errorbar(
            aes(ymin=combined_data['Tr'] - combined_data['Tr_std'],
                ymax=combined_data['Tr'] + combined_data['Tr_std'],
                fill='group'),
            position=position_dodge(width=0.4),
            linetype="blank"
        ) \
        + facet_grid(y='category', scales='free_y') \
        + labs(title='Tr') \
        + ylab('Tr [ms]') \
        + scale_x_discrete(
            limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 'after_pt_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                    's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre',
                    'supine_1_post', 'before_warmup_post', 'after_warmup_post', 'after_pt_post','s1_post', 's2_post', 's3_post',
                    's4_post', 's5_post', 's6_post', 's7_post', 'supine_2_post', 'supine_3_post', 'supine_4_post'],
            labels=['Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                    'After S5', 'After S6', 'After S7', 'After S8', 'Supine 2', 'Supine 3', 'Supine 4',
                    'Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                    'After S5', 'After S6', 'After S7', 'Supine 2', 'Supine 3', 'Supine 4']
        ) \

combined_tr = combined_tr + ggsize(1000, 600)

# Das kombinierte Plot anzeigen oder speichern
combined_tr.show()

In [220]:
# Lets-Plot-Objekt erstellen
combined_vc = ggplot(combined_data, aes(x='measurement', y='Vc', color='group', group='group')) \
        + geom_point(position=position_dodge(width=0.4)) \
        + geom_line(position=position_dodge(width=0.4)) \
        + geom_errorbar(
            aes(ymin=combined_data['Vc'] - combined_data['Vc_std'],
                ymax=combined_data['Vc'] + combined_data['Vc_std'],
                fill='group'),
            position=position_dodge(width=0.4),
            linetype="blank"
        ) \
        + facet_grid(y='category', scales='free_y') \
        + labs(title='Vc') \
        + ylab('Vc [mm/ms]') \
        + scale_x_discrete(
            limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 'after_pt_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                    's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre',
                    'supine_1_post', 'before_warmup_post', 'after_warmup_post', 'after_pt_post','s1_post', 's2_post', 's3_post',
                    's4_post', 's5_post', 's6_post', 's7_post', 'supine_2_post', 'supine_3_post', 'supine_4_post'],
            labels=['Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                    'After S5', 'After S6', 'After S7', 'After S8', 'Supine 2', 'Supine 3', 'Supine 4',
                    'Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                    'After S5', 'After S6', 'After S7', 'Supine 2', 'Supine 3', 'Supine 4']
        ) \

combined_vc = combined_vc + ggsize(1000, 600)

# Das kombinierte Plot anzeigen oder speichern
combined_vc.show()

In [221]:
# Lets-Plot-Objekt erstellen
combined_dm = ggplot(combined_data, aes(x='measurement', y='Dm', color='group', group='group')) \
        + geom_point(position=position_dodge(width=0.4)) \
        + geom_line(position=position_dodge(width=0.4)) \
        + geom_errorbar(
            aes(ymin=combined_data['Dm'] - combined_data['Dm_std'],
                ymax=combined_data['Dm'] + combined_data['Dm_std'],
                fill='group'),
            position=position_dodge(width=0.4),
            linetype="blank"
        ) \
        + facet_grid(y='category', scales='free_y') \
        + labs(title='Dm') \
        + ylab('Dm [mm]') \
        + scale_x_discrete(
            limits=['supine_1_pre', 'before_warmup_pre', 'after_warmup_pre', 'after_pt_pre', 's1_pre', 's2_pre', 's3_pre', 's4_pre',
                    's5_pre', 's6_pre', 's7_pre', 's8_pre','supine_2_pre', 'supine_3_pre', 'supine_4_pre',
                    'supine_1_post', 'before_warmup_post', 'after_warmup_post', 'after_pt_post','s1_post', 's2_post', 's3_post',
                    's4_post', 's5_post', 's6_post', 's7_post', 'supine_2_post', 'supine_3_post', 'supine_4_post'],
            labels=['Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                    'After S5', 'After S6', 'After S7', 'After S8', 'Supine 2', 'Supine 3', 'Supine 4',
                    'Supine 1', 'Before Warmup', 'After Warmup', 'After Peak-Torque', 'After S1', 'After S2', 'After S3', 'After S4',
                    'After S5', 'After S6', 'After S7', 'Supine 2', 'Supine 3', 'Supine 4']
        ) \

combined_dm = combined_dm + ggsize(1000, 600)

# Das kombinierte Plot anzeigen oder speichern
combined_dm.show()

In [231]:
#ggsave(combined_vc, filename='plot_vc.svg')

'C:\\Users\\bvenn\\lets-plot-images\\plot_vc.svg'

In [14]:
tmg_parameter.head()

id     group experiment    measurement        Dm    Td    Tc     Ts  \
0  15073  beta_ala   posttest       supine_1  9.949456  31.0  56.0   77.0   
1  15073  beta_ala   posttest  before_warmup  2.989571  23.0  49.0  179.0   
2  15073  beta_ala   posttest   after_warmup  2.272929  20.0  43.0  194.0   
3  15073  beta_ala   posttest       after_pt  1.812468  19.0  40.0  167.0   
4  15073  beta_ala   posttest             s1  0.742931  16.0  33.0   26.0   

      Tr        Vc  
0   46.0  0.114362  
1  146.0  0.041522  
2   36.0  0.036078  
3  138.0  0.030720  
4    7.0  0.015162

# Supine Plots für Publikation

In [7]:
relevant_measurements = ['supine_1_pre', 'supine_2_pre', 'supine_3_pre', 'supine_4_pre',
                         'supine_1_post', 'supine_2_post', 'supine_3_post', 'supine_4_post']
filtered_data = tmg_parameter[tmg_parameter['measurement'].isin(relevant_measurements)]

filtered_data = filtered_data.sort_values(by=['id', 'group', 'experiment']).reset_index(drop=True)
pretest_data = filtered_data[filtered_data['experiment'] == 'pretest']
posttest_data = filtered_data[filtered_data['experiment'] == 'posttest']


In [8]:
pretest_data = pretest_data.reset_index(drop=True)
pretest_data

id     group experiment   measurement         Dm    Td    Tc     Ts  \
0   15073  beta_ala    pretest  supine_1_pre   9.726150  31.0  57.0  106.0   
1   15073  beta_ala    pretest  supine_2_pre   5.774841  28.0  56.0   98.0   
2   15073  beta_ala    pretest  supine_3_pre   9.100387  30.0  57.0  149.0   
3   15073  beta_ala    pretest  supine_4_pre   9.112594  29.0  59.0  104.0   
4   20438  beta_ala    pretest  supine_1_pre  10.232495  26.0  50.0   44.0   
..    ...       ...        ...           ...        ...   ...   ...    ...   
91  93302   placebo    pretest  supine_4_pre   7.584031  27.0  56.0   51.0   
92  93672  beta_ala    pretest  supine_1_pre  11.228515  26.0  53.0  172.0   
93  93672  beta_ala    pretest  supine_2_pre   8.410425  25.0  51.0  137.0   
94  93672  beta_ala    pretest  supine_3_pre  11.591811  25.0  54.0  144.0   
95  93672  beta_ala    pretest  supine_4_pre  11.039604  26.0  55.0  177.0   

       Tr        Vc  
0    72.0  0.110524  
1    56.0  0.068748  
2   110.0  0.104602  
3    64.0  0.103552  
4    19.0  0.134638  
..    ...       ...  
91   21.0  0.091374  
92  140.0  0.142133  
93  103.0  0.110663  
94  111.0  0.146732  
95  142.0  0.136291  

[96 rows x 10 columns]

In [9]:
posttest_data = posttest_data.reset_index(drop=True)
posttest_data

id     group experiment    measurement         Dm    Td    Tc     Ts  \
0   15073  beta_ala   posttest  supine_1_post   9.949456  31.0  56.0   77.0   
1   15073  beta_ala   posttest  supine_2_post   6.965459  28.0  57.0   86.0   
2   15073  beta_ala   posttest  supine_3_post   8.982938  30.0  57.0  140.0   
3   15073  beta_ala   posttest  supine_4_post   9.926545  30.0  56.0  124.0   
4   20438  beta_ala   posttest  supine_1_post   8.599606  27.0  52.0   49.0   
..    ...       ...        ...            ...        ...   ...   ...    ...   
91  93302   placebo   posttest  supine_4_post   8.152583  25.0  53.0   49.0   
92  93672  beta_ala   posttest  supine_1_post  10.276126  25.0  49.0  173.0   
93  93672  beta_ala   posttest  supine_2_post   9.089581  25.0  50.0  153.0   
94  93672  beta_ala   posttest  supine_3_post  11.476495  26.0  54.0  136.0   
95  93672  beta_ala   posttest  supine_4_post  10.923639  26.0  52.0  179.0   

       Tr        Vc  
0    46.0  0.114362  
1    46.0  0.081947  
2   104.0  0.103252  
3    88.0  0.115425  
4    21.0  0.108856  
..    ...       ...  
91   19.0  0.104520  
92  142.0  0.138867  
93  123.0  0.121194  
94  105.0  0.143456  
95  147.0  0.140047  

[96 rows x 10 columns]

In [10]:
result_data = pd.DataFrame()

# Hinzufügen von 'group', 'measurement' und 'id'
result_data['group'] = pretest_data['group']
result_data['measurement'] = pretest_data['measurement']
result_data['id'] = pretest_data['id']

# Berechnung der Differenzen für alle Parameter
diff_columns = ['Dm', 'Td', 'Tc', 'Ts', 'Tr', 'Vc']
for col in diff_columns:
    result_data[f'diff_{col}'] = posttest_data[col] - pretest_data[col]

# Anzeigen des Ergebnisses
result_data

group   measurement     id   diff_Dm  diff_Td  diff_Tc  diff_Ts  \
0   beta_ala  supine_1_pre  15073  0.223306      0.0     -1.0    -29.0   
1   beta_ala  supine_2_pre  15073  1.190617      0.0      1.0    -12.0   
2   beta_ala  supine_3_pre  15073 -0.117449      0.0      0.0     -9.0   
3   beta_ala  supine_4_pre  15073  0.813951      1.0     -3.0     20.0   
4   beta_ala  supine_1_pre  20438 -1.632890      1.0      2.0      5.0   
..       ...           ...    ...       ...      ...      ...      ...   
91   placebo  supine_4_pre  93302  0.568552     -2.0     -3.0     -2.0   
92  beta_ala  supine_1_pre  93672 -0.952389     -1.0     -4.0      1.0   
93  beta_ala  supine_2_pre  93672  0.679156      0.0     -1.0     16.0   
94  beta_ala  supine_3_pre  93672 -0.115316      1.0      0.0     -8.0   
95  beta_ala  supine_4_pre  93672 -0.115965      0.0     -3.0      2.0   

    diff_Tr   diff_Vc  
0     -26.0  0.003837  
1     -10.0  0.013198  
2      -6.0 -0.001350  
3      24.0  0.011873  
4       2.0 -0.025782  
..      ...       ...  
91     -2.0  0.013146  
92      2.0 -0.003267  
93     20.0  0.010531  
94     -6.0 -0.003276  
95      5.0  0.003755  

[96 rows x 9 columns]

In [11]:
mean_std_supine = result_data.groupby(['group', 'measurement']).agg({
    'diff_Dm': ['mean', 'std'],
    'diff_Td': ['mean', 'std'],
    'diff_Tc': ['mean', 'std'],
    'diff_Ts': ['mean', 'std'],
    'diff_Tr': ['mean', 'std'],
    'diff_Vc': ['mean', 'std'],    
})

mean_std_supine = mean_std_supine.reset_index()
mean_std_supine.columns = ['group', 'measurement',
                           'diff_Dm_mean', 'diff_Dm_std',
                           'diff_Td_mean', 'diff_Td_std',
                           'diff_Tc_mean', 'diff_Tc_std',
                           'diff_Ts_mean', 'diff_Ts_std',
                           'diff_Tr_mean', 'diff_Tr_std',
                           'diff_Vc_mean', 'diff_Vc_std']
mean_std_supine

C:\Users\bvenn\AppData\Local\Temp\ipykernel_8444\1810155329.py:1: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  mean_std_supine = result_data.groupby(['group', 'measurement']).agg({


group   measurement  diff_Dm_mean  diff_Dm_std  diff_Td_mean  \
0  beta_ala  supine_1_pre     -0.412466     1.231345     -0.083333   
1  beta_ala  supine_2_pre      0.282381     0.695844      0.333333   
2  beta_ala  supine_3_pre     -0.603422     1.364757      0.000000   
3  beta_ala  supine_4_pre      0.031945     0.772378      0.250000   
4   placebo  supine_1_pre     -0.198761     1.967166      0.000000   
5   placebo  supine_2_pre      0.355708     1.478547     -0.583333   
6   placebo  supine_3_pre     -0.245030     1.698245      0.000000   
7   placebo  supine_4_pre     -0.070708     1.736899     -0.333333   

   diff_Td_std  diff_Tc_mean  diff_Tc_std  diff_Ts_mean  diff_Ts_std  \
0     0.996205     -1.416667     3.396745      0.583333    25.903521   
1     2.964436      1.166667     4.302924      5.750000    15.903830   
2     2.044949     -1.166667     3.040136      6.083333    26.005099   
3     0.866025     -1.416667     1.975225     -1.583333    48.299178   
4     1.809068     -1.583333     5.991787    -13.750000    41.209277   
5     1.443376     -1.416667     4.601548     -2.583333    23.157399   
6     1.595448      0.333333     3.284491    -19.500000    45.364183   
7     1.723281      0.333333     4.996969    -17.000000    45.889195   

   diff_Tr_mean  diff_Tr_std  diff_Vc_mean  diff_Vc_std  
0      2.666667    29.370156     -0.002972     0.016618  
1      3.750000    16.153384      0.002103     0.013790  
2      4.916667    28.398010     -0.005608     0.019043  
3     -1.166667    45.934406      0.001509     0.009516  
4     -9.333333    40.614224      0.000280     0.028788  
5     -1.416667    22.837204      0.006553     0.019645  
6    -12.250000    49.900128     -0.002420     0.020470  
7    -15.750000    47.342322     -0.000465     0.023840

In [12]:
# extrahieren des data frames mit differenzen
#result_data.to_excel(r"C:\Users\bvenn\OneDrive\Desktop\Publikation\Dataframe\differences_supine.xlsx")

In [19]:
(
    ggplot(result_data, aes(x='measurement', y='diff_Td', color='group'))
    + geom_boxplot(width=0.5)
    + ylab('Td Difference [ms]')
    + scale_x_discrete(labels=['Supine 1', 'Supine 2', 'Supine 3', 'Supine 4',])
)

In [20]:
# distribution
(
    ggplot(result_data, aes(x='diff_Td'))
    + geom_histogram()
    + ylab('Td Difference [ms]')
)

In [26]:
Td_stat = pg.mixed_anova(dv='diff_Td',between='group', within='measurement', subject='id', data=result_data, correction='auto', effsize='np2')
Td_stat

Source        SS  DF1  DF2        MS         F     p-unc       np2  \
0        group  3.010417    1   22  3.010417  0.621992  0.438725  0.027495   
1  measurement  0.197917    3   66  0.065972  0.024890  0.994639  0.001130   
2  Interaction  4.114583    3   66  1.371528  0.517447  0.671719  0.022980   

        eps  
0       NaN  
1  0.916476  
2       NaN

In [21]:
(
    ggplot(result_data, aes(x='measurement', y='diff_Tc', color='group'))
    + geom_boxplot(width=0.5)
    + ylab('Tc Difference [ms]')
    + scale_x_discrete(labels=['Supine 1', 'Supine 2', 'Supine 3', 'Supine 4',])
)

In [29]:
# distribution
(
    ggplot(result_data, aes(x='diff_Tc'))
    + geom_histogram()
    + ylab('Td Diff [ms]')
)

In [30]:
Tc_stat = pg.mixed_anova(dv='diff_Tc',between='group', within='measurement', subject='id', data=result_data, correction='auto', effsize='np2')
Tc_stat

Source         SS  DF1  DF2         MS         F     p-unc       np2  \
0        group   0.375000    1   22   0.375000  0.015534  0.901943  0.000706   
1  measurement  25.541667    3   66   8.513889  0.582146  0.628810  0.025779   
2  Interaction  71.708333    3   66  23.902778  1.634378  0.189841  0.069153   

        eps  
0       NaN  
1  0.886621  
2       NaN

In [22]:
(
    ggplot(result_data, aes(x='measurement', y='diff_Dm', color='group'))
    + geom_boxplot(width=0.5)
    + ylab('Dm Difference [mm]')
    + scale_x_discrete(labels=['Supine 1', 'Supine 2', 'Supine 3', 'Supine 4',])
)

In [32]:
# distribution
(
    ggplot(result_data, aes(x='diff_Dm'))
    + geom_histogram()
    + ylab('Td Diff [ms]')
)

In [33]:
Dm_stat = pg.mixed_anova(dv='diff_Dm',between='group', within='measurement', subject='id', data=result_data, correction='auto', effsize='np2')
Dm_stat

Source        SS  DF1  DF2        MS         F     p-unc       np2  \
0        group  0.441899    1   22  0.441899  0.096011  0.759586  0.004345   
1  measurement  7.902471    3   66  2.634157  2.191772  0.097258  0.090600   
2  Interaction  0.698274    3   66  0.232758  0.193668  0.900355  0.008726   

        eps  
0       NaN  
1  0.945033  
2       NaN

In [23]:
(
    ggplot(result_data, aes(x='measurement', y='diff_Ts', color='group'))
    + geom_boxplot(width=0.5)
    + ylab('Ts Difference [ms]')
    + scale_x_discrete(labels=['Supine 1', 'Supine 2', 'Supine 3', 'Supine 4',])
)

In [38]:
# distribution
(
    ggplot(result_data, aes(x='diff_Ts'))
    + geom_histogram()
    + ylab('Ts Diff [ms]')
)

In [39]:
Ts_stat = pg.mixed_anova(dv='diff_Ts',between='group', within='measurement', subject='id', data=result_data, correction='auto', effsize='np2')
Ts_stat

Source           SS  DF1  DF2           MS         F     p-unc  \
0        group  6080.166667    1   22  6080.166667  3.037713  0.095313   
1  measurement  1606.416667    3   66   535.472222  0.507711  0.678321   
2  Interaction   922.250000    3   66   307.416667  0.291479  0.831402   

        np2      eps  
0  0.121325      NaN  
1  0.022557  0.82267  
2  0.013076      NaN

In [24]:
(
    ggplot(result_data, aes(x='measurement', y='diff_Tr', color='group'))
    + geom_boxplot(width=0.5)
    + ylab('Tr Difference [ms]')
    + scale_x_discrete(labels=['Supine 1', 'Supine 2', 'Supine 3', 'Supine 4',])
)

In [41]:
# distribution
(
    ggplot(result_data, aes(x='diff_Tr'))
    + geom_histogram()
    + ylab('Tr Diff [ms]')
)

In [42]:
Tr_stat = pg.mixed_anova(dv='diff_Tr',between='group', within='measurement', subject='id', data=result_data, correction='auto', effsize='np2')
Tr_stat

Source           SS  DF1  DF2           MS         F     p-unc  \
0        group  3589.260417    1   22  3589.260417  1.681529  0.208158   
1  measurement  1113.531250    3   66   371.177083  0.333728  0.800977   
2  Interaction   479.114583    3   66   159.704861  0.143592  0.933427   

   p-GG-corr       np2       eps sphericity   W-spher   p-spher  
0        NaN  0.071006       NaN        NaN       NaN       NaN  
1   0.748283  0.014943  0.805833      False  0.574002  0.034171  
2        NaN  0.006485       NaN        NaN       NaN       NaN

In [25]:
(
    ggplot(result_data, aes(x='measurement', y='diff_Vc', color='group'))
    + geom_boxplot(width=0.5)
    + ylab('Vc Difference [mm/ms]')
    + scale_x_discrete(labels=['Supine 1', 'Supine 2', 'Supine 3', 'Supine 4',])
)

In [44]:
# distribution
(
    ggplot(result_data, aes(x='diff_Vc'))
    + geom_histogram()
    + ylab('Vc Diff [mm/ms]')
)

In [45]:
Vc_stat = pg.mixed_anova(dv='diff_Vc',between='group', within='measurement', subject='id', data=result_data, correction='auto', effsize='np2')
Vc_stat

C:\Users\bvenn\AppData\Roaming\Python\Python311\site-packages\pingouin\distribution.py:1004: RuntimeWarning: divide by zero encountered in scalar divide
  W = np.prod(eig) / (eig.sum() / d) ** d


Source        SS  DF1  DF2        MS         F     p-unc       np2  \
0        group  0.000119    1   22  0.000119  0.128531  0.723377  0.005808   
1  measurement  0.000885    3   66  0.000295  1.397414  0.251395  0.059725   
2  Interaction  0.000147    3   66  0.000049  0.232779  0.873229  0.010470   

        eps  
0       NaN  
1  0.931854  
2       NaN

## plots von tmg verlauf nachbauen

In [2]:
verlauf = pd.read_excel(r"C:\Users\bvenn\OneDrive\Desktop\TMG Graphik.xlsx")
verlauf

20_mA     30_mA     40_mA     50_mA     60_mA     70_mA     80_mA  \
0    0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
1    0.000520  0.002236  0.003270  0.003492  0.003988  0.003658  0.003437   
2    0.000295  0.001931  0.003045  0.003284  0.004086  0.003511  0.003593   
3   -0.000094  0.001296  0.002376  0.002591  0.003767  0.002862  0.003419   
4   -0.000653  0.000340  0.001257  0.001401  0.003021  0.001687  0.002919   
..        ...       ...       ...       ...       ...       ...       ...   
995 -0.010347 -0.010413 -0.004649  0.001597  0.002891  0.005929  0.004153   
996 -0.004926 -0.004960 -0.002213  0.000744  0.001377  0.002819  0.001974   
997 -0.001939 -0.001954 -0.000871  0.000287  0.000543  0.001108  0.000776   
998 -0.000585 -0.000590 -0.000263  0.000085  0.000164  0.000334  0.000234   
999 -0.000118 -0.000119 -0.000053  0.000017  0.000033  0.000068  0.000047   

        90_mA    100_mA  
0    0.000000  0.000000  
1    0.003407  0.003223  
2    0.003363  0.003097  
3    0.002877  0.002588  
4    0.001936  0.001714  
..        ...       ...  
995  0.009029 -0.000809  
996  0.004286 -0.000427  
997  0.001683 -0.000182  
998  0.000507 -0.000059  
999  0.000102 -0.000013  

[1000 rows x 9 columns]

In [3]:
verlauf['index'] = verlauf.index
melted_verlauf = pd.melt(frame=verlauf, id_vars='index', var_name='ampere', value_name='value')
melted_verlauf

index  ampere     value
0         0   20_mA  0.000000
1         1   20_mA  0.000520
2         2   20_mA  0.000295
3         3   20_mA -0.000094
4         4   20_mA -0.000653
...     ...     ...       ...
8995    995  100_mA -0.000809
8996    996  100_mA -0.000427
8997    997  100_mA -0.000182
8998    998  100_mA -0.000059
8999    999  100_mA -0.000013

[9000 rows x 3 columns]

In [4]:
(
    ggplot(melted_verlauf, aes(x='index', y='value', color='ampere'))
    + geom_point(size=1.2)
    + xlab('Displacement [mm]')
)

In [5]:
(
    ggplot(melted_verlauf, aes(x='index', y='value'))
    + geom_point(size=1.2)
    + ylab('Displacement [mm]')
    + xlab('Time [ms]')
    + labs(title='Incremental TMG Protocol. 20 - 100 mA Stimulus')
)

In [18]:
(
    ggplot(verlauf.iloc[0:426], aes(x='index', y='90_mA'))
    + geom_point(size=1.8)
    + ylab('Displacement [mm]')
    + xlab('Time [ms]')
    + labs(title='TMG-Parameter Definition')
)